In [0]:
# # File location and type
# file_location = "/FileStore/tables/whole_corpus_sentence_merged_top_10_tiny_tsne.csv"
# file_type = "csv"

# # CSV options
# infer_schema = "false"
# first_row_is_header = "false"
# delimiter = ","

# # The applied options are for CSV files. For other file types, these will be ignored.
# df = spark.read.format(file_type) \
#   .option("inferSchema", infer_schema) \
#   .option("header", first_row_is_header) \
#   .option("sep", delimiter) \
#   .load(file_location)

# display(df)

In [0]:
dbutils.library.installPyPI("rake_nltk")
from rake_nltk import Rake, Metric

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 
with metrics_table as
(
select t.group, 
count(*) as num_posts, 
count(*)*1.0 / (select count(*) from `simplified_whole_sentences`) as ratio_num_posts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_trusts,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_delays,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_costs,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_errors,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_access
from `simplified_whole_sentences` as t
group by t.group
)
SELECT rank_table.group,
        num_posts,
        ROUND(num_post_rank / (select count(*) from metrics_table)*100,2) AS percentile_num_post,
        ROUND(ratio_trusts_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_trusts,
        ROUND(ratio_delays_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_delays,
        ROUND(ratio_costs_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_costs,
        ROUND(ratio_errors_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_errors,
        ROUND(ratio_access_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_access,
        ROUND(ratio_negative_trusts_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_trusts,
        ROUND(ratio_negative_delays_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_delays,
        ROUND(ratio_negative_costs_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_costs,
        ROUND(ratio_negative_errors_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_errors,
        ROUND(ratio_negative_access_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_access
from(
  select metrics_table.group,
           num_posts, 
           RANK() OVER(ORDER BY num_posts) AS num_post_rank,
           RANK() OVER(ORDER BY ratio_trusts) AS ratio_trusts_rank,
           RANK() OVER(ORDER BY ratio_delays) AS ratio_delays_rank,
           RANK() OVER(ORDER BY ratio_costs) AS ratio_costs_rank,
           RANK() OVER(ORDER BY ratio_errors) AS ratio_errors_rank,
           RANK() OVER(ORDER BY ratio_access) AS ratio_access_rank,
           RANK() OVER(ORDER BY ratio_negative_trusts) AS ratio_negative_trusts_rank,
           RANK() OVER(ORDER BY ratio_negative_delays) AS ratio_negative_delays_rank,
           RANK() OVER(ORDER BY ratio_negative_costs) AS ratio_negative_costs_rank,
           RANK() OVER(ORDER BY ratio_negative_errors) AS ratio_negative_errors_rank,
           RANK() OVER(ORDER BY ratio_negative_access) AS ratio_negative_access_rank
  from metrics_table
) as rank_table

group num_posts percentile_num_post percentile_ratio_trusts percentile_ratio_delays percentile_ratio_costs percentile_ratio_errors percentile_ratio_access percentile_ratio_negative_trusts percentile_ratio_negative_delays percentile_ratio_negative_costs percentile_ratio_negative_errors percentile_ratio_negative_access Warts_And_Verrucas 814 0.36 1.44 0.36 100.0 0.36 92.78 99.64 0.36 92.42 0.36 0.36 Folliculitis 883 0.72 11.55 28.88 97.11 76.17 45.85 89.89 1.08 98.92 59.21 66.79 Wolff_Parkinson_White_Syndrome 956 1.08 1.08 39.35 0.36 71.12 87.73 0.36 77.62 0.36 59.21 66.79 Trazodone 983 1.44 48.74 8.66 29.96 97.83 8.66 44.4 1.08 41.88 59.21 98.92 Spleen_Disorders_and_Splenectomy 1012 1.81 93.14 26.71 0.36 0.36 93.14 95.31 1.08 0.36 0.36 6.5 Finger_and_Hand_Problems 1042 2.17 88.45 91.34 4.69 68.95 5.78 18.05 28.16 98.92 59.21 0.36 Influenza 1341 2.53 1.81 17.69 11.91 52.71 2.89 0.36 1.08 41.88 59.21 0.36 Alzheimers_Disease 1390 2.89 20.94 5.42 50.54 0.36 42.24 44.4 1.08 96.03 0.36 98.92 ACE_Inhibitors 1390 2.89 85.56 15.88 11.19 50.18 2.53 14.8 1.08 41.88 59.21 98.92 Vitiligo 1400 3.61 0.72 0.36 91.34 0.36 98.19 0.36 0.36 2.17 0.36 23.47 Hepatitis 1431 3.97 52.35 53.43 96.75 85.92 99.28 97.83 11.91 94.58 59.21 45.49 Weight_Loss_and_Gain_Unintentional 1449 4.33 11.91 52.71 31.05 0.36 40.43 78.34 11.91 85.92 0.36 23.47 Topiramate 1524 4.69 98.56 4.69 77.62 44.77 35.38 81.95 1.08 41.88 59.21 0.36 Appendicitis 1603 5.05 9.39 47.29 21.3 99.64 83.39 98.56 96.75 85.92 59.21 23.47 Raynauds_Phenomenon 1662 5.42 73.65 37.55 20.94 38.99 92.42 83.75 18.05 8.3 59.21 89.17 Smoking 1732 5.78 4.69 3.61 1.81 37.18 1.44 2.89 1.08 1.44 59.21 0.36 Lumbar_Puncture 1736 6.14 41.52 67.51 50.9 94.58 93.86 98.56 28.16 21.3 59.21 82.31 Herpes_Non_Genital 1778 6.5 0.36 49.46 34.3 0.36 10.47 0.36 60.65 4.33 0.36 98.92 Coagulation_Disorders 1828 6.86 31.41 92.78 62.45 97.11 42.96 7.94 5.78 41.88 21.3 9.39 Investigations_and_Procedures 1831 7.22 93.5 88.45 81.95 89.53 76.53 94.22 51.99 4.33 59.21 23.47 Oesophageal_Cancer 1915 7.58 78.34 99.28 5.42 0.36 22.74 24.91 68.59 41.88 0.36 0.36 Rosacea 1939 7.94 3.97 9.39 79.42 33.21 9.39 2.89 96.75 15.52 59.21 0.36 Nail_Disorders 2170 8.3 46.57 29.24 80.14 66.06 63.9 14.8 89.17 85.92 59.21 23.47 Varicose_Vein 2239 8.66 79.42 83.03 98.56 64.62 98.92 22.38 87.36 7.58 59.21 6.5 Mastocytosis_and_Mast_Cell_Disorders 2254 9.03 74.37 63.18 19.86 90.61 44.04 44.4 7.22 4.33 59.21 96.75 Quetiapine 2312 9.39 33.21 2.53 0.36 83.39 28.16 89.89 1.08 0.36 59.21 0.36 Elbow_Problems 2313 9.75 40.43 91.7 9.39 0.36 79.42 2.53 89.17 85.92 0.36 0.36 Salivary_Gland_Disorders 2433 10.11 89.17 97.11 30.69 26.71 24.55 21.66 40.79 72.92 59.21 9.39 Candida_Genital 2574 10.47 2.17 18.41 81.59 56.32 80.14 99.64 40.79 29.96 59.21 23.47 Autistic_Spectrum_Disorders 2647 10.83 19.49 37.91 44.77 76.53 59.57 28.52 87.36 26.35 59.21 15.52 Pruritus_Ani 2659 11.19 19.13 1.44 23.1 54.15 59.21 87.0 100.0 98.19 59.21 15.52 Surgery_and_Anaesthetics 2742 11.55 99.28 71.12 96.03 23.83 99.64 44.4 96.03 72.92 7.94 54.15 Dental_Abscess 2793 11.91 58.84 90.61 98.92 49.82 41.88 6.86 94.95 95.67 59.21 66.79 Paroxetine_Hydrochloride 2862 12.27 25.27 9.75 5.78 0.36 16.25 83.75 1.08 98.92 0.36 95.31 Breast_Cancer_and_Screening 2890 12.64 60.29 87.36 39.71 92.42 51.99 5.78 83.03 67.51 59.21 50.9 Carbimazole 2906 13.0 50.9 67.15 10.11 47.29 62.82 25.63 51.99 98.92 59.21 37.55 Antibiotics 3111 13.36 49.1 59.21 25.27 43.68 57.04 96.03 24.55 85.92 59.21 95.31 Palsy_Non_Cerebral 3206 13.72 9.39 80.87 21.3 67.51 22.02 44.4 15.16 85.92 59.21 45.49 Child_Health 3236 14.08 26.71 60.29 14.08 0.36 31.77 3.97 77.62 21.3 0.36 23.47 Acne 3362 14.44 4.33 7.22 87.36 0.36 92.06 70.04 77.62 83.75 0.36 55.23 Pneumothorax 3408 14.8 28.52 84.48 19.49 18.41 40.07 85.56 68.59 41.88 59.21 94.58 Duloxetine 3416 15.16 79.78 3.97 52.35 0.36 29.96 84.48 1.08 72.92 0.36 90.61 Dementia 3444 15.52 74.01 23.1 43.68 77.62 79.78 77.26 11.91 3.97 59.21 90.61 Dihydrocodeine 3463 15.88 87.73 35.74 58.84 0

In [0]:

df = sqlContext.sql('''
with metrics_table as
(
select t.group, 
count(*) as num_posts, 
count(*)*1.0 / (select count(*) from `simplified_whole_sentences`) as ratio_num_posts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_trusts,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_delays,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_costs,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_errors,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_access
from `simplified_whole_sentences` as t
group by t.group
)
SELECT rank_table.group,
        num_posts,
        ROUND(num_post_rank / (select count(*) from metrics_table)*100,2) AS percentile_num_post,
        ROUND(ratio_trusts_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_trusts,
        ROUND(ratio_delays_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_delays,
        ROUND(ratio_costs_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_costs,
        ROUND(ratio_errors_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_errors,
        ROUND(ratio_access_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_access,
        ROUND(ratio_negative_trusts_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_trusts,
        ROUND(ratio_negative_delays_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_delays,
        ROUND(ratio_negative_costs_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_costs,
        ROUND(ratio_negative_errors_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_errors,
        ROUND(ratio_negative_access_rank / (select count(*) from metrics_table)*100,2) AS percentile_ratio_negative_access
from(
  select metrics_table.group,
           num_posts, 
           RANK() OVER(ORDER BY num_posts) AS num_post_rank,
           RANK() OVER(ORDER BY ratio_trusts) AS ratio_trusts_rank,
           RANK() OVER(ORDER BY ratio_delays) AS ratio_delays_rank,
           RANK() OVER(ORDER BY ratio_costs) AS ratio_costs_rank,
           RANK() OVER(ORDER BY ratio_errors) AS ratio_errors_rank,
           RANK() OVER(ORDER BY ratio_access) AS ratio_access_rank,
           RANK() OVER(ORDER BY ratio_negative_trusts) AS ratio_negative_trusts_rank,
           RANK() OVER(ORDER BY ratio_negative_delays) AS ratio_negative_delays_rank,
           RANK() OVER(ORDER BY ratio_negative_costs) AS ratio_negative_costs_rank,
           RANK() OVER(ORDER BY ratio_negative_errors) AS ratio_negative_errors_rank,
           RANK() OVER(ORDER BY ratio_negative_access) AS ratio_negative_access_rank
  from metrics_table
) as rank_table
''')

In [0]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt

query_disease_names = ["Menopause", "Atrophic_Vaginitis", "Menstrual_Cycle_and_Disorders", "Polycystic_Ovary_Syndrome", "Bacterial_Vaginosis"]

categories = ['Trusts','Delays','Costs', 'Errors', 'Access']
fig = make_subplots(rows=1, 
                    cols=len(query_disease_names), 
                    specs=[[{'type': 'polar'}]*len(query_disease_names)]*1,
                    subplot_titles=query_disease_names)
counter = 0
for row in df.collect():
  if row["group"] in query_disease_names:
    counter += 1
    fig.add_trace(go.Scatterpolar(
          r=[row["percentile_ratio_trusts"], 
             row["percentile_ratio_delays"], 
             row["percentile_ratio_costs"], 
             row["percentile_ratio_errors"], 
             row["percentile_ratio_access"]],
          theta=categories,
          name="Percentile of number of Topic Posts",
          marker = dict(color = "royalblue")),
          1, counter)
    
    fig.add_trace(go.Scatterpolar(
          r=[row["percentile_ratio_negative_trusts"], 
             row["percentile_ratio_negative_delays"], 
             row["percentile_ratio_negative_costs"], 
             row["percentile_ratio_negative_errors"], 
             row["percentile_ratio_negative_access"]],
          theta=categories,
          name='Percentile of number of Negative Posts in Topics',
          marker = dict(color = "palevioletred")), 
          1, counter)
    fig.update_traces(fill='toself')

fig.update_layout(title= "Fingerprint of Disease Groups \n [Blue: Percentile of Aspects Rate | Red: Percentile of Negative Ratio on Aspects]", 
                  template="plotly_dark", 
                  showlegend=False)
fig.show()

In [0]:
%sql
WITH tmp as
(
select beta_table.*, num_discussion_table.num_discussion
from `simplified_whole_sentences` as beta_table
join 
(select distinct substring_index(id,'-',3) as new_id, count(*) as num_discussion
from `simplified_whole_sentences` as t
group by substring_index(id,'-', 3)) as num_discussion_table on substring_index(id,'-',3) = substring_index(num_discussion_table.new_id,'-',3)
)
select tmp_rank.group, tmp_rank.trusts, tmp_rank.delays, tmp_rank.access,tmp_rank.errors,tmp_rank.costs,  tmp_rank.sentiment, tmp_rank.num_discussion, tmp_rank.text
from
  (
  select tmp.group, tmp.sentiment, tmp.trusts, tmp.delays, tmp.access,tmp.errors,tmp.costs, tmp.text, tmp.num_discussion,
  Rank() OVER(PARTITION BY tmp.group, tmp.trusts, tmp.sentiment order by tmp.num_discussion desc) as trusts_rank,
  Rank() OVER(PARTITION BY tmp.group, tmp.delays, tmp.sentiment order by tmp.num_discussion desc) as delays_rank,
  Rank() OVER(PARTITION BY tmp.group, tmp.access, tmp.sentiment order by tmp.num_discussion desc) as access_rank,
  Rank() OVER(PARTITION BY tmp.group, tmp.errors, tmp.sentiment order by tmp.num_discussion desc) as errors_rank,
  Rank() OVER(PARTITION BY tmp.group, tmp.costs, tmp.sentiment order by tmp.num_discussion desc) as costs_rank
  from tmp
  where (tmp.group = "Menopause" or 
       tmp.group = "Atrophic_Vaginitis" or 
       tmp.group = "Menstrual_Cycle_and_Disorders" or
       tmp.group = "Polycystic_Ovary_Syndrome" or
       tmp.group = "Bacterial_Vaginosis")
  ) as tmp_rank
where (tmp_rank.sentiment = 1 and ((tmp_rank.trusts_rank <= 20 and tmp_rank.trusts = 1) or 
                                   (tmp_rank.delays_rank <= 20 and tmp_rank.delays = 1)or 
                                   (tmp_rank.access_rank <= 20 and tmp_rank.access = 1)or 
                                   (tmp_rank.errors_rank <= 20 and tmp_rank.errors = 1)or 
                                   (tmp_rank.costs_rank <= 20 and tmp_rank.costs = 1))) or
       (tmp_rank.sentiment = 0 and ((tmp_rank.trusts_rank <= 10 and tmp_rank.trusts = 1) or 
                                   (tmp_rank.delays_rank <= 10 and tmp_rank.delays = 1) or 
                                   (tmp_rank.access_rank <= 10 and tmp_rank.access = 1) or 
                                   (tmp_rank.errors_rank <= 10 and tmp_rank.errors = 1) or 
                                   (tmp_rank.costs_rank <= 10 and tmp_rank.costs = 1)))
order by  tmp_rank.group,tmp_rank.trusts desc, tmp_rank.delays desc, tmp_rank.access desc,tmp_rank.errors desc,tmp_rank.costs desc, tmp_rank.sentiment desc, tmp_rank.num_discussion desc

group trusts delays access errors costs sentiment num_discussion text Atrophic_Vaginitis 1 0 0 0 0 1 44 The gynaecologist gave me lynocaine cream to numb the area , but that stung me and made me worse . Atrophic_Vaginitis 1 0 0 0 0 1 37 , because the pharmaceutical industry here is not interested in a nonpatentable medicine , no matter how safe and effective it is . Atrophic_Vaginitis 1 0 0 0 0 1 31 This doctor also feels the Mona Lisa laser treatment is a very harsh way to treat thinning skin , but that is a whole other topic . Atrophic_Vaginitis 1 0 0 0 0 1 30 I am not a doctor or medically qualified in any sense . Atrophic_Vaginitis 1 0 0 0 0 1 25 Some doctors do not believe in prescribing flagyl because they are so focused on the AV . Atrophic_Vaginitis 1 0 0 0 0 1 24 I ignored the pharmacist who told me I would be on them forever and not to use cortisone cream . Atrophic_Vaginitis 1 0 0 0 0 1 19 The worst for me was dealing with doctors that acted like my pain was not so bad . Atrophic_Vaginitis 1 0 0 0 0 1 19 I tend not to trust doctors when it comes to details . Atrophic_Vaginitis 1 0 0 0 0 1 14 doctortors are having to deal with these consequences and are not very well equipped . Atrophic_Vaginitis 1 0 0 0 0 1 14 I can not believe your urologist would be so unprofessional insensitive to make such a negative comment . Atrophic_Vaginitis 1 0 0 0 0 1 14 That doctor did not fully communicate that the tissue would just continue to get worse , only that it could . Atrophic_Vaginitis 1 0 0 0 0 1 13 The urologist accepted that little is known about why these symptoms appear and that they are not sure how to treat them . Atrophic_Vaginitis 1 0 0 0 0 1 12 I used clotramazole for a while and thought it was better but doctor was not happy with that . Atrophic_Vaginitis 1 0 0 0 0 1 12 I have found doctors to be not worth much and at this point seem to be doing my own prescribing . Atrophic_Vaginitis 1 0 0 0 0 1 12 Uterine fibroids were discovered several years into menopause , which did not concern me , but that doctor was concerned . Atrophic_Vaginitis 1 0 0 0 0 1 12 If so why has not an effective treatment been discovered ? I do not think there is much will on the part of the medical establishment though the drug companies could certainly make if it is that common . Atrophic_Vaginitis 1 0 0 0 0 1 11 My doctor at the time warned of possible future problems , but as doctors always are so pro medicine it sounded alarmist to me . Atrophic_Vaginitis 1 0 0 0 0 1 11 I do not trust HRT and its claims of not causing cancer in the cream form . Atrophic_Vaginitis 1 0 0 0 0 1 10 I had requested Flagyl ( metronidazole ) as it had worked for me in the past , but the doctor insisted there were no indications that it would be appropriate . Atrophic_Vaginitis 1 0 0 0 0 1 10 My doctor is very esteemed in her field and I trust her , however , I do believe that this laser treatment is not all it is talked up to be . Atrophic_Vaginitis 1 0 0 0 0 1 10 I called my GYN and was told by the nurse that the symptoms I had were unheard of and that I needed to see my primary care doctor . Atrophic_Vaginitis 1 0 0 0 0 0 43 The next option is physio- therapy from a specialist in this area . Atrophic_Vaginitis 1 0 0 0 0 0 43 Other drugs that can prove useful are antihistamines , Elmiron ( generic name , pentosan ) and even Viagra ( sildenafil ) , though exactly why these very different groups of medication are effective for this condition is not clear . Atrophic_Vaginitis 1 0 0 0 0 0 43 Other drugs that can prove useful are antihistamines , Elmiron ( generic name , pentosan ) and even Viagra ( sildenafil ) , though exactly why these very different groups of medication are effective for this condition is not clear . Atrophic_Vaginitis 1 0 0 0 0 0 43 The next option is physio- therapy from a specialist in this area . Atrophic_Vaginitis 1 0 0 0 0 0 43 Studies show that physiotherapists trained in pelvic soft tissue rehabilitation can be helpful . Atrophic_Vaginitis

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 
with metrics_table as
(
select t.group, 
count(*) as num_posts, 
count(*)*1.0 / (select count(*) from `simplified_whole_sentences`) as ratio_num_posts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_trusts,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_delays,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_costs,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_errors,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_access
from `simplified_whole_sentences` as t
group by t.group
)
-- num_post
SELECT num_post_table.group,
        cast(num_post_rank as decimal(20,0))*1.0 / (select count(*) from metrics_table) AS percentile_num_post,
        ratio_trusts_table.percentile_ratio_trust
from(
  select metrics_table.group,
           num_posts, 
           RANK() OVER(ORDER BY num_posts) AS num_post_rank
  from metrics_table
) as num_post_table INNER JOIN 
-- ratio_trusts_post
(
  SELECT ratio_trusts_rank_table.group,
         cast(ratio_trusts_rank as decimal(20,0))*1.0 / (select count(*) from metrics_table) AS percentile_ratio_trust
  from(
    select metrics_table.group,
             ratio_trusts, 
             RANK() OVER(ORDER BY ratio_trusts) AS ratio_trusts_rank
             RANK() OVER(ORDER BY ratio_delays) AS ratio_delays_rank
    from metrics_table
      ) as ratio_trusts_rank_table
) ratio_trusts_table ON num_post_table.group = ratio_trusts_table.group INNER JOIN
-- ratio_delays_post
(
  SELECT ratio_delays_rank_table.group,
         cast(ratio_delays_rank as decimal(20,0))*1.0 / (select count(*) from metrics_table) AS percentile_ratio_de
  from(
    select metrics_table.group,
             ratio_delays, 
             RANK() OVER(ORDER BY ratio_delays) AS ratio_delays_rank
    from metrics_table
      ) as ratio_delays_rank_table
) ratio_delays_table ON num_post_table.group = ratio_delays_table.group


group percentile_num_post percentile_ratio_trust Anticoagulants 0.2021660649819495 0.851985559566787 Spinal_Problems 0.8772563176895307 0.8989169675090253 Bartholins_Cyst 0.6317689530685922 0.4693140794223827 Gabapentin 0.7292418772563177 0.9061371841155235 Proton_Pump_Inhibitors 0.5379061371841155 0.5631768953068592 Trigeminal_Neuralgia 0.8411552346570397 0.8122743682310469 Warts_And_Verrucas 0.0036101083032491 0.0144404332129964 Hip_Replacement 0.9963898916967509 0.4945848375451264 Kidney_Failure_and_CKD 0.7833935018050542 0.4476534296028881 Neurological_Disorders 0.7797833935018051 0.444043321299639 Osteomyelitis 0.296028880866426 0.8808664259927798 Restless_Legs_Syndrome 0.4404332129963899 0.4765342960288809 Topiramate 0.0469314079422383 0.9855595667870036 Child_Health 0.1407942238267148 0.2671480144404332 Hyperthyroidism 0.9097472924187726 0.223826714801444 Lumbar_Puncture 0.0613718411552347 0.4151624548736462 Weight_Loss_and_Gain_Unintentional 0.0433212996389892 0.1191335740072202 Dementia 0.1552346570397112 0.740072202166065 Hysterectomy 0.8303249097472925 0.3862815884476534 Pain_and_Pain_Relief 0.5667870036101083 0.7003610108303249 Dermatitis_And_Eczema 0.5415162454873645 0.3285198555956679 Citalopram 0.9747292418772563 0.1263537906137184 Disc_Prolapse 0.8122743682310469 0.8050541516245487 Fibromyalgia_Syndrome 0.9530685920577617 0.4296028880866426 Olanzapine 0.371841155234657 0.9494584837545126 Penis_Disorders 0.8808664259927798 0.0613718411552347 Cystoscopy 0.2418772563176895 0.9530685920577617 Alopecia_and_Hair_Disorders 0.1913357400722022 0.2166064981949458 Vulval_Problems 0.4765342960288809 0.1516245487364621 Blood_Test_General 0.3357400722021661 0.6209386281588448 Headache 0.7472924187725632 0.2274368231046931 Angina 0.4620938628158845 0.9891696750902527 Candida_Genital 0.1046931407942238 0.0216606498194946 Hemifacial_Spasm 0.4296028880866426 0.924187725631769 Nail_Disorders 0.0830324909747292 0.4657039711191336 Finger_and_Hand_Problems 0.0216606498194946 0.8844765342960289 Cardiac_Arrhythmias 0.6028880866425993 0.6642599277978339 Cataract 0.92057761732852 0.5306859205776173 Dihydrocodeine 0.1588447653429603 0.8772563176895307 Irritable_Bowel_Syndrome 0.9277978339350181 0.1805054151624549 Tramadol 0.5306859205776173 0.9025270758122744 Fentanyl 0.4332129963898917 0.9169675090252708 Chatroom 0.7906137184115523 0.1624548736462094 Lupus 0.4043321299638989 0.4620938628158845 Hip_Dysplasia_and_Disorders 0.4512635379061372 0.8267148014440433 Chest_Pain 0.5054151624548736 0.6859205776173285 Smoking 0.0577617328519856 0.0469314079422383 Spleen_Disorders_and_Splenectomy 0.0180505415162455 0.9314079422382671 Bronchiectasis 0.7581227436823105 0.628158844765343 Cervical_Spondylosis 0.7364620938628159 0.6895306859205776 Haematological_Disorders 0.3249097472924188 0.5992779783393501 Sjogrens_Syndrome 0.815884476534296 0.6173285198555957 Steroids 0.2851985559566787 0.6245487364620939 ACE_Inhibitors 0.0288808664259928 0.855595667870036 Ear_Problems 0.6931407942238267 0.2382671480144404 Hidradenitis_Suppurativa 0.7111913357400722 0.5018050541516245 Methotrexate 0.2779783393501805 0.8628158844765343 Pityriasis_Rosea 0.51985559566787 0.0649819494584838 Pulmonary_Embolism 0.5956678700361011 0.6425992779783394 Osteoporosis_and_Osteopenia 0.6859205776173285 0.6823104693140793 Carpal_Tunnel 0.3862815884476534 0.7653429602888087 Lichen_Sclerosus 0.9494584837545126 0.5523465703971119 Orthopaedic_Disorders 0.259927797833935 0.9566787003610108 Polycythaemia_Rubra_Vera 0.6642599277978339 0.3429602888086643 Antibiotics 0.1335740072202166 0.4909747292418773 Henoch_Schonlein_Purpura 0.4548736462093863 0.815884476534296 Depression 0.9783393501805054 0.2346570397111913 Stroke_and_TIA 0.4007220216606498 0.7148014440433214 Abdominal_Disorders 0.9711191335740073 0.2202166064981949 Deep_Vein_Thrombosis 0.2635379061371841 0.7075812274368231 Rosacea 0.0794223826714801 0.0397111913357401 HRT_Hormone_Replacement_Therapy 0.6570397111913358 0.4548736462093

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 
with trust_metrics as
(
select t.group, 
round(LOG(count(*)), 2) as num_posts, 
count(*)*1.0 / (select count(*) from `simplified_whole_sentences`) as ratio_num_posts
from `simplified_whole_sentences` as t
group by t.group
)
select case when num_posts < 6.7+6.47/ 40 then 6.7+6.47/ 40 
            when num_posts < 6.7+ 2.0*6.47/ 40 then 6.7+ 2.0*6.47/ 40
            when num_posts < 6.7+ 3.0*6.47/ 40 then 6.7+ 3.0*6.47/ 40
            when num_posts < 6.7+ 4.0*6.47/ 40 then 6.7+ 4.0*6.47/ 40
            when num_posts < 6.7+ 5.0*6.47/ 40 then 6.7+ 5.0*6.47/ 40
            when num_posts < 6.7+ 6.0*6.47/ 40 then 6.7+ 6.0*6.47/ 40
            when num_posts < 6.7+ 7.0*6.47/ 40 then 6.7+ 7.0*6.47/ 40
            when num_posts < 6.7+ 8.0*6.47/ 40 then 6.7+ 8.0*6.47/ 40
            when num_posts < 6.7+ 9.0*6.47/ 40 then 6.7+ 9.0*6.47/ 40
            when num_posts < 6.7+ 10.0*6.47/ 40 then 6.7+ 10.0*6.47/ 40
            when num_posts < 6.7+ 11.0*6.47/ 40 then 6.7+ 11.0*6.47/ 40
            when num_posts < 6.7+ 12.0*6.47/ 40 then 6.7+ 12.0*6.47/ 40
            when num_posts < 6.7+ 13.0*6.47/ 40 then 6.7+ 13.0*6.47/ 40
            when num_posts < 6.7+ 14.0*6.47/ 40 then 6.7+ 14.0*6.47/ 40
            when num_posts < 6.7+ 15.0*6.47/ 40 then 6.7+ 15.0*6.47/ 40
            when num_posts < 6.7+ 16.0*6.47/ 40 then 6.7+ 16.0*6.47/ 40
            when num_posts < 6.7+ 17.0*6.47/ 40 then 6.7+ 17.0*6.47/ 40
            when num_posts < 6.7+ 18.0*6.47/ 40 then 6.7+ 18.0*6.47/ 40
            when num_posts < 6.7+ 19.0*6.47/ 40 then 6.7+ 19.0*6.47/ 40
            when num_posts < 6.7+ 20.0*6.47/ 40 then 6.7+ 20.0*6.47/ 40
	        when num_posts < 6.7+ 21*6.47/ 40 then 6.7+ 21*6.47/ 40 
            when num_posts < 6.7+ 22.0*6.47/ 40 then 6.7+ 22.0*6.47/ 40
            when num_posts < 6.7+ 23.0*6.47/ 40 then 6.7+ 23.0*6.47/ 40
            when num_posts < 6.7+ 24.0*6.47/ 40 then 6.7+ 24.0*6.47/ 40
            when num_posts < 6.7+ 25.0*6.47/ 40 then 6.7+ 25.0*6.47/ 40
            when num_posts < 6.7+ 26.0*6.47/ 40 then 6.7+ 26.0*6.47/ 40
            when num_posts < 6.7+ 27.0*6.47/ 40 then 6.7+ 27.0*6.47/ 40
            when num_posts < 6.7+ 28.0*6.47/ 40 then 6.7+ 28.0*6.47/ 40
            when num_posts < 6.7+ 29.0*6.47/ 40 then 6.7+ 29.0*6.47/ 40
            when num_posts < 6.7+ 30.0*6.47/ 40 then 6.7+ 30.0*6.47/ 40
            when num_posts < 6.7+ 31.0*6.47/ 40 then 6.7+ 31.0*6.47/ 40
            when num_posts < 6.7+ 32.0*6.47/ 40 then 6.7+ 32.0*6.47/ 40
            when num_posts < 6.7+ 33.0*6.47/ 40 then 6.7+ 33.0*6.47/ 40
            when num_posts < 6.7+ 34.0*6.47/ 40 then 6.7+ 34.0*6.47/ 40
            when num_posts < 6.7+ 35.0*6.47/ 40 then 6.7+ 35.0*6.47/ 40
            when num_posts < 6.7+ 36.0*6.47/ 40 then 6.7+ 36.0*6.47/ 40
            when num_posts < 6.7+ 37.0*6.47/ 40 then 6.7+ 37.0*6.47/ 40
            when num_posts < 6.7+ 38.0*6.47/ 40 then 6.7+ 38.0*6.47/ 40
            when num_posts < 6.7+ 39.0*6.47/ 40 then 6.7+ 39.0*6.47/ 40
            when num_posts <= 6.7+ 40.0*6.47/ 40 then 6.7+ 40.0*6.47/ 40 
            end as num_posts_range,
       count(*) as frequency
from
  (select trust_metrics.group,
           num_posts, 
           ratio_num_posts
  from trust_metrics) s
group by num_posts_range
order by num_posts_range

In [0]:
%sql

select beta_table.*, num_discussion_table.num_discussion
from `simplified_whole_sentences` as beta_table
join 
(select distinct substring_index(id,'-',3) as new_id, count(*) as num_discussion
from `simplified_whole_sentences` as t
group by substring_index(id,'-', 3)) as num_discussion_table on substring_index(id,'-',3) = substring_index(num_discussion_table.new_id,'-',3)

group id text access costs delays errors trusts sentiment num_discussion Abdominal_Disorders Abdominal_Disorders--40483-0-1 Actually whenever i eat or drink something i split it out with some bitter liquid . 0 0 0 0 0 0 9 Abdominal_Disorders Abdominal_Disorders--40483-0-2 l also have soar throat and the end portion of left side of my tongue is full of mouth sores . 0 0 0 0 0 1 9 Abdominal_Disorders Abdominal_Disorders--40483-0-3 i m also having mouth sores under my tongue . 0 0 0 0 0 1 9 Abdominal_Disorders Abdominal_Disorders--40483-0-4 I m also experiencing constipation , ucous in stool , ometimes very hard stool , ain on the left side of my abdomen . 0 0 0 0 0 0 9 Abdominal_Disorders Abdominal_Disorders--40483-0-5 I often feel a bubbling sensation in different part of my abdomen . 0 0 0 0 0 0 9 Abdominal_Disorders Abdominal_Disorders--40483-0-6 i often feel pain while passing stool . 0 0 0 0 0 1 9 Abdominal_Disorders Abdominal_Disorders--40483-0-7 These are the problems i am having . 0 0 0 0 0 1 9 Abdominal_Disorders Abdominal_Disorders--40483-0-8 Please tell me what is going on with me . 0 0 0 0 0 0 9 Abdominal_Disorders Abdominal_Disorders--40483-0-9 I will be very grateful . 0 0 0 0 0 0 9 Abdominal_Disorders Abdominal_Disorders--62971-1-1 There is no point worrying that you will get cancer , it is a never ending hamster wheel ride , I know . 0 0 0 0 0 0 14 Abdominal_Disorders Abdominal_Disorders--62971-0-1 I have only had it significantly for a relatively short time now get some problems after I eat but mainly at night when the acid comes back up my throat . 0 0 0 0 0 1 14 Abdominal_Disorders Abdominal_Disorders--62971-0-2 I now have aconstant mild sore throat and cough . 0 0 0 0 0 1 14 Abdominal_Disorders Abdominal_Disorders--62971-0-3 How on earth do you know what to take all the advice both fromdoctorand fellow sufferers is different . 0 0 0 0 0 0 14 Abdominal_Disorders Abdominal_Disorders--62971-0-4 I took omeprazole for a short while only three days but it did not agree with me bad stomach ache so I came off it had also had no effect in that time , probably not long enough . 0 0 0 0 0 1 14 Abdominal_Disorders Abdominal_Disorders--62971-0-5 But my gp says that if you ttakePPIs as soon as you come off them the problem returns . 0 0 0 0 0 1 14 Abdominal_Disorders Abdominal_Disorders--62971-0-6 Now taking advance gaviscon ( which bizarrely is peppermint flavour ) and if this does not help ( and it is not very much ) ranitidine which is also an acid suppressant but less powerful than PPIs . 0 0 0 0 0 1 14 Abdominal_Disorders Abdominal_Disorders--62971-0-7 which I have not tried yet as quite honestly I am worried about side effects etc . 0 0 0 0 0 1 14 Abdominal_Disorders Abdominal_Disorders--62971-0-8 I am on a strict diet have raised my bed somewhat by putting pillows under the mattress dont eat for 2-3 hrs before bedtime . 0 0 0 0 0 0 14 Abdominal_Disorders Abdominal_Disorders--62971-0-9 No alcohol caffeine etc . 0 0 0 0 0 0 14 Abdominal_Disorders Abdominal_Disorders--62971-0-10 Worried that I may get cancer . 0 0 0 0 0 1 14 Abdominal_Disorders Abdominal_Disorders--62971-0-11 . 0 0 0 0 0 0 14 Abdominal_Disorders Abdominal_Disorders--62971-2-1 particularly because I do not sleep very well in any case . 0 0 0 0 0 1 14 Abdominal_Disorders Abdominal_Disorders--62971-2-2 Keep waking up and cleaning my teeth ! 0 0 0 0 0 0 14 Abdominal_Disorders Abdominal_Disorders-124353-2-1 I am sorry to read that your going through a rough time , I two have been suffering very similar symptoms as you since October last year so for about 5 1 2 months , I have had endoscopy , colonoscopy blood tests stool tests and ultrasounds , all clear . 0 0 0 0 0 1 5 Abdominal_Disorders Abdominal_Disorders-124353-2-2 However I am still suffering , the only advise I can give going through it myself is try not to self diagnose . 0 0 0 0 0 1 5 Abdominal_Disorders Abdominal_Disorders-124353-2-3 it definitely causes more anxiety and worry which is not needed 

In [0]:
%sql
select t.group, 
sum(case when t.sentiment = 1 then 1 else 0 end) / count(*) as ratio_negative_general
from `simplified_whole_sentences` as t
group by t.group
order by ratio_negative_general


group ratio_negative_general Orlistat 0.1342381562099872 Polycythaemia_Rubra_Vera 0.14725189141076991 Cataract 0.15039286413332215 Prostate_Problems 0.1515531497529362 Blepharitis 0.15864759427828348 Prostate_Cancer 0.15941346395378045 Hallux_Valgus_Bunions 0.16538759298529065 Hip_Replacement 0.1679826213438136 Weight_Loss_Intentional 0.1702845100105374 Pulmonary_Fibrosis 0.17081050709369294 Alendronic_Acid 0.17192676547515257 Osteoporosis_and_Osteopenia 0.17359688652191724 Penis_Disorders 0.17604904161630117 Alternative_and_Complementary_Medicine 0.1768417908218513 Knee_Problems 0.1807045083260438 Diabetes 0.180805783919305 Tendon_Problems 0.18094846209237733 Glaucoma 0.18098958333333334 Granuloma_Annulare 0.18343509423944784 Vitiligo 0.18571428571428572 Polymyalgia_Rheumatica_and_GCA 0.18607378154375068 Lichen_Sclerosus 0.18793110167179766 Blood_Test_General 0.18935108153078203 Nail_Disorders 0.18986175115207374 Atrial_Fibrillation_And_Flutter 0.19030225856175859 Hyperthyroidism 0.19063973989101066 Aortic_Aneurysm_and_Dissection 0.19096979966111832 Haemochromatosis 0.1915940655415011 Kidney_Failure_and_CKD 0.19207708779443255 Chronic_Obstructive_Pulmonary_Disease 0.1943549335528637 Hydrocele 0.19509043927648578 Bronchiectasis 0.19511259446810142 Molluscum_Contagiosum 0.1976225854383358 Sex_Chromosome_Aneuploidies 0.19931327665140613 Hysterectomy 0.19951130116065974 Hypertension 0.2000064831923239 Gout_and_Pseudogout 0.20314327485380118 Breast_Cancer_and_Screening 0.20346020761245676 Alcohol_Consumption 0.20482768724308206 Restless_Legs_Syndrome 0.20635838150289018 Chatroom 0.20645138718818878 Benefits_and_Allowances 0.2076639237199582 Hemifacial_Spasm 0.2079699612403101 Ankle_Problems 0.20917613299243773 Lichen_Planus 0.21239612716322329 Cramps 0.21490422461296246 Genitourinary_Prolapse 0.2164822373171055 Menieres_Disease 0.21720924294650837 Mastocytosis_and_Mast_Cell_Disorders 0.21739130434782608 Folliculitis 0.217440543601359 ACE_Inhibitors 0.21942446043165467 Warts_And_Verrucas 0.2199017199017199 Rosacea 0.22021660649819494 Atrophic_Vaginitis 0.22021660649819494 Foot_and_Toe_Problems 0.22048619306112816 Wegeners_Granulomatosis 0.22055953155497723 Dermatology 0.22099753384669585 Alopecia_and_Hair_Disorders 0.2213072568193515 Dermatitis_And_Eczema 0.2215084264975805 Hypothyroidism 0.22220275242960547 Fungal_and_Yeast_Infections 0.22232953447942824 Diverticula 0.22250859106529208 Supraventricular_Tachycardia 0.22481228836433234 Osteoarthritis 0.22499092778516996 Oesophageal_Achalasia_and_Spasm 0.22512872552335852 Elbow_Problems 0.22524859489840035 Plantar_Fasciitis 0.2255053232525845 Liver_Problems 0.2263574590112836 Methotrexate 0.22734375 Barretts_Oesophagus 0.22746530314097882 Dietary_Nutrition_and_Exercise_Advice 0.22751405371642724 Pruritus_Ani 0.2279052275291463 Ankylosing_Spondylitis 0.22899066251667408 Pityriasis_Rosea 0.2301175184476633 Olanzapine 0.2302127659574468 Urethral_Disorders 0.23053995185142725 Pernicious_Anaemia 0.23113634080176831 Thyroid_and_Parathyroid_Disorders 0.23144024888671993 HRT_Hormone_Replacement_Therapy 0.2314772467413675 Herpes_Non_Genital 0.23172103487064116 Bacterial_Vaginosis 0.23195939086294418 Alzheimers_Disease 0.23237410071942446 Scabies 0.23336834733893558 Arthroscopy 0.23382104670793472 Acne 0.2340868530636526 Deep_Vein_Thrombosis 0.2340977068793619 Carpal_Tunnel 0.23411953899758778 Uterine_Fibroids 0.23432416281180143 Eye_Problems 0.23455029106750452 Anticoagulants 0.23660386591632004 Sexual_Health 0.23673222999144827 Postherpetic_Neuralgia 0.23742933650699197 Ulcerative_Colitis 0.23929113924050632 Urticarial_Rash 0.23968565815324164 Cystoscopy 0.239778534923339 Spleen_Disorders_and_Splenectomy 0.24011857707509882 Threadworm 0.2405300662582823 Tinnitus 0.24080107320812572 Abscess_Non_dental 0.24084778420038536 Wolff_Parkinson_White_Syndrome 0.24163179916317992 Rheumatoid_Arthritis 0.24164989939637826 Finger_and_Hand_Problems 0.2418426103646833 Smoking 0.24191685912240185 Haemorrhoi

In [0]:
%sql
/* Query the created temp table in a SQL cell */
with trusts as
(
select t.group, count(*) as num_posts, 
sum(case when t.trusts = 1 then 1 else 0 end) as num_trusts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_in_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_in_all_negative,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select trusts.group,
       num_posts, 
       num_trusts, 
       ratio_trusts,
       num_negative_trusts,
       ratio_negative_in_trusts,
       ratio_negative_trusts_in_all_negative,
       ratio_negative_trusts_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from trusts)) +
       (1.0 * ratio_trusts  / (select sum(ratio_trusts) from trusts)) + 
       (1.0 * ratio_negative_trusts_over_all / (select sum(ratio_negative_trusts_over_all) from trusts)) as composite_index
from trusts
order by composite_index 

group num_posts num_trusts ratio_trusts num_negative_trusts ratio_negative_in_trusts ratio_negative_trusts_over_all composite_index Surgery_and_Anaesthetics 2742 48 0.0175054704595186 24 0.5 0.0087527352297593 0.019148 Fluoroquinolone_Antibiotics 6675 97 0.0145318352059925 67 0.6907216494845361 0.0100374531835206 0.018899 Angina 9390 150 0.0159744408945687 85 0.5666666666666667 0.0090521831735889 0.018627 Topiramate 1524 23 0.0150918635170604 14 0.608695652173913 0.0091863517060367 0.018286 Upper_Gastrointestinal_Endoscopy 10377 190 0.0183097234268093 71 0.3736842105263158 0.0068420545437024 0.017519 Statins_and_Other_Lipid_lowering_Medicines 15127 211 0.013948568784293 128 0.6066350710900474 0.008461691016064 0.016869 Colonoscopy 16731 297 0.0177514792899408 109 0.367003367003367 0.0065148526686988 0.016857 Cervical_Smear_and_Disorders 5336 72 0.0134932533733133 42 0.5833333333333333 0.0078710644677661 0.015978 Pilonidal_Sinus 4255 60 0.0141010575793184 32 0.5333333333333333 0.0075205640423032 0.015933 Beta_blockers_others 4705 64 0.0136025504782147 36 0.5625 0.0076514346439957 0.0158

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000542	0.073411	0.072869
with trust_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.trusts = 1 then 1 else 0 end) as num_trusts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_in_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_in_all_negative,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 0.000542 + 1.0* 0.072869 / 20 then 0.000542 + 1.0* 0.072869 / 20
            when composite_index < 0.000542 + 2.0* 0.072869 / 20 then 0.000542 + 2.0* 0.072869 / 20
            when composite_index < 0.000542 + 3.0* 0.072869 / 20 then 0.000542 + 3.0* 0.072869 / 20
            when composite_index < 0.000542 + 4.0* 0.072869 / 20 then 0.000542 + 4.0* 0.072869 / 20
            when composite_index < 0.000542 + 5.0* 0.072869 / 20 then 0.000542 + 5.0* 0.072869 / 20
            when composite_index < 0.000542 + 6.0* 0.072869 / 20 then 0.000542 + 6.0* 0.072869 / 20
            when composite_index < 0.000542 + 7.0* 0.072869 / 20 then 0.000542 + 7.0* 0.072869 / 20
            when composite_index < 0.000542 + 8.0* 0.072869 / 20 then 0.000542 + 8.0* 0.072869 / 20
            when composite_index < 0.000542 + 9.0* 0.072869 / 20 then 0.000542 + 9.0* 0.072869 / 20
            when composite_index < 0.000542 + 10.0* 0.072869 / 20 then 0.000542 + 10.0* 0.072869 / 20
            when composite_index < 0.000542 + 11.0* 0.072869 / 20 then 0.000542 + 11.0* 0.072869 / 20
            when composite_index < 0.000542 + 12.0* 0.072869 / 20 then 0.000542 + 12.0* 0.072869 / 20
            when composite_index < 0.000542 + 13.0* 0.072869 / 20 then 0.000542 + 13.0* 0.072869 / 20
            when composite_index < 0.000542 + 14.0* 0.072869 / 20 then 0.000542 + 14.0* 0.072869 / 20
            when composite_index < 0.000542 + 15.0* 0.072869 / 20 then 0.000542 + 15.0* 0.072869 / 20
            when composite_index < 0.000542 + 16.0* 0.072869 / 20 then 0.000542 + 16.0* 0.072869 / 20
            when composite_index < 0.000542 + 17.0* 0.072869 / 20 then 0.000542 + 17.0* 0.072869 / 20
            when composite_index < 0.000542 + 18.0* 0.072869 / 20 then 0.000542 + 18.0* 0.072869 / 20
            when composite_index < 0.000542 + 19.0* 0.072869 / 20 then 0.000542 + 19.0* 0.072869 / 20
            when composite_index <= 0.000542 + 20.0* 0.072869 / 20 then 0.000542 + 20.0* 0.072869 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select trust_metrics.group,
         num_posts, 
         num_trusts, 
         ratio_trusts,
         num_negative_trusts,
         ratio_negative_in_trusts,
         ratio_negative_trusts_in_all_negative,
         ratio_negative_trusts_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (1.0 * num_posts / (select sum(num_posts) from trust_metrics)) +
         (1.0 * ratio_trusts  / (select sum(ratio_trusts) from trust_metrics)) + 
         (1.0 * ratio_negative_trusts_over_all / (select sum(ratio_negative_trusts_over_all) from trust_metrics)) as composite_index
  from trust_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.00418545 13 0.0078289 79 0.01147235 102 0.0151158 44 0.01875925 19 0.0224027 11 0.02604615 1 0.0296896 1 0.0369765 1 0.04061995 2 0.04790685 1 0.0515503 1 0.06248065 1 0.073411 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000542	0.073411	0.072869
with trust_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.trusts = 1 then 1 else 0 end) as num_trusts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_in_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_in_all_negative,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select trust_metrics.group,
       num_posts, 
       num_trusts, 
       ratio_trusts,
       num_negative_trusts,
       ratio_negative_in_trusts,
       ratio_negative_trusts_in_all_negative,
       ratio_negative_trusts_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (1.0 * num_posts / (select sum(num_posts) from trust_metrics)) +
       (1.0 * ratio_trusts  / (select sum(ratio_trusts) from trust_metrics)) + 
       (1.0 * ratio_negative_trusts_over_all / (select sum(ratio_negative_trusts_over_all) from trust_metrics)) as composite_index
from trust_metrics
order by composite_index desc

group num_posts num_trusts ratio_trusts num_negative_trusts ratio_negative_in_trusts ratio_negative_trusts_in_all_negative ratio_negative_trusts_over_all composite_index Anxiety_Disorders 526203 2321 0.0044108452441358 1070 0.4610081861266695 0.0020334357652845 0.0020334357652845 0.073411 Hip_Replacement 422127 2579 0.006109535755827 883 0.3423807677394339 0.0020917875426116 0.0020917875426116 0.060809 Menopause 342523 1268 0.0037019411835118 691 0.5449526813880126 0.0020173827742954 0.0020173827742954 0.048997 Polymyalgia_Rheumatica_and_GCA 312978 1799 0.0057480078471969 848 0.471372984991662 0.0027094556166887 0.0027094556166887 0.047014 Prostate_Problems 241638 2061 0.0085292876120478 754 0.3658418243571082 0.003120370140458 0.003120370140458 0.03967 Knee_Problems 250359 1192 0.0047611629699751 442 0.3708053691275168 0.0017654647925579 0.0017654647925579 0.037262 Depression 230756 1022 0.0044289205914472 484 0.4735812133072407 0.002097453587339 0.002097453587339 0.034877 Citalopram 186113 682 0.0036644404206047 308 0.4516129032258065 0.0016549085770473 0.0016549085770473 0.028141 Abdominal_Disorders 136553 598 0.0043792520120393 374 0.6254180602006689 0.0027388632984995 0.0027388632984995 0.023233 Gallbladder_Problems 110324 648 0.0058736086436315 308 0.4753086419753086 0.0027917769478989 0.0027917769478989 0.020686 Lichen_Sclerosus 102644 664 0.0064689606796306 326 0.4909638554216867 0.0031760258758427 0.0031760258758427 0.020428 Fibromyalgia_Syndrome 104012 603 0.0057974079913856 304 0.5041459369817579 0.0029227396838826 0.0029227396838826 0.019961 Angina 9390 150 0.0159744408945687 85 0.5666666666666667 0.0090521831735889 0.0090521831735889 0.019854 Fluoroquinolone_Antibiotics 6675 97 0.0145318352059925 67 0.6907216494845361 0.0100374531835206 0.0100374531835206 0.019771 Surgery_and_Anaesthetics 2742 48 0.0175054704595186 24 0.5 0.0087527352297593 0.0087527352297593 0.019506 Mirtazapine 94010 559 0.0059461759387299 340 0.6082289803220036 0.0036166365280289 0.0036166365280289 0.019488 Chronic_Fatigue_Syndrome 104500 535 0.0051196172248804 260 0.485981308411215 0.002488038277512 0.002488038277512 0.01918 Colonoscopy 16731 297 0.0177514792899408 109 0.367003367003367 0.0065148526686988 0.0065148526686988 0.019044 Upper_Gastrointestinal_Endoscopy 10377 190 0.0183097234268093 71 0.3736842105263158 0.0068420545437024 0.0068420545437024 0.018875 Statins_and_Other_Lipid_lowering_Medicines 15127 211 0.013948568784293 128 0.6066350710900474 0.008461691016064 0.008461691016064 0.018846 Topiramate 1524 23 0.0150918635170604 14 0.608695652173913 0.0091863517060367 0.0091863517060367 0.018485 Sertraline 107756 419 0.0038884145662423 208 0.4964200477326969 0.0019302869445785 0.0019302869445785 0.018321 Alcohol_Consumption 116039 368 0.003171347564181 150 0.4076086956521739 0.0012926688440955 0.0012926688440955 0.018317 Benzodiazepines_and_Z_Drugs 33566 390 0.0116189000774593 218 0.558974358974359 0.006494667222785 0.006494667222785 0.017838 Reflux_Oesophagitis 99149 403 0.0040645896579895 216 0.5359801488833748 0.002178539370039 0.002178539370039 0.017563 Ankle_Problems 92697 510 0.0055017961746335 202 0.396078431372549 0.0021791427985803 0.0021791427985803 0.017513 Vertigo_and_Dizziness 88940 494 0.0055543062738925 195 0.3947368421052632 0.0021924893186418 0.0021924893186418 0.017066 Cervical_Smear_and_Disorders 5336 72 0.0134932533733133 42 0.5833333333333333 0.0078710644677661 0.0078710644677661 0.016675 Hypothyroidism 74189 430 0.0057960074943725 258 0.6 0.0034776044966235 0.0034776044966235 0.016664 Pilonidal_Sinus 4255 60 0.0141010575793184 32 0.5333333333333333 0.0075205640423032 0.0075205640423032 0.016489 Cauda_Equina_Syndrome 6221 82 0.0131811605851149 48 0.5853658536585366 0.0077158013181161 0.0077158013181161 0.01645 Spinal_Problems 45897 456 0.009935289888228 210 0.4605263157894737 0.004575462448526 0.004575462448526 0.016441 Beta_blockers_others 4705 64 0.0136025504782147 36 0.5625 0.0076514346439957 0.0076514346439957 0.

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 
with trust_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.trusts = 1 then 1 else 0 end) as num_trusts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_in_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_in_all_negative,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 0.00031 + 0.018838 / 20 then 0.00031 + 0.018838 / 20 
            when composite_index < 0.00031 + 2.0* 0.018838 / 20 then 0.00031 + 2.0* 0.018838 / 20
            when composite_index < 0.00031 + 3.0* 0.018838 / 20 then 0.00031 + 3.0* 0.018838 / 20
            when composite_index < 0.00031 + 4.0* 0.018838 / 20 then 0.00031 + 4.0* 0.018838 / 20
            when composite_index < 0.00031 + 5.0* 0.018838 / 20 then 0.00031 + 5.0* 0.018838 / 20
            when composite_index < 0.00031 + 6.0* 0.018838 / 20 then 0.00031 + 6.0* 0.018838 / 20
            when composite_index < 0.00031 + 7.0* 0.018838 / 20 then 0.00031 + 7.0* 0.018838 / 20
            when composite_index < 0.00031 + 8.0* 0.018838 / 20 then 0.00031 + 8.0* 0.018838 / 20
            when composite_index < 0.00031 + 9.0* 0.018838 / 20 then 0.00031 + 9.0* 0.018838 / 20
            when composite_index < 0.00031 + 10.0* 0.018838 / 20 then 0.00031 + 10.0* 0.018838 / 20
            when composite_index < 0.00031 + 11.0* 0.018838 / 20 then 0.00031 + 11.0* 0.018838 / 20
            when composite_index < 0.00031 + 12.0* 0.018838 / 20 then 0.00031 + 12.0* 0.018838 / 20
            when composite_index < 0.00031 + 13.0* 0.018838 / 20 then 0.00031 + 13.0* 0.018838 / 20
            when composite_index < 0.00031 + 14.0* 0.018838 / 20 then 0.00031 + 14.0* 0.018838 / 20
            when composite_index < 0.00031 + 15.0* 0.018838 / 20 then 0.00031 + 15.0* 0.018838 / 20
            when composite_index < 0.00031 + 16.0* 0.018838 / 20 then 0.00031 + 16.0* 0.018838 / 20
            when composite_index < 0.00031 + 17.0* 0.018838 / 20 then 0.00031 + 17.0* 0.018838 / 20
            when composite_index < 0.00031 + 18.0* 0.018838 / 20 then 0.00031 + 18.0* 0.018838 / 20
            when composite_index < 0.00031 + 19.0* 0.018838 / 20 then 0.00031 + 19.0* 0.018838 / 20
            when composite_index <= 0.00031 + 20.0* 0.018838 / 20 then 0.00031 + 20.0* 0.018838 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select trust_metrics.group,
         num_posts, 
         num_trusts, 
         ratio_trusts,
         num_negative_trusts,
         ratio_negative_in_trusts,
         ratio_negative_trusts_in_all_negative,
         ratio_negative_trusts_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from trust_metrics)) +
         (1.0 * ratio_trusts  / (select sum(ratio_trusts) from trust_metrics)) + 
         (1.0 * ratio_negative_trusts_over_all / (select sum(ratio_negative_trusts_over_all) from trust_metrics)) as composite_index
  from trust_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.0012519 4 0.0021938 5 0.0031357 8 0.0040776 20 0.0050195 32 0.0059614 40 0.0069033 37 0.0078452 26 0.0087871 33 0.009729 26 0.0106709 12 0.0116128 11 0.0125547 5 0.0134966 4 0.0144385 2 0.0153804 1 0.0163223 4 0.0172642 2 0.0182061 1 0.019148 4

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000542	0.073411	0.072869
with trust_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.trusts = 1 then 1 else 0 end) as num_trusts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_in_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_in_all_negative,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select trust_metrics.group,
       num_posts, 
       num_trusts, 
       ratio_trusts,
       num_negative_trusts,
       ratio_negative_in_trusts,
       ratio_negative_trusts_in_all_negative,
       ratio_negative_trusts_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from trust_metrics)) +
       (1.0 * ratio_trusts  / (select sum(ratio_trusts) from trust_metrics)) + 
       (1.0 * ratio_negative_trusts_over_all / (select sum(ratio_negative_trusts_over_all) from trust_metrics)) as composite_index
from trust_metrics
order by composite_index desc

group num_posts num_trusts ratio_trusts num_negative_trusts ratio_negative_in_trusts ratio_negative_trusts_in_all_negative ratio_negative_trusts_over_all composite_index Surgery_and_Anaesthetics 2742 48 0.0175054704595186 24 0.5 0.0087527352297593 0.0087527352297593 0.019148 Fluoroquinolone_Antibiotics 6675 97 0.0145318352059925 67 0.6907216494845361 0.0100374531835206 0.0100374531835206 0.018899 Angina 9390 150 0.0159744408945687 85 0.5666666666666667 0.0090521831735889 0.0090521831735889 0.018627 Topiramate 1524 23 0.0150918635170604 14 0.608695652173913 0.0091863517060367 0.0091863517060367 0.018286 Upper_Gastrointestinal_Endoscopy 10377 190 0.0183097234268093 71 0.3736842105263158 0.0068420545437024 0.0068420545437024 0.017519 Statins_and_Other_Lipid_lowering_Medicines 15127 211 0.013948568784293 128 0.6066350710900474 0.008461691016064 0.008461691016064 0.016869 Colonoscopy 16731 297 0.0177514792899408 109 0.367003367003367 0.0065148526686988 0.0065148526686988 0.016857 Cervical_Smear_and_Disorders 5336 72 0.0134932533733133 42 0.5833333333333333 0.0078710644677661 0.0078710644677661 0.015978 Pilonidal_Sinus 4255 60 0.0141010575793184 32 0.5333333333333333 0.0075205640423032 0.0075205640423032 0.015933 Beta_blockers_others 4705 64 0.0136025504782147 36 0.5625 0.0076514346439957 0.0076514346439957 0.0158 Cauda_Equina_Syndrome 6221 82 0.0131811605851149 48 0.5853658536585366 0.0077158013181161 0.0077158013181161 0.015637 Spleen_Disorders_and_Splenectomy 1012 11 0.0108695652173913 8 0.7272727272727273 0.0079051383399209 0.0079051383399209 0.014567 Investigations_and_Procedures 1831 20 0.0109229929000546 14 0.7 0.0076460950300382 0.0076460950300382 0.014315 Olanzapine 7050 82 0.0116312056737589 51 0.6219512195121951 0.0072340425531915 0.0072340425531915 0.014259 Benzodiazepines_and_Z_Drugs 33566 390 0.0116189000774593 218 0.558974358974359 0.006494667222785 0.006494667222785 0.013451 Gabapentin 22579 225 0.0099650117365694 160 0.7111111111111111 0.0070862305682271 0.0070862305682271 0.01318 Angiotensin_II_Receptor_Blockers 3648 40 0.0109649122807018 23 0.575 0.0063048245614035 0.0063048245614035 0.012885 Orthopaedic_Disorders 4932 62 0.0125709651257097 27 0.4354838709677419 0.0054744525547445 0.0054744525547445 0.012871 Complex_Regional_Pain_Syndrome 12192 141 0.0115649606299213 69 0.4893617021276596 0.0056594488188976 0.0056594488188976 0.012517 Dihydrocodeine 3463 33 0.0095293098469535 23 0.696969696969697 0.0066416401963615 0.0066416401963615 0.012457 Fentanyl 8338 85 0.0101942911969297 49 0.5764705882352941 0.005876709042936 0.005876709042936 0.011995 Amlodipine 19529 201 0.0102923856828307 112 0.5572139303482587 0.0057350606789902 0.0057350606789902 0.011896 Chiari_Malformation 17184 184 0.010707635009311 93 0.5054347826086957 0.0054120111731844 0.0054120111731844 0.011775 Tramadol 11572 115 0.0099377808503284 65 0.5652173913043478 0.0056170065675769 0.0056170065675769 0.011573 Cervical_Rib_Syndrome 4138 55 0.013291445142581 16 0.2909090909090909 0.0038666022232963 0.0038666022232963 0.011525 Lyme_Disease 11216 105 0.0093616262482168 64 0.6095238095238095 0.0057061340941512 0.0057061340941512 0.011351 Osteomyelitis 5217 50 0.0095840521372436 29 0.58 0.0055587502396013 0.0055587502396013 0.011314 Hernia 29611 301 0.0101651413326129 150 0.4983388704318937 0.0050656850494749 0.0050656850494749 0.0111 Henoch_Schonlein_Purpura 8978 79 0.0087992871463578 50 0.6329113924050633 0.0055691690799733 0.0055691690799733 0.010893 Methotrexate 5120 48 0.009375 27 0.5625 0.0052734375 0.0052734375 0.010889 Ramipril 3706 35 0.0094441446303292 19 0.5428571428571429 0.0051268213707501 0.0051268213707501 0.010768 Levothyroxine_Sodium 9399 93 0.009894669645707 46 0.4946236559139785 0.0048941376742207 0.0048941376742207 0.010765 Cystoscopy 4696 58 0.012350936967632 17 0.2931034482758621 0.0036201022146508 0.0036201022146508 0.010739 Cushings_Syndrome 7882 70 0.0088809946714032 42 0.6 0.0053285968028419 0.0053285968028419 0.010677 Backache 1862

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 
with trust_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.trusts = 1 then 1 else 0 end) as num_trusts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_in_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_in_all_negative,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.01088 / 20 then 1.0* 0.01088 / 20 
            when composite_index < 2.0* 0.01088 / 20 then 2.0* 0.01088 / 20
            when composite_index < 3.0* 0.01088 / 20 then 3.0* 0.01088 / 20
            when composite_index < 4.0* 0.01088 / 20 then 4.0* 0.01088 / 20
            when composite_index < 5.0* 0.01088 / 20 then 5.0* 0.01088 / 20
            when composite_index < 6.0* 0.01088 / 20 then 6.0* 0.01088 / 20
            when composite_index < 7.0* 0.01088 / 20 then 7.0* 0.01088 / 20
            when composite_index < 8.0* 0.01088 / 20 then 8.0* 0.01088 / 20
            when composite_index < 9.0* 0.01088 / 20 then 9.0* 0.01088 / 20
            when composite_index < 10.0* 0.01088 / 20 then 10.0* 0.01088 / 20
            when composite_index < 11.0* 0.01088 / 20 then 11.0* 0.01088 / 20
            when composite_index < 12.0* 0.01088 / 20 then 12.0* 0.01088 / 20
            when composite_index < 13.0* 0.01088 / 20 then 13.0* 0.01088 / 20
            when composite_index < 14.0* 0.01088 / 20 then 14.0* 0.01088 / 20
            when composite_index < 15.0* 0.01088 / 20 then 15.0* 0.01088 / 20
            when composite_index < 16.0* 0.01088 / 20 then 16.0* 0.01088 / 20
            when composite_index < 17.0* 0.01088 / 20 then 17.0* 0.01088 / 20
            when composite_index < 18.0* 0.01088 / 20 then 18.0* 0.01088 / 20
            when composite_index < 19.0* 0.01088 / 20 then 19.0* 0.01088 / 20
            when composite_index <= 20.0* 0.01088 / 20 then 20.0* 0.01088 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select trust_metrics.group,
         num_posts, 
         num_trusts, 
         ratio_trusts,
         num_negative_trusts,
         ratio_negative_in_trusts,
         ratio_negative_trusts_in_all_negative,
         ratio_negative_trusts_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from trust_metrics)) +
         (1.0 * ratio_trusts  / (select sum(ratio_trusts) from trust_metrics)) + 
         (0.0 * ratio_negative_trusts_over_all / (select sum(ratio_negative_trusts_over_all) from trust_metrics)) as composite_index
  from trust_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 5.44E-4 2 0.001088 7 0.001632 12 0.002176 26 0.00272 40 0.003264 35 0.003808 42 0.004352 41 0.004896 22 0.00544 19 0.005984 11 0.006528 6 0.007072 2 0.007616 4 0.00816 3 0.008704 1 0.009248 1 0.009792 1 0.010336 2

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 
with trust_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.trusts = 1 then 1 else 0 end) as num_trusts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_in_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_in_all_negative,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.01088 / 20 then 1.0* 0.01088 / 20 
            when composite_index < 2.0* 0.01088 / 20 then 2.0* 0.01088 / 20
            when composite_index < 3.0* 0.01088 / 20 then 3.0* 0.01088 / 20
            when composite_index < 4.0* 0.01088 / 20 then 4.0* 0.01088 / 20
            when composite_index < 5.0* 0.01088 / 20 then 5.0* 0.01088 / 20
            when composite_index < 6.0* 0.01088 / 20 then 6.0* 0.01088 / 20
            when composite_index < 7.0* 0.01088 / 20 then 7.0* 0.01088 / 20
            when composite_index < 8.0* 0.01088 / 20 then 8.0* 0.01088 / 20
            when composite_index < 9.0* 0.01088 / 20 then 9.0* 0.01088 / 20
            when composite_index < 10.0* 0.01088 / 20 then 10.0* 0.01088 / 20
            when composite_index < 11.0* 0.01088 / 20 then 11.0* 0.01088 / 20
            when composite_index < 12.0* 0.01088 / 20 then 12.0* 0.01088 / 20
            when composite_index < 13.0* 0.01088 / 20 then 13.0* 0.01088 / 20
            when composite_index < 14.0* 0.01088 / 20 then 14.0* 0.01088 / 20
            when composite_index < 15.0* 0.01088 / 20 then 15.0* 0.01088 / 20
            when composite_index < 16.0* 0.01088 / 20 then 16.0* 0.01088 / 20
            when composite_index < 17.0* 0.01088 / 20 then 17.0* 0.01088 / 20
            when composite_index < 18.0* 0.01088 / 20 then 18.0* 0.01088 / 20
            when composite_index < 19.0* 0.01088 / 20 then 19.0* 0.01088 / 20
            when composite_index <= 20.0* 0.01088 / 20 then 20.0* 0.01088 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select trust_metrics.group,
         num_posts, 
         num_trusts, 
         ratio_trusts,
         num_negative_trusts,
         ratio_negative_in_trusts,
         ratio_negative_trusts_in_all_negative,
         ratio_negative_trusts_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from trust_metrics)) +
         (0.0 * ratio_trusts  / (select sum(ratio_trusts) from trust_metrics)) + 
         (1.0 * ratio_negative_trusts_over_all / (select sum(ratio_negative_trusts_over_all) from trust_metrics)) as composite_index
  from trust_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 5.44E-4 4 0.001088 5 0.001632 16 0.002176 28 0.00272 44 0.003264 40 0.003808 36 0.004352 30 0.004896 22 0.00544 16 0.005984 11 0.006528 7 0.007072 3 0.007616 2 0.00816 3 0.008704 5 0.009248 1 0.009792 1 0.010336 2 0.01088 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000542	0.073411	0.072869
with trust_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.trusts = 1 then 1 else 0 end) as num_trusts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as ratio_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.trusts = 1 then 1 else 0 end) as ratio_negative_in_trusts,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_in_all_negative,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_trusts_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select trust_metrics.group,
       num_posts, 
       num_trusts, 
       ratio_trusts,
       num_negative_trusts,
       ratio_negative_in_trusts,
       ratio_negative_trusts_in_all_negative,
       ratio_negative_trusts_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from trust_metrics)) +
       (0.0 * ratio_trusts  / (select sum(ratio_trusts) from trust_metrics)) + 
       (1.0 * ratio_negative_trusts_over_all / (select sum(ratio_negative_trusts_over_all) from trust_metrics)) as composite_index
from trust_metrics
order by composite_index desc

group num_posts num_trusts ratio_trusts num_negative_trusts ratio_negative_in_trusts ratio_negative_trusts_in_all_negative ratio_negative_trusts_over_all composite_index Fluoroquinolone_Antibiotics 6675 97 0.0145318352059925 67 0.6907216494845361 0.0100374531835206 0.0100374531835206 0.01088 Topiramate 1524 23 0.0150918635170604 14 0.608695652173913 0.0091863517060367 0.0091863517060367 0.009958 Angina 9390 150 0.0159744408945687 85 0.5666666666666667 0.0090521831735889 0.0090521831735889 0.009812 Surgery_and_Anaesthetics 2742 48 0.0175054704595186 24 0.5 0.0087527352297593 0.0087527352297593 0.009488 Statins_and_Other_Lipid_lowering_Medicines 15127 211 0.013948568784293 128 0.6066350710900474 0.008461691016064 0.008461691016064 0.009172 Spleen_Disorders_and_Splenectomy 1012 11 0.0108695652173913 8 0.7272727272727273 0.0079051383399209 0.0079051383399209 0.008569 Cervical_Smear_and_Disorders 5336 72 0.0134932533733133 42 0.5833333333333333 0.0078710644677661 0.0078710644677661 0.008532 Cauda_Equina_Syndrome 6221 82 0.0131811605851149 48 0.5853658536585366 0.0077158013181161 0.0077158013181161 0.008364 Beta_blockers_others 4705 64 0.0136025504782147 36 0.5625 0.0076514346439957 0.0076514346439957 0.008294 Investigations_and_Procedures 1831 20 0.0109229929000546 14 0.7 0.0076460950300382 0.0076460950300382 0.008288 Pilonidal_Sinus 4255 60 0.0141010575793184 32 0.5333333333333333 0.0075205640423032 0.0075205640423032 0.008152 Olanzapine 7050 82 0.0116312056737589 51 0.6219512195121951 0.0072340425531915 0.0072340425531915 0.007841 Gabapentin 22579 225 0.0099650117365694 160 0.7111111111111111 0.0070862305682271 0.0070862305682271 0.007681 Upper_Gastrointestinal_Endoscopy 10377 190 0.0183097234268093 71 0.3736842105263158 0.0068420545437024 0.0068420545437024 0.007416 Dihydrocodeine 3463 33 0.0095293098469535 23 0.696969696969697 0.0066416401963615 0.0066416401963615 0.007199 Colonoscopy 16731 297 0.0177514792899408 109 0.367003367003367 0.0065148526686988 0.0065148526686988 0.007062 Benzodiazepines_and_Z_Drugs 33566 390 0.0116189000774593 218 0.558974358974359 0.006494667222785 0.006494667222785 0.00704 Angiotensin_II_Receptor_Blockers 3648 40 0.0109649122807018 23 0.575 0.0063048245614035 0.0063048245614035 0.006834 Fentanyl 8338 85 0.0101942911969297 49 0.5764705882352941 0.005876709042936 0.005876709042936 0.00637 Amlodipine 19529 201 0.0102923856828307 112 0.5572139303482587 0.0057350606789902 0.0057350606789902 0.006217 Lyme_Disease 11216 105 0.0093616262482168 64 0.6095238095238095 0.0057061340941512 0.0057061340941512 0.006185 Complex_Regional_Pain_Syndrome 12192 141 0.0115649606299213 69 0.4893617021276596 0.0056594488188976 0.0056594488188976 0.006135 Tramadol 11572 115 0.0099377808503284 65 0.5652173913043478 0.0056170065675769 0.0056170065675769 0.006089 Henoch_Schonlein_Purpura 8978 79 0.0087992871463578 50 0.6329113924050633 0.0055691690799733 0.0055691690799733 0.006037 Osteomyelitis 5217 50 0.0095840521372436 29 0.58 0.0055587502396013 0.0055587502396013 0.006025 Orthopaedic_Disorders 4932 62 0.0125709651257097 27 0.4354838709677419 0.0054744525547445 0.0054744525547445 0.005934 Chiari_Malformation 17184 184 0.010707635009311 93 0.5054347826086957 0.0054120111731844 0.0054120111731844 0.005866 Idiopathic_Intracranial_Hypertension 3527 29 0.0082222852282393 19 0.6551724137931034 0.0053870144598809 0.0053870144598809 0.005839 Cushings_Syndrome 7882 70 0.0088809946714032 42 0.6 0.0053285968028419 0.0053285968028419 0.005776 Infectious_Disease 11338 91 0.00802610689716 60 0.6593406593406593 0.0052919386135121 0.0052919386135121 0.005736 Movement_Disorders 4734 33 0.0069708491761724 25 0.7575757575757576 0.0052809463455851 0.0052809463455851 0.005724 Methotrexate 5120 48 0.009375 27 0.5625 0.0052734375 0.0052734375 0.005716 Duloxetine 3416 29 0.0084894613583138 18 0.6206896551724138 0.0052693208430913 0.0052693208430913 0.005712 Ramipril 3706 35 0.0094441446303292 19 0.5428571428571429 0.0051268213707501 0.0051268213707

In [0]:
%sql
-- Statins_and_Other_Lipid_lowering_Medicines, Angina
select t.group, t.text
from `simplified_whole_sentences` as t
where t.trusts = 1 and t.sentiment = 1 and 
(t.group = 'Fluoroquinolone_Antibiotics' or 
 t.group = "Topiramate" or 
 t.group = "Angina" or 
 t.group = "Surgery_and_Anaesthetics" or 
 t.group="Statins_and_Other_Lipid_lowering_Medicines" or 
 t.group="Spleen_Disorders_and_Splenectomy" or 
 t.group = "Cervical_Smear_and_Disorders" or 
 t.group = "Cauda_Equina_Syndrome" or 
 t.group = "Beta_blockers_others" or 
 t.group = "Investigations_and_Procedures" or
 t.group = "Pilonidal_Sinus" or
 t.group = "Olanzapine" or
 t.group = "Gabapentin" or
 t.group = "Upper_Gastrointestinal_Endoscopy" or
 t.group = "Dihydrocodeine" or
 t.group = "Colonoscopy" or
 t.group = "Cervical_Rib_Syndrome" or
 t.group = "Orthopaedic_Disorders" or
 t.group = "Cystoscopy")
order by t.group

group text Angina Fumbling nurse kept driving the needle into the top bony part of my foot . Angina , I attended our emergency department due to my angina and breathlessness , the paramedics asked me why I was limping , I explained what I thought it was , they mentioned it to the triage nurse , she came out and had a chat and pulled up both my trouser legs , looked at both calf muscles , as I mentioned the left one was puffed up and it was slightly red and hot to the touch , triage nurse said to me that she was more concerned about my calf muscle than my chest pain this night , unfortunately I am Angina Another rare genetic condition and combined with what I know know to be prinzmetals angina , going to doctors who think you are either crazy or depressed instead of just listening to me . Angina I am trying very hard to give them away but it is very hard , I have tried everything with the exception of hypnotherapy and the one where they use needle like things , sorry I can not remember the name of that ancient alternative treatment , The reason I have not tried those 2 is because I do not believe in that kind of alternative treatment for smoking cesation , I have not found or heard of enough evidence to say that it indeed works , I have tried nicotine replacement therapy and as you know they Angina Had the best medical care all my life with great men and women , but medicine has changed and doctors while caring are not what I am used to . Angina The name of this drug is called amitriptyline , I do not know the statistics in regards to this drug and treatment of Prinzmetal but I can not take it as I suffer the nasty side effects from this drug . Angina doctortors receptionists can be very unhelpful and ask questions they are not entitled to . Angina this might be a case of never knowing because some doctors are ignorant to a lot of things , I am experiencing something completely different , medication related and I am having trouble convincing doctors that the new medication is the cause of my problem . Angina Last 3 weeks alone I was in our Emergency Department 3 times a week because my cardiologist had fiddled around with my medication , he in fact halved them all because he is starting to think it is neuropathic pain , My old cardiologist did warn me about being taken over by a new cardio , it turns out that my old cardio never retired so I go see him when I think the other one is carrying on a bit Last week my GP put me back on the full dosage rate again and now I have only had to visit the hospital Angina they were great but the doctor was far from professional , she made me endure my pain for well over an hour , he asked for my pain score on several occasions the first time it was fluctuating between 7-5 with the use of the GTN but crept back up to 7 every 10 -15 minutes , In the end when I was transferred around to another unit for a repeat blood test I had to ask one of the regular senior doctors for pain relief , he had no hesitations in giving me any , it must just be these young registrars that Angina Hi peter , I understand your frustrations completely , I am in the same boat , however most , and I say most doctors give me pain relief as there are the younger doctors that do not believe opiate based pain relievers are for cardiac pain , they are of the opinion that the GTN and the anti angina medication ( s ) will take care of the pain , now I am pretty sure you know that is not true , especially with prinzmetal angina ( coronary vasospasms ) . Angina Depending on which doctor I saw they all had different opinions on the troponin rise , 3 doctors were concerned but the consultant ( their boss ) made the decision that nothing was occurring , the other 2 said the rise was not cardiac related , I am scratching my head with these 2 doctors , troponin is a heart specific enzyme and is released when the heart is in distress or having a heart attack , I know there are other conditions that can raise troponins but everything

In [0]:
df = sqlContext.sql('''
select t.group, t.text
from `simplified_whole_sentences` as t
where t.trusts = 1 and t.sentiment = 1 and t.group = 'Surgery_and_Anaesthetics'
''')
f = df.select("text").collect()
text = ""
for each in f:
  text += each['text'] + " "
  
# r = Rake(ranking_metric=Metric.DEGREE_TO_FREQUENCY_RATIO)
# r = Rake(ranking_metric=Metric.WORD_DEGREE)
# r = Rake(ranking_metric=Metric.WORD_FREQUENCY)
r = Rake(min_length=1, max_length=5)
r.extract_keywords_from_text(text)
r.get_ranked_phrases()

Out[4]: ['anxiety whose anxiety levels went',
 'numerous blood tests stool samples',
 'terrible one 30 years ago',
 'sedation anaesthetist doctor n doctors',
 'myou sterilistation numerous times',
 'experienced various medical procedures',
 'take deep slow breaths',
 'somsome operations last year',
 'worst stomach cramps',
 'suspected autoimmune hepatitis',
 'seen 4 consultants',
 'keep getting sent',
 'feeling really frustrated',
 'doctors say without',
 'kept getting panicy',
 'always thought highly',
 'always left lateral',
 'take two biopsies',
 'nurses kept reassuring',
 'repeatledly saying ow',
 'last 3 years',
 'trust doctors whatsoever',
 'poor nurses hand',
 'sweat ws running',
 'overweight female suffering',
 'consultant gently inserted',
 'would ever imagined',
 'even exchanged one',
 'four nurses told',
 'doctor kept saying',
 'anything else done',
 'one bad experience',
 'flexible sigmoidoscopy procedure',
 'terrible sensation',
 'many years',
 'sedation would',
 'last time',
 'one woman',
 'initial one',
 'good doctors',
 'always advocate',
 'nurses told',
 'male nurses',
 'never trust',
 'flexible sigmoidoscopy',
 'done ever',
 'doctor says',
 'doctor believed',
 'doctor agreed',
 'undergo one',
 'poor nurse',
 'kept asking',
 'website shortly',
 'treatment fromantic',
 'totally mistrust',
 'terrterriable fear',
 'self conscious',
 'scope round',
 'rough handled',
 'rememeber gripping',
 'procedure worse',
 'procedure ended',
 'possibly liked',
 'patients position',
 'nightmare procedure',
 'much better',
 'means lying',
 'literally screamed',
 'ill fortune',
 'heart condition',
 'heart attack',
 'great experience',
 'get patients',
 'get around',
 'fabric touches',
 'even started',
 'even give',
 'complete collapse',
 'come across',
 'colonoscopy done',
 'colonoscopy aswell',
 'carefully trained',
 'big boobed',
 'awful experience',
 'would go',
 'nurse holding',
 'male nurse',
 'staff including',
 'nursing staff',
 'local hospital',
 'hospital said',
 'yes begging',
 'torture onto',
 'top bend',
 'tis point',
 'nearly yelling',
 'nails digging',
 'little air',
 'hurts even',
 'got told',
 'flat chest',
 'felt sick',
 'another consultant',
 'tests',
 'surgeon put',
 'doctors',
 'sedation',
 'doctor',
 'saying',
 'two',
 'told',
 'sweat',
 'sigmoidoscopy',
 'procedure',
 'female',
 'experience',
 'even',
 'done',
 'consultant',
 'bad',
 'anything',
 '3',
 'nurse',
 'staff',
 'hospital',
 'undergo',
 'torture',
 'surgeon',
 'put',
 'point',
 'nearly',
 'hurts',
 'got',
 'go',
 'felt',
 'digging',
 'chest',
 'bend',
 'begging',
 'asking',
 'another',
 'air',
 'wrote',
 'worth',
 'worried',
 'work',
 'wind',
 'whilst',
 'wear',
 'unlikely',
 'underwent',
 'understand',
 'undergear',
 'uncle',
 'unaware',
 'unable',
 'traumatised',
 'tip',
 'think',
 'thankfully',
 'sympathetic',
 'swearing',
 'surprised',
 'surgery',
 'submitted',
 'stop',
 'start',
 'stand',
 'since',
 'side',
 'sich',
 'shell',
 'seem',
 'rooth',
 'room',
 'research',
 'regardless',
 'refused',
 'refer',
 'realised',
 'read',
 'pumped',
 'prucolapride',
 'problems',
 'possible',
 'pillow',
 'performed',
 'people',
 'panicking',
 'painful',
 'pain',
 'others',
 'op',
 'ok',
 'numbness',
 'nothing',
 'nose',
 'nightmares',
 'nice',
 'negative',
 'needed',
 'mention',
 'men',
 'lovely',
 'lot',
 'lived',
 'like',
 'life',
 'lie',
 'knows',
 'interested',
 'instrument',
 'insisted',
 'inflict',
 'impression',
 'hopefully',
 'home',
 'help',
 'head',
 'hard',
 'happy',
 'hands',
 'gone',
 'found',
 'forcing',
 'forced',
 'fingernails',
 'fed',
 'fears',
 'fart',
 'far',
 'fan',
 'fact',
 'face',
 'eventually',
 'enough',
 'enema',
 'end',
 'encouraged',
 'embarrasing',
 'drenched',
 'dreadful',
 'distress',
 'discretion',
 'discharged',
 'description',
 'defend',
 'dedicated',
 'decided',
 'could',
 'cope',
 'comment',
 'colon',
 'colitis',
 'clinc',
 'change',
 'cause',
 'carry',
 'camera',
 'burried',
 'bridge',
 'bother',
 'boobs',
 'bob',
 'blown'

In [0]:
%sql
with delays as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select delays.group,
       num_posts, 
       num_delays, 
       ratio_delays,
       num_negative_delays,
       ratio_negative_in_delays,
       ratio_negative_delays_over_all,
       (0.0 * num_posts / (select sum(num_posts) from delays)) + 
       (1.0 * ratio_delays / (select sum(ratio_delays) from delays)) + 
       (1.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays)) as composite_index
from delays
order by composite_index desc
LIMIT 10

group num_posts num_delays ratio_delays num_negative_delays ratio_negative_in_delays ratio_negative_delays_over_all composite_index Disc_Prolapse 31536 449 0.0142376966007103 142 0.3162583518930958 0.0045027904616946 0.025278 Ovarian_Cyst 53101 839 0.0158000790945557 216 0.2574493444576877 0.004067720005273 0.025253 Oesophageal_Cancer 1915 26 0.0135770234986945 8 0.3076923076923077 0.004177545691906 0.023754 Cervical_Rib_Syndrome 4138 55 0.013291445142581 16 0.2909090909090909 0.0038666022232963 0.022583 Bowel_Cancer 9859 126 0.0127802008317274 32 0.253968253968254 0.0032457652905974 0.020292 Gallbladder_Problems 110324 1387 0.0125720604764149 363 0.2617159336697909 0.003290308545738 0.020256 Cholesteatoma 5918 76 0.0128421764109496 19 0.25 0.0032105441027374 0.020237 Pilonidal_Sinus 4255 48 0.0112808460634548 14 0.2916666666666667 0.0032902467685076 0.019192 Dental_Abscess 2793 24 0.0085929108485499 11 0.4583333333333333 0.0039384174722521 0.018932 Arthroscopy 3554 44 0.0123804164321891 10 0.2272727272727273 0.0028137310073157 0.018662

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000106	0.07251	0.072404
with delays_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_in_all_negative,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 0.000106 + 1.0* 0.072404 / 20 then 0.000106 + 1.0* 0.072404 / 20
            when composite_index < 0.000106 + 2.0* 0.072404 / 20 then 0.000106 + 2.0* 0.072404 / 20
            when composite_index < 0.000106 + 3.0* 0.072404 / 20 then 0.000106 + 3.0* 0.072404 / 20
            when composite_index < 0.000106 + 4.0* 0.072404 / 20 then 0.000106 + 4.0* 0.072404 / 20
            when composite_index < 0.000106 + 5.0* 0.072404 / 20 then 0.000106 + 5.0* 0.072404 / 20
            when composite_index < 0.000106 + 6.0* 0.072404 / 20 then 0.000106 + 6.0* 0.072404 / 20
            when composite_index < 0.000106 + 7.0* 0.072404 / 20 then 0.000106 + 7.0* 0.072404 / 20
            when composite_index < 0.000106 + 8.0* 0.072404 / 20 then 0.000106 + 8.0* 0.072404 / 20
            when composite_index < 0.000106 + 9.0* 0.072404 / 20 then 0.000106 + 9.0* 0.072404 / 20
            when composite_index < 0.000106 + 10.0* 0.072404 / 20 then 0.000106 + 10.0* 0.072404 / 20
            when composite_index < 0.000106 + 11.0* 0.072404 / 20 then 0.000106 + 11.0* 0.072404 / 20
            when composite_index < 0.000106 + 12.0* 0.072404/ 20 then 0.000106 + 12.0* 0.072404 / 20
            when composite_index < 0.000106 + 13.0* 0.072404 / 20 then 0.000106 + 13.0* 0.072404 / 20
            when composite_index < 0.000106 + 14.0* 0.072404 / 20 then 0.000106 + 14.0* 0.072404 / 20
            when composite_index < 0.000106 + 15.0* 0.072404 / 20 then 0.000106 + 15.0* 0.072404 / 20
            when composite_index < 0.000106 + 16.0* 0.072404 / 20 then 0.000106 + 16.0* 0.072404 / 20
            when composite_index < 0.000106 + 17.0* 0.072404 / 20 then 0.000106 + 17.0* 0.072404 / 20
            when composite_index < 0.000106 + 18.0* 0.072404 / 20 then 0.000106 + 18.0* 0.072404 / 20
            when composite_index < 0.000106 + 19.0* 0.072404 / 20 then 0.000106 + 19.0* 0.072404 / 20
            when composite_index <= 0.000106 + 20.0* 0.072404 / 20 then 0.000106 + 20.0* 0.072404 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select delays_metrics.group,
         num_posts, 
         num_delays, 
         ratio_delays,
         num_negative_delays,
         ratio_negative_in_delays,
         ratio_negative_delays_in_all_negative,
         ratio_negative_delays_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (1.0 * num_posts / (select sum(num_posts) from delays_metrics)) +
         (1.0 * ratio_delays  / (select sum(ratio_delays) from delays_metrics)) + 
         (1.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays_metrics)) as composite_index
  from delays_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.0037262 40 0.0073464 62 0.0109666 70 0.0145868 40 0.018207 36 0.0218272 13 0.0254474 3 0.0290676 3 0.0326878 2 0.036308 3 0.0435484 1 0.0471686 1 0.0507888 1 0.0688898 1 0.07251 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000106	0.07251	0.072404
with delays_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_in_all_negative,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select delays_metrics.group,
       num_posts, 
       num_delays, 
       ratio_delays,
       num_negative_delays,
       ratio_negative_in_delays,
       ratio_negative_delays_in_all_negative,
       ratio_negative_delays_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (1.0 * num_posts / (select sum(num_posts) from delays_metrics)) +
       (1.0 * ratio_delays  / (select sum(ratio_delays) from delays_metrics)) + 
       (1.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays_metrics)) as composite_index
from delays_metrics
order by composite_index desc

group num_posts num_delays ratio_delays num_negative_delays ratio_negative_in_delays ratio_negative_delays_in_all_negative ratio_negative_delays_over_all composite_index Anxiety_Disorders 526203 1039 0.001974523140309 369 0.3551491819056785 7.012502779346E-4 7.012502779346E-4 0.07251 Hip_Replacement 422127 3010 0.0071305554963317 713 0.2368770764119601 0.0016890651391643 0.0016890651391643 0.066126 Menopause 342523 530 0.0015473413464205 142 0.2679245283018868 4.145707003617E-4 4.145707003617E-4 0.047288 Polymyalgia_Rheumatica_and_GCA 312978 708 0.0022621398309146 196 0.2768361581920904 6.262421000837E-4 6.262421000837E-4 0.044653 Knee_Problems 250359 1632 0.0065186392340599 398 0.2438725490196078 0.0015897171661494 0.0015897171661494 0.042873 Prostate_Problems 241638 609 0.0025202989596007 118 0.19376026272578 4.883337885597E-4 4.883337885597E-4 0.035126 Gallbladder_Problems 110324 1387 0.0125720604764149 363 0.2617159336697909 0.003290308545738 0.003290308545738 0.034675 Depression 230756 331 0.0014344155731595 107 0.3232628398791541 4.636932517464E-4 4.636932517464E-4 0.032736 Ovarian_Cyst 53101 839 0.0158000790945557 216 0.2574493444576877 0.004067720005273 0.004067720005273 0.032193 Disc_Prolapse 31536 449 0.0142376966007103 142 0.3162583518930958 0.0045027904616946 0.0045027904616946 0.0294 Citalopram 186113 472 0.002536093663527 96 0.2033898305084746 5.158156603784E-4 5.158156603784E-4 0.027965 Abdominal_Disorders 136553 806 0.0059024701031834 215 0.2667493796526055 0.0015744802384422 0.0015744802384422 0.027446 Genitourinary_Prolapse 67867 752 0.0110804956753651 184 0.2446808510638298 0.0027111851120574 0.0027111851120574 0.026154 Ankle_Problems 92697 708 0.0076377876306677 189 0.2669491525423729 0.0020389009353053 0.0020389009353053 0.024541 Oesophageal_Cancer 1915 26 0.0135770234986945 8 0.3076923076923077 0.004177545691906 0.004177545691906 0.024004 Cervical_Rib_Syndrome 4138 55 0.013291445142581 16 0.2909090909090909 0.0038666022232963 0.0038666022232963 0.023124 Bowel_Cancer 9859 126 0.0127802008317274 32 0.253968253968254 0.0032457652905974 0.0032457652905974 0.021581 Cholesteatoma 5918 76 0.0128421764109496 19 0.25 0.0032105441027374 0.0032105441027374 0.02101 Reflux_Oesophagitis 99149 466 0.0046999969742509 125 0.2682403433476395 0.0012607288021059 0.0012607288021059 0.020624 Vertigo_and_Dizziness 88940 502 0.0056442545536317 120 0.2390438247011952 0.0013492241960872 0.0013492241960872 0.020332 Shoulder_Problems 21973 205 0.0093296318208711 71 0.3463414634146341 0.0032312383379602 0.0032312383379602 0.020281 Fibromyalgia_Syndrome 104012 421 0.0040476098911664 114 0.2707838479809976 0.001096027381456 0.001096027381456 0.020226 Pilonidal_Sinus 4255 48 0.0112808460634548 14 0.2916666666666667 0.0032902467685076 0.0032902467685076 0.019748 Dental_Abscess 2793 24 0.0085929108485499 11 0.4583333333333333 0.0039384174722521 0.0039384174722521 0.019297 Arthroscopy 3554 44 0.0123804164321891 10 0.2272727272727273 0.0028137310073157 0.0028137310073157 0.019126 Uterine_Fibroids 45181 393 0.0086983466501405 90 0.2290076335877863 0.0019919877824749 0.0019919877824749 0.019063 Lichen_Sclerosus 102644 337 0.0032831923931258 95 0.2818991097922849 9.25529012899E-4 9.25529012899E-4 0.018904 Genital_Herpes_Simplex 100631 373 0.0037066112828055 83 0.2225201072386059 8.247955401417E-4 8.247955401417E-4 0.018687 Salivary_Gland_Disorders 2433 28 0.011508425811755 7 0.25 0.0028771064529388 0.0028771064529388 0.018453 Chiari_Malformation 17184 164 0.0095437616387337 45 0.274390243902439 0.0026187150837989 0.0026187150837989 0.017986 Hip_Dysplasia_and_Disorders 8757 79 0.0090213543450954 27 0.3417721518987342 0.0030832476875642 0.0030832476875642 0.017855 Elbow_Problems 2313 20 0.0086467790747946 8 0.4 0.0034587116299179 0.0034587116299179 0.017834 Frozen_Shoulder 32057 249 0.0077674142932901 77 0.3092369477911647 0.0024019714882865 0.0024019714882865 0.017816 Chronic_Fatigue_Syndrome 104500 292 0.0027942583732057 64 0.2191780821917808 

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0	0.025278	0.025278
with delays_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_in_all_negative,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.025278 / 20 then 1.0* 0.025278 / 20 
            when composite_index < 2.0* 0.025278/ 20 then 2.0* 0.025278 / 20
            when composite_index < 3.0* 0.025278 / 20 then 3.0* 0.025278 / 20
            when composite_index < 4.0* 0.025278/ 20 then 4.0* 0.025278 / 20
            when composite_index < 5.0* 0.025278 / 20 then 5.0* 0.025278 / 20
            when composite_index < 6.0* 0.025278 / 20 then 6.0* 0.025278 / 20
            when composite_index < 7.0* 0.025278 / 20 then 7.0* 0.025278 / 20
            when composite_index < 8.0* 0.025278 / 20 then 8.0* 0.025278 / 20
            when composite_index < 9.0* 0.025278 / 20 then 9.0* 0.025278 / 20
            when composite_index < 10.0* 0.025278 / 20 then 10.0* 0.025278 / 20
            when composite_index < 11.0* 0.025278 / 20 then 11.0* 0.025278 / 20
            when composite_index < 12.0* 0.025278 / 20 then 12.0* 0.025278 / 20
            when composite_index < 13.0* 0.025278 / 20 then 13.0* 0.025278 / 20
            when composite_index < 14.0* 0.025278 / 20 then 14.0* 0.025278 / 20
            when composite_index < 15.0* 0.025278 / 20 then 15.0* 0.025278 / 20
            when composite_index < 16.0* 0.025278 / 20 then 16.0* 0.025278 / 20
            when composite_index < 17.0* 0.025278 / 20 then 17.0* 0.025278 / 20
            when composite_index < 18.0* 0.025278 / 20 then 18.0* 0.025278 / 20
            when composite_index < 19.0* 0.025278 / 20 then 19.0* 0.025278 / 20
            when composite_index <= 20.0* 0.025278 / 20 then 20.0* 0.025278 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select delays_metrics.group,
         num_posts, 
         num_delays, 
         ratio_delays,
         num_negative_delays,
         ratio_negative_in_delays,
         ratio_negative_delays_in_all_negative,
         ratio_negative_delays_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from delays_metrics)) +
         (1.0 * ratio_delays  / (select sum(ratio_delays) from delays_metrics)) + 
         (1.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays_metrics)) as composite_index
  from delays_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.0012639 23 0.0025278 34 0.0037917 27 0.0050556 20 0.0063195 36 0.0075834 25 0.0088473 22 0.0101112 21 0.0113751 21 0.012639 5 0.0139029 16 0.0151668 7 0.0164307 3 0.0176946 6 0.0189585 3 0.0202224 1 0.0214863 3 0.0227502 1 0.0240141 1 0.025278 2

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000106	0.07251	0.072404
with delays_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_in_all_negative,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select delays_metrics.group,
       num_posts, 
       num_delays, 
       ratio_delays,
       num_negative_delays,
       ratio_negative_in_delays,
       ratio_negative_delays_in_all_negative,
       ratio_negative_delays_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from delays_metrics)) +
       (1.0 * ratio_delays  / (select sum(ratio_delays) from delays_metrics)) + 
       (1.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays_metrics)) as composite_index
from delays_metrics
order by composite_index desc

group num_posts num_delays ratio_delays num_negative_delays ratio_negative_in_delays ratio_negative_delays_in_all_negative ratio_negative_delays_over_all composite_index Disc_Prolapse 31536 449 0.0142376966007103 142 0.3162583518930958 0.0045027904616946 0.0045027904616946 0.025278 Ovarian_Cyst 53101 839 0.0158000790945557 216 0.2574493444576877 0.004067720005273 0.004067720005273 0.025253 Oesophageal_Cancer 1915 26 0.0135770234986945 8 0.3076923076923077 0.004177545691906 0.004177545691906 0.023754 Cervical_Rib_Syndrome 4138 55 0.013291445142581 16 0.2909090909090909 0.0038666022232963 0.0038666022232963 0.022583 Bowel_Cancer 9859 126 0.0127802008317274 32 0.253968253968254 0.0032457652905974 0.0032457652905974 0.020292 Gallbladder_Problems 110324 1387 0.0125720604764149 363 0.2617159336697909 0.003290308545738 0.003290308545738 0.020256 Cholesteatoma 5918 76 0.0128421764109496 19 0.25 0.0032105441027374 0.0032105441027374 0.020237 Pilonidal_Sinus 4255 48 0.0112808460634548 14 0.2916666666666667 0.0032902467685076 0.0032902467685076 0.019192 Dental_Abscess 2793 24 0.0085929108485499 11 0.4583333333333333 0.0039384174722521 0.0039384174722521 0.018932 Arthroscopy 3554 44 0.0123804164321891 10 0.2272727272727273 0.0028137310073157 0.0028137310073157 0.018662 Salivary_Gland_Disorders 2433 28 0.011508425811755 7 0.25 0.0028771064529388 0.0028771064529388 0.018135 Elbow_Problems 2313 20 0.0086467790747946 8 0.4 0.0034587116299179 0.0034587116299179 0.017532 Shoulder_Problems 21973 205 0.0093296318208711 71 0.3463414634146341 0.0032312383379602 0.0032312383379602 0.017409 Genitourinary_Prolapse 67867 752 0.0110804956753651 184 0.2446808510638298 0.0027111851120574 0.0027111851120574 0.017284 Pituitary_Disorders 3970 39 0.009823677581864 12 0.3076923076923077 0.0030226700251889 0.0030226700251889 0.017188 Hip_Dysplasia_and_Disorders 8757 79 0.0090213543450954 27 0.3417721518987342 0.0030832476875642 0.0030832476875642 0.01671 Haematological_Disorders 5787 47 0.0081216519785727 19 0.4042553191489362 0.0032832210126145 0.0032832210126145 0.016571 Cushings_Syndrome 7882 74 0.0093884800811977 22 0.2972972972972973 0.0027911697538696 0.0027911697538696 0.016132 Chiari_Malformation 17184 164 0.0095437616387337 45 0.274390243902439 0.0026187150837989 0.0026187150837989 0.01574 Crohns_Disease 16784 142 0.0084604385128694 48 0.3380281690140845 0.0028598665395615 0.0028598665395615 0.015575 Abscess_Non_dental 5190 44 0.0084778420038536 14 0.3181818181818182 0.0026974951830443 0.0026974951830443 0.0151 Breast_Cancer_and_Screening 2890 23 0.0079584775086505 8 0.3478260869565217 0.0027681660899654 0.0027681660899654 0.014886 Multiple_Sclerosis 11629 101 0.0086851835927423 28 0.2772277227722772 0.0024077736692751 0.0024077736692751 0.014399 Accidents_and_Injuries 25889 222 0.0085750704932597 62 0.2792792792792793 0.0023948395071266 0.0023948395071266 0.014269 Idiopathic_Intracranial_Hypertension 3527 28 0.0079387581514035 9 0.3214285714285714 0.0025517436915225 0.0025517436915225 0.014218 Aortic_Aneurysm_and_Dissection 10033 88 0.0087710555167946 23 0.2613636363636364 0.0022924349646168 0.0022924349646168 0.014123 Varicose_Vein 2239 16 0.0071460473425636 6 0.375 0.0026797677534614 0.0026797677534614 0.013951 Sciatica 13788 126 0.0091383812010444 29 0.2301587301587302 0.0021032782129388 0.0021032782129388 0.013855 Foot_and_Toe_Problems 21185 176 0.0083077649280151 48 0.2727272727272727 0.0022657540712768 0.0022657540712768 0.01366 Frozen_Shoulder 32057 249 0.0077674142932901 77 0.3092369477911647 0.0024019714882865 0.0024019714882865 0.013626 Carpal_Tunnel 7462 68 0.0091128383811311 15 0.2205882352941176 0.0020101849370142 0.0020101849370142 0.013554 Bowel_Disorders 10766 81 0.0075236856771317 26 0.3209876543209877 0.0024150102173509 0.0024150102173509 0.013465 Pneumothorax 3408 26 0.0076291079812207 8 0.3076923076923077 0.0023474178403756 0.0023474178403756 0.013348 Investigations_and_Procedures 1831 15 0.008192244675041 4 0.2666666666666667 0.00

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0	0.01356	0.01356
with delays_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_in_all_negative,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.01356 / 20 then 1.0* 0.01356 / 20 
            when composite_index < 2.0* 0.01356 / 20 then 2.0* 0.01356 / 20
            when composite_index < 3.0* 0.01356 / 20 then 3.0* 0.01356 / 20
            when composite_index < 4.0* 0.01356/ 20 then 4.0* 0.01356 / 20
            when composite_index < 5.0* 0.01356 / 20 then 5.0* 0.01356 / 20
            when composite_index < 6.0* 0.01356 / 20 then 6.0* 0.01356 / 20
            when composite_index < 7.0* 0.01356 / 20 then 7.0* 0.01356 / 20
            when composite_index < 8.0* 0.01356 / 20 then 8.0* 0.01356 / 20
            when composite_index < 9.0* 0.01356 / 20 then 9.0* 0.01356 / 20
            when composite_index < 10.0* 0.01356 / 20 then 10.0* 0.01356 / 20
            when composite_index < 11.0* 0.01356 / 20 then 11.0* 0.01356 / 20
            when composite_index < 12.0* 0.01356 / 20 then 12.0* 0.01356 / 20
            when composite_index < 13.0* 0.01356 / 20 then 13.0* 0.01356 / 20
            when composite_index < 14.0* 0.01356 / 20 then 14.0* 0.01356 / 20
            when composite_index < 15.0* 0.01356 / 20 then 15.0* 0.01356 / 20
            when composite_index < 16.0* 0.01356 / 20 then 16.0* 0.01356 / 20
            when composite_index < 17.0* 0.01356 / 20 then 17.0* 0.01356 / 20
            when composite_index < 18.0* 0.01356 / 20 then 18.0* 0.01356 / 20
            when composite_index < 19.0* 0.01356 / 20 then 19.0* 0.01356 / 20
            when composite_index <= 20.0* 0.01356 / 20 then 20.0* 0.01356 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select delays_metrics.group,
         num_posts, 
         num_delays, 
         ratio_delays,
         num_negative_delays,
         ratio_negative_in_delays,
         ratio_negative_delays_in_all_negative,
         ratio_negative_delays_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from delays_metrics)) +
         (0.0 * ratio_delays  / (select sum(ratio_delays) from delays_metrics)) + 
         (1.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays_metrics)) as composite_index
  from delays_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 6.78E-4 33 0.001356 25 0.002034 35 0.002712 31 0.00339 31 0.004068 21 0.004746 22 0.005424 17 0.006102 15 0.00678 11 0.007458 11 0.008136 5 0.008814 6 0.009492 2 0.01017 6 0.010848 1 0.012204 2 0.012882 2 0.01356 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000106	0.07251	0.072404
with delays_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_in_all_negative,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select delays_metrics.group,
       num_posts, 
       num_delays, 
       ratio_delays,
       num_negative_delays,
       ratio_negative_in_delays,
       ratio_negative_delays_in_all_negative,
       ratio_negative_delays_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from delays_metrics)) +
       (0.0 * ratio_delays  / (select sum(ratio_delays) from delays_metrics)) + 
       (1.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays_metrics)) as composite_index
from delays_metrics
-- order by composite_index desc

group num_posts num_delays ratio_delays num_negative_delays ratio_negative_in_delays ratio_negative_delays_in_all_negative ratio_negative_delays_over_all composite_index Kidney_Failure_and_CKD 28020 83 0.0029621698786581 23 0.2771084337349398 8.208422555318E-4 8.208422555318E-4 0.002472 Kidney_Stones 13229 76 0.0057449542671404 19 0.25 0.0014362385667851 0.0014362385667851 0.004325 Kidney_Problems 8038 49 0.0060960437919881 13 0.2653061224489796 0.0016173177407315 0.0016173177407315 0.00487

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0	0.01356	0.01356
with delays_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_in_all_negative,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.01356 / 20 then 1.0* 0.01356 / 20 
            when composite_index < 2.0* 0.01356 / 20 then 2.0* 0.01356 / 20
            when composite_index < 3.0* 0.01356 / 20 then 3.0* 0.01356 / 20
            when composite_index < 4.0* 0.01356/ 20 then 4.0* 0.01356 / 20
            when composite_index < 5.0* 0.01356 / 20 then 5.0* 0.01356 / 20
            when composite_index < 6.0* 0.01356 / 20 then 6.0* 0.01356 / 20
            when composite_index < 7.0* 0.01356 / 20 then 7.0* 0.01356 / 20
            when composite_index < 8.0* 0.01356 / 20 then 8.0* 0.01356 / 20
            when composite_index < 9.0* 0.01356 / 20 then 9.0* 0.01356 / 20
            when composite_index < 10.0* 0.01356 / 20 then 10.0* 0.01356 / 20
            when composite_index < 11.0* 0.01356 / 20 then 11.0* 0.01356 / 20
            when composite_index < 12.0* 0.01356 / 20 then 12.0* 0.01356 / 20
            when composite_index < 13.0* 0.01356 / 20 then 13.0* 0.01356 / 20
            when composite_index < 14.0* 0.01356 / 20 then 14.0* 0.01356 / 20
            when composite_index < 15.0* 0.01356 / 20 then 15.0* 0.01356 / 20
            when composite_index < 16.0* 0.01356 / 20 then 16.0* 0.01356 / 20
            when composite_index < 17.0* 0.01356 / 20 then 17.0* 0.01356 / 20
            when composite_index < 18.0* 0.01356 / 20 then 18.0* 0.01356 / 20
            when composite_index < 19.0* 0.01356 / 20 then 19.0* 0.01356 / 20
            when composite_index <= 20.0* 0.01356 / 20 then 20.0* 0.01356 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select delays_metrics.group,
         num_posts, 
         num_delays, 
         ratio_delays,
         num_negative_delays,
         ratio_negative_in_delays,
         ratio_negative_delays_in_all_negative,
         ratio_negative_delays_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from delays_metrics)) +
         (1.0 * ratio_delays  / (select sum(ratio_delays) from delays_metrics)) + 
         (0.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays_metrics)) as composite_index
  from delays_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 6.78E-4 17 0.001356 43 0.002034 24 0.002712 31 0.00339 29 0.004068 32 0.004746 27 0.005424 16 0.006102 13 0.00678 13 0.007458 15 0.008136 6 0.009492 3 0.010848 4 0.011526 2 0.012204 1 0.01356 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000106	0.07251	0.072404
with delays_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.delays = 1 then 1 else 0 end) as num_delays,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as ratio_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.delays = 1 then 1 else 0 end) as ratio_negative_in_delays,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_in_all_negative,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_delays_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select delays_metrics.group,
       num_posts, 
       num_delays, 
       ratio_delays,
       num_negative_delays,
       ratio_negative_in_delays,
       ratio_negative_delays_in_all_negative,
       ratio_negative_delays_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from delays_metrics)) +
       (1.0 * ratio_delays  / (select sum(ratio_delays) from delays_metrics)) + 
       (0.0 * ratio_negative_delays_over_all / (select sum(ratio_negative_delays_over_all) from delays_metrics)) as composite_index
from delays_metrics
order by composite_index desc

group num_posts num_delays ratio_delays num_negative_delays ratio_negative_in_delays ratio_negative_delays_in_all_negative ratio_negative_delays_over_all composite_index Ovarian_Cyst 53101 839 0.0158000790945557 216 0.2574493444576877 0.004067720005273 0.004067720005273 0.013003 Disc_Prolapse 31536 449 0.0142376966007103 142 0.3162583518930958 0.0045027904616946 0.0045027904616946 0.011718 Oesophageal_Cancer 1915 26 0.0135770234986945 8 0.3076923076923077 0.004177545691906 0.004177545691906 0.011174 Cervical_Rib_Syndrome 4138 55 0.013291445142581 16 0.2909090909090909 0.0038666022232963 0.0038666022232963 0.010939 Cholesteatoma 5918 76 0.0128421764109496 19 0.25 0.0032105441027374 0.0032105441027374 0.010569 Bowel_Cancer 9859 126 0.0127802008317274 32 0.253968253968254 0.0032457652905974 0.0032457652905974 0.010518 Gallbladder_Problems 110324 1387 0.0125720604764149 363 0.2617159336697909 0.003290308545738 0.003290308545738 0.010347 Arthroscopy 3554 44 0.0123804164321891 10 0.2272727272727273 0.0028137310073157 0.0028137310073157 0.010189 Salivary_Gland_Disorders 2433 28 0.011508425811755 7 0.25 0.0028771064529388 0.0028771064529388 0.009471 Pilonidal_Sinus 4255 48 0.0112808460634548 14 0.2916666666666667 0.0032902467685076 0.0032902467685076 0.009284 Genitourinary_Prolapse 67867 752 0.0110804956753651 184 0.2446808510638298 0.0027111851120574 0.0027111851120574 0.009119 Pituitary_Disorders 3970 39 0.009823677581864 12 0.3076923076923077 0.0030226700251889 0.0030226700251889 0.008085 Chiari_Malformation 17184 164 0.0095437616387337 45 0.274390243902439 0.0026187150837989 0.0026187150837989 0.007854 Cushings_Syndrome 7882 74 0.0093884800811977 22 0.2972972972972973 0.0027911697538696 0.0027911697538696 0.007727 Shoulder_Problems 21973 205 0.0093296318208711 71 0.3463414634146341 0.0032312383379602 0.0032312383379602 0.007678 Sciatica 13788 126 0.0091383812010444 29 0.2301587301587302 0.0021032782129388 0.0021032782129388 0.007521 Carpal_Tunnel 7462 68 0.0091128383811311 15 0.2205882352941176 0.0020101849370142 0.0020101849370142 0.0075 Hip_Dysplasia_and_Disorders 8757 79 0.0090213543450954 27 0.3417721518987342 0.0030832476875642 0.0030832476875642 0.007425 Hernia 29611 261 0.0088142919860863 58 0.2222222222222222 0.0019587315524636 0.0019587315524636 0.007254 Aortic_Aneurysm_and_Dissection 10033 88 0.0087710555167946 23 0.2613636363636364 0.0022924349646168 0.0022924349646168 0.007219 Coagulation_Disorders 1828 16 0.0087527352297593 1 0.0625 5.4704595186E-4 5.4704595186E-4 0.007203 Uterine_Fibroids 45181 393 0.0086983466501405 90 0.2290076335877863 0.0019919877824749 0.0019919877824749 0.007159 Multiple_Sclerosis 11629 101 0.0086851835927423 28 0.2772277227722772 0.0024077736692751 0.0024077736692751 0.007148 Elbow_Problems 2313 20 0.0086467790747946 8 0.4 0.0034587116299179 0.0034587116299179 0.007116 Finger_and_Hand_Problems 1042 9 0.008637236084453 2 0.2222222222222222 0.0019193857965451 0.0019193857965451 0.007108 Hemifacial_Spasm 8256 71 0.0085998062015504 10 0.1408450704225352 0.0012112403100775 0.0012112403100775 0.007078 Dental_Abscess 2793 24 0.0085929108485499 11 0.4583333333333333 0.0039384174722521 0.0039384174722521 0.007072 Accidents_and_Injuries 25889 222 0.0085750704932597 62 0.2792792792792793 0.0023948395071266 0.0023948395071266 0.007057 Abscess_Non_dental 5190 44 0.0084778420038536 14 0.3181818181818182 0.0026974951830443 0.0026974951830443 0.006977 Crohns_Disease 16784 142 0.0084604385128694 48 0.3380281690140845 0.0028598665395615 0.0028598665395615 0.006963 Tendon_Problems 19442 162 0.0083324760827075 39 0.2407407407407407 0.0020059664643555 0.0020059664643555 0.006858 Foot_and_Toe_Problems 21185 176 0.0083077649280151 48 0.2727272727272727 0.0022657540712768 0.0022657540712768 0.006837 Investigations_and_Procedures 1831 15 0.008192244675041 4 0.2666666666666667 0.0021845985800109 0.0021845985800109 0.006742 Haematological_Disorders 5787 47 0.0081216519785727 19 0.4042553191489362 0.0032832210126145 0.00

In [0]:
%sql
-- Gallbladder_Problems, Disc_Prolapse 
select t.group, t.text
from `simplified_whole_sentences` as t
where t.delays = 1 and t.sentiment = 1 and 
(t.group = 'Ovarian_Cyst' or 
 t.group = "Disc_Prolapse" or 
 t.group = "Oesophageal_Cancer" or 
 t.group = "Cervical_Rib_Syndrome" or 
 t.group = "Bowel_Cancer" or 
 t.group = "Cholesteatoma" or 
 t.group = "Gallbladder_Problems" or 
 t.group = "Pruritus_Ani" or 
 t.group = "Dental_Abscess" or 
 t.group = "Salivary_Gland_Disorders" or
 t.group = "Pilonidal_Sinus" or
 t.group = "Genitourinary_Prolapse" or
 t.group = "Pituitary_Disorders" or
 t.group = "Chiari_Malformation" or
 t.group = "Cushings_Syndrome" or
 t.group = "Shoulder_Problems" or
 t.group = "Dental_Abscess" or
 t.group = "Elbow_Problems" or
 t.group = "Haematological_Disorders" or
 t.group = "Hip_Dysplasia_and_Disorders")
order by t.group

group text Bowel_Cancer Hi Amy I am sorry your going through a tough time ! I also have black spots in my stool I wonder what it is , I have a fecal occult test it came back negative for blood I am wondering if it was a false negative ? My symptoms seem to be getting worse that is what I find so worrying , I have recently developed shortness of breath I was given pain killers that are no longer working and all these other worrying symptoms but my doctor is happy for me to have waited 5 months to see the specialist and god Bowel_Cancer The extra couple of weeks that I had to wait for my surgery likely did not make a difference . Bowel_Cancer I went to the emergency department and they were not too concerned with my symptoms and told me to wait until my appointment in March . Bowel_Cancer please go see another doctor And I have a colonoscopy booked at 12 on Thursday really nervous but just want it to be done at the same time we keep u updated . Bowel_Cancer It s true that I feel I am getting the medical advice I need now but I do get worried that the longer I wait for appointments , the more I have to worry . Bowel_Cancer I have explained these symptoms over and over again , I really am at a loss with what to do next apart from wait for the colonoscopy . Bowel_Cancer Hi Dean I am going through something very similar to you and I am also 27 and a mother I have had rectal bleeding and a change in my bowel habits and also in the consistency severe abdominal pain that comes and goes I have been waiting since October for my specialist appointment which I go to on Monday , I am so scared that I have colon cancer and I will be leaving my little girl without a mum . Bowel_Cancer Scheduled for gastroscopy and colonoscopy this week and feeling petrified about what is going to be uncovered . Bowel_Cancer consultants do not even know until i have had tests ? ! ? I now think there is something wrong with the system and no wonder so many people are being diagnosed too late ! I now have to wait for appt . Bowel_Cancer Holiday greetings ! I am a 60 year old man , waiting for my colonoscopy on Wednesday and worrying . Bowel_Cancer After speaking with my GI doctor last Thursday he told me he would like to get an endoscopy done soon and told me his receptionist would call me back with an appointment but I never got a call back . Bowel_Cancer Hey I am going through the exact same thing slightly elevated CRP low iron and abdominal pain and even had the swollen lymph nodes ( and lots more symptoms ) Got a CT scan done last week for those still waiting on the results ( more worried it will show something messed up in my abdomen ) I have a colonoscopy booked for mid June just wondering if you ever got the results back of your biopsy ? I am only 21 and realize cancer would be rare but still a possibility I am freaking out . Bowel_Cancer How are you and how did you make out in colonoscopy ? I feel for you I am going through the same type of thing and waiting to see a gastroentologist I am SO scared it is consuming my thoughts everyday . Bowel_Cancer Do nt worry about the apparent delay in surgery as the rectal tumours are very slow growing . Bowel_Cancer It does concern me that you are still having to wait so long for the hospital appointment . Bowel_Cancer He s in panic and he is worried that the symptoms might be getting worse while waiting to see a specialist and get colonoscopy . Bowel_Cancer Lately , and I do not know whether it is because my husband is awaiting diagnosis of a condition or whether it is because I am awaiting my first CT scan but I have become very depressed . Bowel_Cancer Many people are scared to get a colonoscopy just like I was . Bowel_Cancer I saw my GI yesterday and asked for a colonoscopy but have to wait a month for a He thinks its highly unlikely that its cancer . Bowel_Cancer I have a follow up appointment a week from today , but I might have completely lost my mind from panic by then . Bowel_Cancer having had nearly 6 mont

In [0]:
df = sqlContext.sql('''
select t.group, t.text
from `simplified_whole_sentences` as t
where t.delays = 1 and t.sentiment = 1 and t.group = 'Ovarian_Cyst'
''')
f = df.select("text").collect()
text = ""
for each in f:
  text += each['text'] + " "
  
# r = Rake(ranking_metric=Metric.DEGREE_TO_FREQUENCY_RATIO)
# r = Rake(ranking_metric=Metric.WORD_DEGREE)
# r = Rake(ranking_metric=Metric.WORD_FREQUENCY)
r = Rake(min_length=1, max_length=4, ranking_metric=Metric.WORD_FREQUENCY)
r.extract_keywords_from_text(text)
r.get_ranked_phrases()

Out[10]: ['waiting another 5 weeks',
 'waiting 3 weeks',
 'waiting 2 weeks',
 '6 weeks waiting',
 'time im waiting',
 'whilst waiting fir surgery',
 'waiting yet another month',
 'waiting surgery',
 'scan 2 weeks ago',
 'getting pretty bad waiting',
 'wait another 22 weeks',
 'normal waiting time',
 'ended waiting 3 months',
 'waiting 3 months',
 '2 weeks time',
 'get another cyst',
 '12 week waiting list',
 'haemorragic cyst causing pain',
 'another 3 weeks',
 'long waiting list',
 'rescope still waiting',
 'im waiting',
 'still waiting',
 'waiting since feb',
 'nhs waiting list issues',
 'appointment within 4 weeks',
 'wait 5 weeks',
 'going crazy waiting',
 'results waiting',
 'much anguish waiting',
 'back pain etc',
 'another two weeks',
 'longer recovery time needed',
 'im going back today',
 'far longer recovery time',
 'waiting three years',
 'currently waiting tests',
 'cold could delay surgery',
 '2 weeks since',
 'mri waiting',
 'know waiting',
 'waiting times',
 'waiting 7 hours',
 'much quicker recovery time',
 'feb 2015 waiting',
 'dread another surgery',
 'back pain tender breasts',
 'another cyst',
 'worst stage waiting',
 'waiting around',
 'said 5 weeks',
 'pain even longer',
 'large dermoid cyst',
 'keep getting sharp pain',
 'would delay surgery',
 'waiting list',
 'open surgery due',
 'large ovarian cyst',
 'currently waiting',
 'remove 10cm dermoid cyst',
 'feel pain',
 'dermoid cyst removal',
 'wait another month',
 'stressful waiting',
 'emergency appointment next week',
 'waiting lists',
 'surgery since october 2016',
 'right side pain',
 'hell waiting',
 'done within weeks',
 'dermoid cyst growing',
 'anxiously waiting',
 '3 weeks',
 '2 weeks',
 'waiting',
 'ruptured ovarian cyst',
 'felt like every time',
 'doctor last year probably',
 '26cm dermoid cyst',
 'whole 6 weeks',
 'wait one week',
 'e last time',
 'dermoid cyst',
 'cyst may turn',
 'constant pain due',
 'around 8 weeks',
 '6cm ovarian cyst',
 'open surgery vs keyhole',
 'ct scan last thursday',
 'back feels like',
 'appointment next week',
 'surgery actually took',
 'results came back normal',
 'open surgery yesterday',
 'first surgery',
 'cyst ovary',
 'cyst may',
 'another doctor thought',
 'abdominal surgery seems horrible',
 '6 weeks',
 'surgery date following',
 'smaller left cyst',
 'six weeks ive',
 'shorter recovery time',
 'much pain',
 'large cyst',
 'doctor thinks im making',
 'average recovery time',
 'another scan',
 'another appointment',
 'took another week',
 'recovery time',
 'past three weeks',
 'ovarian pain',
 'outpatient appointment im',
 'open surgery',
 'need surgery',
 'formal results back yet',
 'awfully long time',
 'worrying time though whatever',
 'two weeks',
 'surgery date',
 'second surgery',
 'said results would',
 'results back yet',
 'long time',
 'last 3 days',
 'hopefully surgery without',
 'get appointment',
 'cyst removal',
 '6 month wait',
 'problem could get',
 'laproscopy pre op appointment',
 'key hole surgery',
 'get back',
 'feel like',
 'way 2 days ago',
 'cyst whole',
 'cyst gets',
 'could feel',
 '12 weeks',
 'surgery soon',
 'surgery managing',
 'still getting pains',
 'six weeks',
 'nearly 11 weeks',
 'much time',
 'im still awaiting',
 'horrid cyst',
 'hate surgery',
 'gps surgery',
 'functional cyst',
 'dermiod cyst',
 'cyst destroyed',
 'cyst cuz',
 'bone cyst',
 '7cm cyst',
 'wait long',
 'wait 2',
 'surgery slot',
 'stronger pain killers',
 'several weeks',
 'scan results',
 'pretty bad like',
 'pain levels rise massively',
 'pain free',
 'moved surgery',
 'long wait',
 'jabbing pain frequently',
 'heard anything back',
 'first time',
 'final year feeling like',
 'elective surgery',
 'cyst',
 'could get',
 'would like',
 'weeks',
 'test results would',
 'surgery',
 'pain killers',
 'pain comes',
 'jabbing pain',
 'feign immense pain',
 'abdomen ultrasound scan',
 '6 months though sounds',
 'still getting bloating',
 'said wait',
 'pain relief',
 'pain everyday',
 'pain built',
 'pain --

In [0]:
%sql
with costs as
(
select t.group, 1.0*count(t.text) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(t.text) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select costs.group,
       num_posts, 
       num_costs, 
       ratio_costs,
       num_negative_costs,
       ratio_negative_in_costs,
       ratio_negative_costs_over_all,
       (ratio_costs * 1.0 / (select sum(ratio_costs) from costs)) + (ratio_negative_costs_over_all * 1.0 / (select sum(ratio_negative_costs_over_all) from costs)) as composite_index
from costs
order by composite_index desc

group num_posts num_costs ratio_costs num_negative_costs ratio_negative_in_costs ratio_negative_costs_over_all composite_index Warts_And_Verrucas 814.0 10 0.0122850122850123 7 0.7 0.0085995085995086 0.032987 Folliculitis 883.0 7 0.0079275198187995 7 1.0 0.0079275198187995 0.026553 Dental_Abscess 2793.0 26 0.0093089867525958 19 0.7307692307692308 0.0068027210884354 0.02563 Atrophic_Vaginitis 23545.0 277 0.0117647058823529 110 0.3971119133574007 0.0046719048630282 0.023699 Hepatitis 1431.0 11 0.0076869322152341 8 0.7272727272727273 0.0055904961565339 0.021105 Lyme_Disease 11216.0 97 0.0086483594864479 50 0.5154639175257733 0.0044579172610556 0.019688 Cataract 71526.0 747 0.0104437547185639 212 0.2838018741633199 0.0029639571624304 0.018417 Cervical_Smear_and_Disorders 5336.0 39 0.0073088455772114 24 0.6153846153846154 0.0044977511244378 0.018256 Surgery_and_Anaesthetics 2742.0 20 0.0072939460247994 12 0.6 0.0043763676148796 0.01797 Sweating 4750.0 32 0.0067368421052632 19 0.59375 0.004 0.016505 Varicose_Vein 2239.0 20 0.0089325591782046 6 0.3 0.0026797677534614 0.016073 Backache 18628.0 119 0.0063882327678763 74 0.6218487394957983 0.0039725144943096 0.016048 Anticoagulants 4087.0 33 0.0080743821874235 12 0.3636363636363636 0.0029361389772449 0.015667 Nasal_Problems 7904.0 45 0.0056933198380567 31 0.6888888888888889 0.0039220647773279 0.015147 Eustachian_Tube_Dysfunction 21744.0 150 0.0068984547461369 71 0.4733333333333333 0.0032652685798381 0.015061 Prostate_Problems 241638.0 1933 0.0079995696041186 652 0.3372995344024832 0.0026982511028894 0.015055 Levothyroxine_Sodium 9399.0 58 0.0061708692414087 33 0.5689655172413793 0.003511011809767 0.014779 Oral_and_Dental_Problems 23008.0 141 0.0061283031988873 81 0.574468085106383 0.0035205146036161 0.014752 Disc_Prolapse 31536.0 202 0.0064053779807204 101 0.5 0.0032026889903602 0.014362 Rhinitis 4431.0 25 0.0056420672534417 15 0.6 0.003385240352065 0.0139 Sciatica 13788.0 82 0.0059472004641717 44 0.5365853658536585 0.0031911807368726 0.013817 Pain_and_Pain_Relief 13221.0 81 0.0061266167460858 38 0.4691358024691358 0.0028742152635958 0.013319 Prostate_Cancer 31848.0 215 0.0067508163777945 80 0.372093023255814 0.0025119316754584 0.013225 Acne 3362.0 17 0.0050565139797739 11 0.6470588235294118 0.0032718619869126 0.012984 Postherpetic_Neuralgia 13444.0 83 0.0061737578101755 34 0.4096385542168675 0.0025290092234454 0.012608 Statins_and_Other_Lipid_lowering_Medicines 15127.0 80 0.00528855688504 45 0.5625 0.002974813247835 0.01259 Glaucoma 3840.0 23 0.0059895833333333 10 0.4347826086956522 0.0026041666666667 0.012566 Osteoarthritis 33068.0 182 0.0055038103302286 94 0.5164835164835165 0.0028426273134148 0.012542 Spinal_Problems 45897.0 243 0.0052944636904373 128 0.5267489711934156 0.0027888533019587 0.012186 Vasectomy 3608.0 23 0.0063747228381375 8 0.3478260869565217 0.0022172949002217 0.012146 Scabies 5712.0 26 0.0045518207282913 18 0.6923076923076923 0.0031512605042017 0.012145 Complex_Regional_Pain_Syndrome 12192.0 60 0.0049212598425197 36 0.6 0.0029527559055118 0.012125 Psoriasis_and_Psoriatic_Arthritis 10695.0 54 0.0050490883590463 30 0.5555555555555556 0.002805049088359 0.011942 Hydrocele 4644.0 26 0.0055986218776916 11 0.4230769230769231 0.0023686477174849 0.0116 Urticarial_Rash 15779.0 79 0.0050066544140947 42 0.5316455696202532 0.0026617656378731 0.011577 Opiates_And_Opioids 12290.0 60 0.0048820179007323 33 0.55 0.0026851098454028 0.011487 Ramipril 3706.0 21 0.0056664867781975 8 0.380952380952381 0.0021586616297895 0.011212 Hemifacial_Spasm 8256.0 42 0.0050872093023256 20 0.4761904761904762 0.002422480620155 0.011138 Neuropathic_Pain 16060.0 77 0.0047945205479452 41 0.5324675324675325 0.0025529265255293 0.011095 Angiotensin_II_Receptor_Blockers 3648.0 16 0.0043859649122807 10 0.625 0.0027412280701754 0.011048 Nail_Disorders 2170.0 9 0.004147465437788 6 0.6666666666666667 0.0027649769585253 0.010831 Pernicious_Anaemia 19906.0 107 0.005375263739576 40 0.3738317757009346 0.002009444388626

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000125	0.072249	0.072124
with costs_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_in_all_negative,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 0.000125 + 1.0* 0.072124 / 20 then 0.000125 + 1.0* 0.072124 / 20 
            when composite_index < 0.000125 + 2.0* 0.072124 / 20 then 0.000125 + 2.0* 0.072124 / 20
            when composite_index < 0.000125 + 3.0* 0.072124 / 20 then 0.000125 + 3.0* 0.072124 / 20
            when composite_index < 0.000125 + 4.0* 0.072124/ 20 then 0.000125 + 4.0* 0.072124 / 20
            when composite_index < 0.000125 + 5.0* 0.072124 / 20 then 0.000125 + 5.0* 0.072124 / 20
            when composite_index < 0.000125 + 6.0* 0.072124 / 20 then 0.000125 + 6.0* 0.072124/ 20
            when composite_index < 0.000125 + 7.0* 0.072124 / 20 then 0.000125 + 7.0* 0.072124 / 20
            when composite_index < 0.000125 + 8.0* 0.072124 / 20 then 0.000125 + 8.0* 0.072124 / 20
            when composite_index < 0.000125 + 9.0* 0.072124/ 20 then 0.000125 + 9.0* 0.072124 / 20
            when composite_index < 0.000125 + 10.0* 0.072124 / 20 then 0.000125 + 10.0* 0.072124 / 20
            when composite_index < 0.000125 + 11.0* 0.072124 / 20 then 0.000125 + 11.0* 0.072124 / 20
            when composite_index < 0.000125 + 12.0* 0.072124 / 20 then 0.000125 + 12.0* 0.072124 / 20
            when composite_index < 0.000125 + 13.0* 0.072124 / 20 then 0.000125 + 13.0* 0.072124 / 20
            when composite_index < 0.000125 + 14.0* 0.072124 / 20 then 0.000125 + 14.0* 0.072124 / 20
            when composite_index < 0.000125 + 15.0* 0.072124 / 20 then 0.000125 + 15.0* 0.072124 / 20
            when composite_index < 0.000125 + 16.0* 0.072124 / 20 then 0.000125 + 16.0* 0.072124 / 20
            when composite_index < 0.000125 + 17.0* 0.072124 / 20 then 0.000125 + 17.0* 0.072124 / 20
            when composite_index < 0.000125 + 18.0* 0.072124 / 20 then 0.000125 + 18.0* 0.072124 / 20
            when composite_index < 0.000125 + 19.0* 0.072124 / 20 then 0.000125 + 19.0* 0.072124 / 20
            when composite_index <= 0.000125 + 20.0* 0.072124 / 20 then 0.000125 + 20.0* 0.072124 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select costs_metrics.group,
         num_posts, 
         num_costs, 
         ratio_costs,
         num_negative_costs,
         ratio_negative_in_costs,
         ratio_negative_costs_in_all_negative,
         ratio_negative_costs_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (1.0 * num_posts / (select sum(num_posts) from costs_metrics)) +
         (1.0 * ratio_costs  / (select sum(ratio_costs) from costs_metrics)) + 
         (1.0 * ratio_negative_costs_over_all / (select sum(ratio_negative_costs_over_all) from costs_metrics)) as composite_index
  from costs_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.0037312 21 0.0073374 70 0.0109436 92 0.0145498 47 0.018156 21 0.0217622 12 0.0253684 1 0.0289746 5 0.036187 2 0.0397932 1 0.0470056 1 0.0506118 2 0.0614304 1 0.072249 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000125	0.072249	0.072124
with costs_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_in_all_negative,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select costs_metrics.group,
       num_posts, 
       num_costs, 
       ratio_costs,
       num_negative_costs,
       ratio_negative_in_costs,
       ratio_negative_costs_in_all_negative,
       ratio_negative_costs_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (1.0 * num_posts / (select sum(num_posts) from costs_metrics)) +
       (1.0 * ratio_costs  / (select sum(ratio_costs) from costs_metrics)) + 
       (1.0 * ratio_negative_costs_over_all / (select sum(ratio_negative_costs_over_all) from costs_metrics)) as composite_index
from costs_metrics
order by composite_index desc

group num_posts num_costs ratio_costs num_negative_costs ratio_negative_in_costs ratio_negative_costs_in_all_negative ratio_negative_costs_over_all composite_index Anxiety_Disorders 526203 749 0.0014234050356992 442 0.5901201602136182 8.399800077157E-4 8.399800077157E-4 0.072249 Hip_Replacement 422127 791 0.0018738436536872 296 0.3742098609355247 7.012107730612E-4 7.012107730612E-4 0.058851 Menopause 342523 578 0.0016874779211907 312 0.5397923875432526 9.10887736006E-4 9.10887736006E-4 0.048699 Polymyalgia_Rheumatica_and_GCA 312978 963 0.0030768935835746 395 0.4101765316718588 0.001262069538434 0.001262069538434 0.047192 Prostate_Problems 241638 1933 0.0079995696041186 652 0.3372995344024832 0.0026982511028894 0.0026982511028894 0.046636 Knee_Problems 250359 492 0.0019651780043857 191 0.3882113821138211 7.629044691823E-4 7.629044691823E-4 0.036641 Warts_And_Verrucas 814 10 0.0122850122850123 7 0.7 0.0085995085995086 0.0085995085995086 0.033093 Depression 230756 269 0.0011657335020541 145 0.5390334572490706 6.283693598433E-4 6.283693598433E-4 0.032873 Cataract 71526 747 0.0104437547185639 212 0.2838018741633199 0.0029639571624304 0.0029639571624304 0.027765 Atrophic_Vaginitis 23545 277 0.0117647058823529 110 0.3971119133574007 0.0046719048630282 0.0046719048630282 0.026776 Folliculitis 883 7 0.0079275198187995 7 1.0 0.0079275198187995 0.0079275198187995 0.026668 Dental_Abscess 2793 26 0.0093089867525958 19 0.7307692307692308 0.0068027210884354 0.0068027210884354 0.025995 Citalopram 186113 126 6.770080542466E-4 73 0.5793650793650794 3.922348250794E-4 3.922348250794E-4 0.025962 Abdominal_Disorders 136553 340 0.0024898757259086 204 0.6 0.0014939254355452 0.0014939254355452 0.023981 Hepatitis 1431 11 0.0076869322152341 8 0.7272727272727273 0.0055904961565339 0.0055904961565339 0.021292 Lyme_Disease 11216 97 0.0086483594864479 50 0.5154639175257733 0.0044579172610556 0.0044579172610556 0.021154 Lichen_Sclerosus 102644 303 0.0029519504306146 146 0.4818481848184818 0.0014223919566658 0.0014223919566658 0.019916 Gallbladder_Problems 110324 254 0.0023023095609296 141 0.5551181102362205 0.001278053732642 0.001278053732642 0.019862 Alcohol_Consumption 116039 277 0.0023871284654297 104 0.3754512635379061 8.962503985729E-4 8.962503985729E-4 0.019861 Cervical_Smear_and_Disorders 5336 39 0.0073088455772114 24 0.6153846153846154 0.0044977511244378 0.0044977511244378 0.018953 Reflux_Oesophagitis 99149 260 0.0026223159083803 133 0.5115384615384615 0.0013414154454407 0.0013414154454407 0.018905 Fibromyalgia_Syndrome 104012 248 0.0023843402684306 119 0.4798387096774194 0.0011440987578356 0.0011440987578356 0.018833 Disc_Prolapse 31536 202 0.0064053779807204 101 0.5 0.0032026889903602 0.0032026889903602 0.018484 Backache 18628 119 0.0063882327678763 74 0.6218487394957983 0.0039725144943096 0.0039725144943096 0.018483 Surgery_and_Anaesthetics 2742 20 0.0072939460247994 12 0.6 0.0043763676148796 0.0043763676148796 0.018328 Spinal_Problems 45897 243 0.0052944636904373 128 0.5267489711934156 0.0027888533019587 0.0027888533019587 0.018185 Eustachian_Tube_Dysfunction 21744 150 0.0068984547461369 71 0.4733333333333333 0.0032652685798381 0.0032652685798381 0.017903 Genital_Herpes_Simplex 100631 191 0.0018980234718924 112 0.5863874345549738 0.0011129771144081 0.0011129771144081 0.017771 Oral_and_Dental_Problems 23008 141 0.0061283031988873 81 0.574468085106383 0.0035205146036161 0.0035205146036161 0.017759 Hypothyroidism 74189 266 0.0035854371941932 132 0.4962406015037594 0.0017792395099004 0.0017792395099004 0.017706 Prostate_Cancer 31848 215 0.0067508163777945 80 0.372093023255814 0.0025119316754584 0.0025119316754584 0.017387 Vertigo_and_Dizziness 88940 204 0.0022936811333483 123 0.6029411764705882 0.0013829548009894 0.0013829548009894 0.017289 Chronic_Fatigue_Syndrome 104500 157 0.0015023923444976 88 0.5605095541401274 8.421052631579E-4 8.421052631579E-4 0.017228 Sweating 4750 32 0.0067368421052632 19 0.59375 0.004 0.004 0.017126 Osteoarthritis 33068 18

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.0	0.032987	0.032987
with costs_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_in_all_negative,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.032987 / 20 then 1.0* 0.032987 / 20 
            when composite_index < 2.0* 0.032987 / 20 then 2.0* 0.032987 / 20
            when composite_index < 3.0* 0.032987 / 20 then 3.0* 0.032987 / 20
            when composite_index < 4.0* 0.032987/ 20 then 4.0* 0.032987 / 20
            when composite_index < 5.0* 0.032987 / 20 then 5.0* 0.032987 / 20
            when composite_index < 6.0* 0.032987 / 20 then 6.0* 0.032987 / 20
            when composite_index < 7.0* 0.032987 / 20 then 7.0* 0.032987 / 20
            when composite_index < 8.0* 0.032987 / 20 then 8.0* 0.032987 / 20
            when composite_index < 9.0* 0.032987 / 20 then 9.0* 0.032987 / 20
            when composite_index < 10.0* 0.032987 / 20 then 10.0* 0.032987 / 20
            when composite_index < 11.0* 0.032987 / 20 then 11.0* 0.032987 / 20
            when composite_index < 12.0* 0.032987 / 20 then 12.0* 0.032987 / 20
            when composite_index < 13.0* 0.032987 / 20 then 13.0* 0.032987 / 20
            when composite_index < 14.0* 0.032987 / 20 then 14.0* 0.032987 / 20
            when composite_index < 15.0* 0.032987 / 20 then 15.0* 0.032987 / 20
            when composite_index < 16.0* 0.032987 / 20 then 16.0* 0.032987 / 20
            when composite_index < 17.0* 0.032987 / 20 then 17.0* 0.032987 / 20
            when composite_index < 18.0* 0.032987 / 20 then 18.0* 0.032987 / 20
            when composite_index < 19.0* 0.032987 / 20 then 19.0* 0.032987 / 20
            when composite_index <= 20.0* 0.032987 / 20 then 20.0* 0.032987 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select costs_metrics.group,
         num_posts, 
         num_costs, 
         ratio_costs,
         num_negative_costs,
         ratio_negative_in_costs,
         ratio_negative_costs_in_all_negative,
         ratio_negative_costs_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from costs_metrics)) +
         (1.0 * ratio_costs  / (select sum(ratio_costs) from costs_metrics)) + 
         (1.0 * ratio_negative_costs_over_all / (select sum(ratio_negative_costs_over_all) from costs_metrics)) as composite_index
  from costs_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.00164935 8 0.0032987 24 0.00494805 60 0.0065974 54 0.00824675 51 0.0098961 30 0.01154545 15 0.0131948 12 0.01484415 7 0.0164935 6 0.01814285 2 0.0197922 3 0.02144155 1 0.02474025 1 0.0263896 1 0.02803895 1 0.032987 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000125	0.072249	0.072124
with costs_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_in_all_negative,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select costs_metrics.group,
       num_posts, 
       num_costs, 
       ratio_costs,
       num_negative_costs,
       ratio_negative_in_costs,
       ratio_negative_costs_in_all_negative,
       ratio_negative_costs_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from costs_metrics)) +
       (1.0 * ratio_costs  / (select sum(ratio_costs) from costs_metrics)) + 
       (1.0 * ratio_negative_costs_over_all / (select sum(ratio_negative_costs_over_all) from costs_metrics)) as composite_index
from costs_metrics
order by composite_index desc

group num_posts num_costs ratio_costs num_negative_costs ratio_negative_in_costs ratio_negative_costs_in_all_negative ratio_negative_costs_over_all composite_index Warts_And_Verrucas 814 10 0.0122850122850123 7 0.7 0.0085995085995086 0.0085995085995086 0.032987 Folliculitis 883 7 0.0079275198187995 7 1.0 0.0079275198187995 0.0079275198187995 0.026553 Dental_Abscess 2793 26 0.0093089867525958 19 0.7307692307692308 0.0068027210884354 0.0068027210884354 0.02563 Atrophic_Vaginitis 23545 277 0.0117647058823529 110 0.3971119133574007 0.0046719048630282 0.0046719048630282 0.023699 Hepatitis 1431 11 0.0076869322152341 8 0.7272727272727273 0.0055904961565339 0.0055904961565339 0.021105 Lyme_Disease 11216 97 0.0086483594864479 50 0.5154639175257733 0.0044579172610556 0.0044579172610556 0.019688 Cataract 71526 747 0.0104437547185639 212 0.2838018741633199 0.0029639571624304 0.0029639571624304 0.018417 Cervical_Smear_and_Disorders 5336 39 0.0073088455772114 24 0.6153846153846154 0.0044977511244378 0.0044977511244378 0.018256 Surgery_and_Anaesthetics 2742 20 0.0072939460247994 12 0.6 0.0043763676148796 0.0043763676148796 0.01797 Sweating 4750 32 0.0067368421052632 19 0.59375 0.004 0.004 0.016505 Varicose_Vein 2239 20 0.0089325591782046 6 0.3 0.0026797677534614 0.0026797677534614 0.016073 Backache 18628 119 0.0063882327678763 74 0.6218487394957983 0.0039725144943096 0.0039725144943096 0.016048 Anticoagulants 4087 33 0.0080743821874235 12 0.3636363636363636 0.0029361389772449 0.0029361389772449 0.015667 Nasal_Problems 7904 45 0.0056933198380567 31 0.6888888888888889 0.0039220647773279 0.0039220647773279 0.015147 Eustachian_Tube_Dysfunction 21744 150 0.0068984547461369 71 0.4733333333333333 0.0032652685798381 0.0032652685798381 0.015061 Prostate_Problems 241638 1933 0.0079995696041186 652 0.3372995344024832 0.0026982511028894 0.0026982511028894 0.015055 Levothyroxine_Sodium 9399 58 0.0061708692414087 33 0.5689655172413793 0.003511011809767 0.003511011809767 0.014779 Oral_and_Dental_Problems 23008 141 0.0061283031988873 81 0.574468085106383 0.0035205146036161 0.0035205146036161 0.014752 Disc_Prolapse 31536 202 0.0064053779807204 101 0.5 0.0032026889903602 0.0032026889903602 0.014362 Rhinitis 4431 25 0.0056420672534417 15 0.6 0.003385240352065 0.003385240352065 0.0139 Sciatica 13788 82 0.0059472004641717 44 0.5365853658536585 0.0031911807368726 0.0031911807368726 0.013817 Pain_and_Pain_Relief 13221 81 0.0061266167460858 38 0.4691358024691358 0.0028742152635958 0.0028742152635958 0.013319 Prostate_Cancer 31848 215 0.0067508163777945 80 0.372093023255814 0.0025119316754584 0.0025119316754584 0.013225 Acne 3362 17 0.0050565139797739 11 0.6470588235294118 0.0032718619869126 0.0032718619869126 0.012984 Postherpetic_Neuralgia 13444 83 0.0061737578101755 34 0.4096385542168675 0.0025290092234454 0.0025290092234454 0.012608 Statins_and_Other_Lipid_lowering_Medicines 15127 80 0.00528855688504 45 0.5625 0.002974813247835 0.002974813247835 0.01259 Glaucoma 3840 23 0.0059895833333333 10 0.4347826086956522 0.0026041666666667 0.0026041666666667 0.012566 Osteoarthritis 33068 182 0.0055038103302286 94 0.5164835164835165 0.0028426273134148 0.0028426273134148 0.012542 Spinal_Problems 45897 243 0.0052944636904373 128 0.5267489711934156 0.0027888533019587 0.0027888533019587 0.012186 Vasectomy 3608 23 0.0063747228381375 8 0.3478260869565217 0.0022172949002217 0.0022172949002217 0.012146 Scabies 5712 26 0.0045518207282913 18 0.6923076923076923 0.0031512605042017 0.0031512605042017 0.012145 Complex_Regional_Pain_Syndrome 12192 60 0.0049212598425197 36 0.6 0.0029527559055118 0.0029527559055118 0.012125 Psoriasis_and_Psoriatic_Arthritis 10695 54 0.0050490883590463 30 0.5555555555555556 0.002805049088359 0.002805049088359 0.011942 Hydrocele 4644 26 0.0055986218776916 11 0.4230769230769231 0.0023686477174849 0.0023686477174849 0.0116 Urticarial_Rash 15779 79 0.0050066544140947 42 0.5316455696202532 0.0026617656378731 0.0026617656378731 0.011577 Opiates_And_Opioids 12290 6

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.0	0.032987	0.032987
with costs_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_in_all_negative,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.019043 / 20 then 1.0* 0.019043 / 20 
            when composite_index < 2.0* 0.019043 / 20 then 2.0* 0.019043 / 20
            when composite_index < 3.0* 0.019043 / 20 then 3.0* 0.019043 / 20
            when composite_index < 4.0* 0.019043/ 20 then 4.0* 0.019043 / 20
            when composite_index < 5.0* 0.019043 / 20 then 5.0* 0.019043 / 20
            when composite_index < 6.0* 0.019043 / 20 then 6.0* 0.019043 / 20
            when composite_index < 7.0* 0.019043 / 20 then 7.0* 0.019043 / 20
            when composite_index < 8.0* 0.019043 / 20 then 8.0* 0.019043 / 20
            when composite_index < 9.0* 0.019043 / 20 then 9.0* 0.019043 / 20
            when composite_index < 10.0* 0.019043 / 20 then 10.0* 0.019043 / 20
            when composite_index < 11.0* 0.019043 / 20 then 11.0* 0.019043 / 20
            when composite_index < 12.0* 0.019043 / 20 then 12.0* 0.019043 / 20
            when composite_index < 13.0* 0.019043 / 20 then 13.0* 0.019043 / 20
            when composite_index < 14.0* 0.019043 / 20 then 14.0* 0.019043 / 20
            when composite_index < 15.0* 0.019043 / 20 then 15.0* 0.019043 / 20
            when composite_index < 16.0* 0.019043 / 20 then 16.0* 0.019043 / 20
            when composite_index < 17.0* 0.019043 / 20 then 17.0* 0.019043 / 20
            when composite_index < 18.0* 0.019043 / 20 then 18.0* 0.019043 / 20
            when composite_index < 19.0* 0.019043 / 20 then 19.0* 0.019043 / 20
            when composite_index <= 20.0* 0.019043 / 20 then 20.0* 0.019043 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select costs_metrics.group,
         num_posts, 
         num_costs, 
         ratio_costs,
         num_negative_costs,
         ratio_negative_in_costs,
         ratio_negative_costs_in_all_negative,
         ratio_negative_costs_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from costs_metrics)) +
         (0.0 * ratio_costs  / (select sum(ratio_costs) from costs_metrics)) + 
         (1.0 * ratio_negative_costs_over_all / (select sum(ratio_negative_costs_over_all) from costs_metrics)) as composite_index
  from costs_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 9.5215E-4 13 0.0019043 43 0.00285645 65 0.0038086 55 0.00476075 41 0.0057129 23 0.00666505 18 0.0076172 6 0.00856935 2 0.0095215 3 0.01047365 4 0.0133301 1 0.0152344 1 0.01809085 1 0.019043 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
with costs_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_in_all_negative,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)

select costs_metrics.group,
       num_posts, 
       num_costs, 
       ratio_costs,
       num_negative_costs,
       ratio_negative_in_costs,
       ratio_negative_costs_in_all_negative,
       ratio_negative_costs_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from costs_metrics)) +
       (0.0 * ratio_costs  / (select sum(ratio_costs) from costs_metrics)) + 
       (1.0 * ratio_negative_costs_over_all / (select sum(ratio_negative_costs_over_all) from costs_metrics)) as composite_index
from costs_metrics
order by composite_index desc

group num_posts num_costs ratio_costs num_negative_costs ratio_negative_in_costs ratio_negative_costs_in_all_negative ratio_negative_costs_over_all composite_index Warts_And_Verrucas 814 10 0.0122850122850123 7 0.7 0.0085995085995086 0.0085995085995086 0.019043 Folliculitis 883 7 0.0079275198187995 7 1.0 0.0079275198187995 0.0079275198187995 0.017555 Dental_Abscess 2793 26 0.0093089867525958 19 0.7307692307692308 0.0068027210884354 0.0068027210884354 0.015064 Hepatitis 1431 11 0.0076869322152341 8 0.7272727272727273 0.0055904961565339 0.0055904961565339 0.01238 Atrophic_Vaginitis 23545 277 0.0117647058823529 110 0.3971119133574007 0.0046719048630282 0.0046719048630282 0.010345 Cervical_Smear_and_Disorders 5336 39 0.0073088455772114 24 0.6153846153846154 0.0044977511244378 0.0044977511244378 0.00996 Lyme_Disease 11216 97 0.0086483594864479 50 0.5154639175257733 0.0044579172610556 0.0044579172610556 0.009872 Surgery_and_Anaesthetics 2742 20 0.0072939460247994 12 0.6 0.0043763676148796 0.0043763676148796 0.009691 Sweating 4750 32 0.0067368421052632 19 0.59375 0.004 0.004 0.008858 Backache 18628 119 0.0063882327678763 74 0.6218487394957983 0.0039725144943096 0.0039725144943096 0.008797 Nasal_Problems 7904 45 0.0056933198380567 31 0.6888888888888889 0.0039220647773279 0.0039220647773279 0.008685 Oral_and_Dental_Problems 23008 141 0.0061283031988873 81 0.574468085106383 0.0035205146036161 0.0035205146036161 0.007796 Levothyroxine_Sodium 9399 58 0.0061708692414087 33 0.5689655172413793 0.003511011809767 0.003511011809767 0.007775 Rhinitis 4431 25 0.0056420672534417 15 0.6 0.003385240352065 0.003385240352065 0.007496 Acne 3362 17 0.0050565139797739 11 0.6470588235294118 0.0032718619869126 0.0032718619869126 0.007245 Eustachian_Tube_Dysfunction 21744 150 0.0068984547461369 71 0.4733333333333333 0.0032652685798381 0.0032652685798381 0.007231 Disc_Prolapse 31536 202 0.0064053779807204 101 0.5 0.0032026889903602 0.0032026889903602 0.007092 Sciatica 13788 82 0.0059472004641717 44 0.5365853658536585 0.0031911807368726 0.0031911807368726 0.007067 Scabies 5712 26 0.0045518207282913 18 0.6923076923076923 0.0031512605042017 0.0031512605042017 0.006978 Statins_and_Other_Lipid_lowering_Medicines 15127 80 0.00528855688504 45 0.5625 0.002974813247835 0.002974813247835 0.006587 Cataract 71526 747 0.0104437547185639 212 0.2838018741633199 0.0029639571624304 0.0029639571624304 0.006563 Complex_Regional_Pain_Syndrome 12192 60 0.0049212598425197 36 0.6 0.0029527559055118 0.0029527559055118 0.006539 Anticoagulants 4087 33 0.0080743821874235 12 0.3636363636363636 0.0029361389772449 0.0029361389772449 0.006502 Pain_and_Pain_Relief 13221 81 0.0061266167460858 38 0.4691358024691358 0.0028742152635958 0.0028742152635958 0.006365 Osteoarthritis 33068 182 0.0055038103302286 94 0.5164835164835165 0.0028426273134148 0.0028426273134148 0.006295 Psoriasis_and_Psoriatic_Arthritis 10695 54 0.0050490883590463 30 0.5555555555555556 0.002805049088359 0.002805049088359 0.006211 Spinal_Problems 45897 243 0.0052944636904373 128 0.5267489711934156 0.0027888533019587 0.0027888533019587 0.006176 Granuloma_Annulare 7534 29 0.0038492168834616 21 0.7241379310344828 0.0027873639500929 0.0027873639500929 0.006172 Nail_Disorders 2170 9 0.004147465437788 6 0.6666666666666667 0.0027649769585253 0.0027649769585253 0.006123 Angiotensin_II_Receptor_Blockers 3648 16 0.0043859649122807 10 0.625 0.0027412280701754 0.0027412280701754 0.00607 Prostate_Problems 241638 1933 0.0079995696041186 652 0.3372995344024832 0.0026982511028894 0.0026982511028894 0.005975 Opiates_And_Opioids 12290 60 0.0048820179007323 33 0.55 0.0026851098454028 0.0026851098454028 0.005946 Varicose_Vein 2239 20 0.0089325591782046 6 0.3 0.0026797677534614 0.0026797677534614 0.005934 Urticarial_Rash 15779 79 0.0050066544140947 42 0.5316455696202532 0.0026617656378731 0.0026617656378731 0.005894 Glaucoma 3840 23 0.0059895833333333 10 0.4347826086956522 0.0026041666666667 0.0026041666666667 0.005767 Cystitis 6154 24 0.003899

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.0	0.032987	0.032987
with costs_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_in_all_negative,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.019043 / 20 then 1.0* 0.019043 / 20 
            when composite_index < 2.0* 0.019043 / 20 then 2.0* 0.019043 / 20
            when composite_index < 3.0* 0.019043 / 20 then 3.0* 0.019043 / 20
            when composite_index < 4.0* 0.019043/ 20 then 4.0* 0.019043 / 20
            when composite_index < 5.0* 0.019043 / 20 then 5.0* 0.019043 / 20
            when composite_index < 6.0* 0.019043 / 20 then 6.0* 0.019043 / 20
            when composite_index < 7.0* 0.019043 / 20 then 7.0* 0.019043 / 20
            when composite_index < 8.0* 0.019043 / 20 then 8.0* 0.019043 / 20
            when composite_index < 9.0* 0.019043 / 20 then 9.0* 0.019043 / 20
            when composite_index < 10.0* 0.019043 / 20 then 10.0* 0.019043 / 20
            when composite_index < 11.0* 0.019043 / 20 then 11.0* 0.019043 / 20
            when composite_index < 12.0* 0.019043 / 20 then 12.0* 0.019043 / 20
            when composite_index < 13.0* 0.019043 / 20 then 13.0* 0.019043 / 20
            when composite_index < 14.0* 0.019043 / 20 then 14.0* 0.019043 / 20
            when composite_index < 15.0* 0.019043 / 20 then 15.0* 0.019043 / 20
            when composite_index < 16.0* 0.019043 / 20 then 16.0* 0.019043 / 20
            when composite_index < 17.0* 0.019043 / 20 then 17.0* 0.019043 / 20
            when composite_index < 18.0* 0.019043 / 20 then 18.0* 0.019043 / 20
            when composite_index < 19.0* 0.019043 / 20 then 19.0* 0.019043 / 20
            when composite_index <= 20.0* 0.019043 / 20 then 20.0* 0.019043 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select costs_metrics.group,
         num_posts, 
         num_costs, 
         ratio_costs,
         num_negative_costs,
         ratio_negative_in_costs,
         ratio_negative_costs_in_all_negative,
         ratio_negative_costs_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from costs_metrics)) +
         (1.0 * ratio_costs  / (select sum(ratio_costs) from costs_metrics)) + 
         (0.0 * ratio_negative_costs_over_all / (select sum(ratio_negative_costs_over_all) from costs_metrics)) as composite_index
  from costs_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 9.5215E-4 12 0.0019043 35 0.00285645 69 0.0038086 63 0.00476075 46 0.0057129 15 0.00666505 13 0.0076172 9 0.00856935 5 0.0095215 4 0.01047365 2 0.0114258 1 0.01237795 1 0.01428225 2

In [0]:
%sql
/* Query the created temp table in a SQL cell */
with costs_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.costs = 1 then 1 else 0 end) as num_costs,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as ratio_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.costs = 1 then 1 else 0 end) as ratio_negative_in_costs,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_in_all_negative,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_costs_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select costs_metrics.group,
       num_posts, 
       num_costs, 
       ratio_costs,
       num_negative_costs,
       ratio_negative_in_costs,
       ratio_negative_costs_in_all_negative,
       ratio_negative_costs_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from costs_metrics)) +
       (1.0 * ratio_costs  / (select sum(ratio_costs) from costs_metrics)) + 
       (0.0 * ratio_negative_costs_over_all / (select sum(ratio_negative_costs_over_all) from costs_metrics)) as composite_index
from costs_metrics
order by composite_index desc

group num_posts num_costs ratio_costs num_negative_costs ratio_negative_in_costs ratio_negative_costs_in_all_negative ratio_negative_costs_over_all composite_index Warts_And_Verrucas 814 10 0.0122850122850123 7 0.7 0.0085995085995086 0.0085995085995086 0.013944 Atrophic_Vaginitis 23545 277 0.0117647058823529 110 0.3971119133574007 0.0046719048630282 0.0046719048630282 0.013354 Cataract 71526 747 0.0104437547185639 212 0.2838018741633199 0.0029639571624304 0.0029639571624304 0.011854 Dental_Abscess 2793 26 0.0093089867525958 19 0.7307692307692308 0.0068027210884354 0.0068027210884354 0.010566 Varicose_Vein 2239 20 0.0089325591782046 6 0.3 0.0026797677534614 0.0026797677534614 0.010139 Lyme_Disease 11216 97 0.0086483594864479 50 0.5154639175257733 0.0044579172610556 0.0044579172610556 0.009816 Anticoagulants 4087 33 0.0080743821874235 12 0.3636363636363636 0.0029361389772449 0.0029361389772449 0.009165 Prostate_Problems 241638 1933 0.0079995696041186 652 0.3372995344024832 0.0026982511028894 0.0026982511028894 0.00908 Folliculitis 883 7 0.0079275198187995 7 1.0 0.0079275198187995 0.0079275198187995 0.008998 Hepatitis 1431 11 0.0076869322152341 8 0.7272727272727273 0.0055904961565339 0.0055904961565339 0.008725 Cervical_Smear_and_Disorders 5336 39 0.0073088455772114 24 0.6153846153846154 0.0044977511244378 0.0044977511244378 0.008296 Surgery_and_Anaesthetics 2742 20 0.0072939460247994 12 0.6 0.0043763676148796 0.0043763676148796 0.008279 Eustachian_Tube_Dysfunction 21744 150 0.0068984547461369 71 0.4733333333333333 0.0032652685798381 0.0032652685798381 0.00783 Prostate_Cancer 31848 215 0.0067508163777945 80 0.372093023255814 0.0025119316754584 0.0025119316754584 0.007663 Sweating 4750 32 0.0067368421052632 19 0.59375 0.004 0.004 0.007647 Disc_Prolapse 31536 202 0.0064053779807204 101 0.5 0.0032026889903602 0.0032026889903602 0.00727 Backache 18628 119 0.0063882327678763 74 0.6218487394957983 0.0039725144943096 0.0039725144943096 0.007251 Vasectomy 3608 23 0.0063747228381375 8 0.3478260869565217 0.0022172949002217 0.0022172949002217 0.007236 Postherpetic_Neuralgia 13444 83 0.0061737578101755 34 0.4096385542168675 0.0025290092234454 0.0025290092234454 0.007008 Levothyroxine_Sodium 9399 58 0.0061708692414087 33 0.5689655172413793 0.003511011809767 0.003511011809767 0.007004 Oral_and_Dental_Problems 23008 141 0.0061283031988873 81 0.574468085106383 0.0035205146036161 0.0035205146036161 0.006956 Pain_and_Pain_Relief 13221 81 0.0061266167460858 38 0.4691358024691358 0.0028742152635958 0.0028742152635958 0.006954 Glaucoma 3840 23 0.0059895833333333 10 0.4347826086956522 0.0026041666666667 0.0026041666666667 0.006799 Sciatica 13788 82 0.0059472004641717 44 0.5365853658536585 0.0031911807368726 0.0031911807368726 0.00675 Vitiligo 1400 8 0.0057142857142857 1 0.125 7.142857142857E-4 7.142857142857E-4 0.006486 Nasal_Problems 7904 45 0.0056933198380567 31 0.6888888888888889 0.0039220647773279 0.0039220647773279 0.006462 Ramipril 3706 21 0.0056664867781975 8 0.380952380952381 0.0021586616297895 0.0021586616297895 0.006432 Rhinitis 4431 25 0.0056420672534417 15 0.6 0.003385240352065 0.003385240352065 0.006404 Hydrocele 4644 26 0.0055986218776916 11 0.4230769230769231 0.0023686477174849 0.0023686477174849 0.006355 Osteoarthritis 33068 182 0.0055038103302286 94 0.5164835164835165 0.0028426273134148 0.0028426273134148 0.006247 Sex_Chromosome_Aneuploidies 6116 33 0.0053956834532374 11 0.3333333333333333 0.0017985611510791 0.0017985611510791 0.006124 Pernicious_Anaemia 19906 107 0.005375263739576 40 0.3738317757009346 0.0020094443886265 0.0020094443886265 0.006101 Spinal_Problems 45897 243 0.0052944636904373 128 0.5267489711934156 0.0027888533019587 0.0027888533019587 0.00601 Statins_and_Other_Lipid_lowering_Medicines 15127 80 0.00528855688504 45 0.5625 0.002974813247835 0.002974813247835 0.006003 Hemifacial_Spasm 8256 42 0.0050872093023256 20 0.4761904761904762 0.002422480620155 0.002422480620155 0.005774 Acne 3362 17 0.0050565139797739 11 0.647058

In [0]:
%sql
-- Cataract, Atrophic_Vaginitis
select t.group, t.text
from `simplified_whole_sentences` as t
where t.costs = 1 and t.sentiment = 1 and 
(t.group = 'Warts_And_Verrucas' or 
t.group = "Atrophic_Vaginitis" or 
t.group = "Folliculitis" or 
t.group = "Dental_Abscess" or 
t.group = "Hepatitis" or 
t.group = "Cataract" or 
t.group = "Lyme_Disease" or 
t.group = "Cervical_Smear_and_Disorders" or 
t.group = "Surgery_and_Anaesthetics" or 
t.group = "Sweating" or
t.group = "Backache" or
t.group = "Nasal_Problems" or
t.group = "Oral_and_Dental_Problems" or
t.group = "Levothyroxine_Sodium" or
t.group = "Rhinitis" or
t.group = "Acne" or
t.group = "Varicose_Vein" or
t.group = "Anticoagulants" or
t.group = "Prostate_Problems" or
t.group = "Eustachian_Tube_Dysfunction" or
t.group = "Prostate_Cancer")
order by t.group

group text Acne I do not know which products to try out and dermatologists are a bit expensive . Acne I have looked into getting laser removal to help , but have read mixed reviews and as its really expensive for 3 sessions , i wanted to get some feedback and find out peoples experience . Acne Is the scarring is too bad then laser treatment is the way to go , but it is very expensive . Acne I tried different diets , all the expensive and cheap face creams , face treatments . Acne I have really become tired of trying to figure it out and have even taken magnesium , zinc , vit b12 6 and saw palmetto ( as i thought it might be hormonal even tho i am male ) Does anyone have any new ideas of what it could be ? I would go to a dermatologist but the waiting list is 6 months to a year with huge costs and needs a GP refferal in most cases . Acne I have tried everything and have wasted thousands of dollars in treatments , natural or not . Acne Or you could try a doctor although the latter would be more costly . Acne I could not afford expensive treatment but I might be able to afford a monthly thing . Acne Can anyone suggest anything else I could try please ? I have looked at laser treatment but it is not available on the NHS and I can not afford to go privately . Acne It did not really helped me a lot , so I decided to go with medication prescribed by my doctors , something that just wasted money and time and stress and overall hope . Acne I paid to see a Dermatologist initially and it really was a waste of money she did not tell me anything different to what the NHS dermatologist has told me . Anticoagulants NOPE I just emailed my doctor ( not an old fuddy duddy bit a specsilist trained in USA and Britain and head of the Geriatric dept in a VERY expensive hospital here , , e is wekk known and stays on top of things and a friend so he wants only the best . Anticoagulants There are three new and expensive alternatives that do not require you to have frequent tests for your INR . Anticoagulants 3 seems expencive but to save time in the doctrs surgery or hospital and the cost of fuel or bus , its probably the same . Anticoagulants Apixaban is also The most expensive as it is one tablet twice a day . Anticoagulants because of an operation and possible bleeding ) They switched me from Xarelto to PLAVIX a milder blood thinner which may have to be stopped for 5 7 days before and after operation ( RISKING STROKES ) Thetyswitched me from the first NEW blood thinner Xarelto which is expensive and I think it caused a himotoma in my mastctomy breast ( which was reconstructed 12 years ago nowt ( NOW has hardened now and needs to be replaced BUT most dcctors rs AND myself are nervous to do even if taken off the new blood Anticoagulants My doctors reaction when I did ask about Eilquis ( although I do realise now it is not the way to go ) was that it was very expensive and that s all she said . Anticoagulants Also the cost of these NOAC s is significantly higher than Warfarin and because of this they seem to be only prescribed to those patients who can not deal with Warfarin because their INR is totally unstable . Anticoagulants Other examples concern medications recommended by private consultants that are more expensive , but without good evidence that they are more effective , than those locally prescribed for the same condition within the NHS . Anticoagulants This advice should be explained to the patient who will retain the option of purchasing the more expensive drug via the private consultant . Anticoagulants My local authority had contacted my doctors stating that I needed to be taken off of phenindione as it was not often in stock and that it was too expensive and that it should be replaced with Rivoxaban . Anticoagulants we then found out that they were paid to do the test ! Anticoagulants Now there is a alternative to warfarin I will be asking my doctor if i can go on to it , I know they will not be happy about the extra costs but as I under

In [0]:
df = sqlContext.sql('''
select t.group, t.text
from `simplified_whole_sentences` as t
where t.costs = 1 and t.sentiment = 1 and t.group = 'Warts_And_Verrucas'
''')
f = df.select("text").collect()
text = ""
for each in f:
  text += each['text'] + " "
  
# r = Rake(ranking_metric=Metric.DEGREE_TO_FREQUENCY_RATIO)
# r = Rake(ranking_metric=Metric.WORD_DEGREE)
# r = Rake(ranking_metric=Metric.WORD_FREQUENCY)
r = Rake(min_length=1, max_length=4, ranking_metric=Metric.DEGREE_TO_FREQUENCY_RATIO)
r.extract_keywords_from_text(text)
r.get_ranked_phrases()

Out[12]: ['doctor suggested gardisil',
 'side effects',
 'generally recommended',
 'wart',
 'vaccine',
 'painful',
 'label',
 'kill',
 'expensive',
 'dose',
 'dermatologist',
 'cryotherapy',
 'attempt',
 'afford',
 '45',
 '240']

In [0]:
%sql
with errors as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select errors.group,
       num_posts, 
       num_errors, 
       ratio_errors,
       num_negative_errors,
       ratio_negative_in_errors,
       ratio_negative_errors_over_all,
       (ratio_errors * 1.0 / (select sum(ratio_errors) from errors)) + (ratio_negative_errors_over_all * 1.0 / (select sum(ratio_negative_errors_over_all) from errors)) as composite_index
from errors
order by composite_index desc
LIMIT 10

group num_posts num_errors ratio_errors num_negative_errors ratio_negative_in_errors ratio_negative_errors_over_all composite_index Lyme_Disease 11216 53 0.004725392296719 47 0.8867924528301887 0.0041904422253923 0.039024 Appendicitis 1603 6 0.0037429819089208 6 1.0 0.0037429819089208 0.032852 Pityriasis_Rosea 10977 35 0.0031884850141204 34 0.9714285714285714 0.0030973854422884 0.027567 Osteomyelitis 5217 16 0.003066896683918 16 1.0 0.003066896683918 0.026918 Trazodone 983 3 0.0030518819938962 3 1.0 0.0030518819938962 0.026786 Pituitary_Disorders 3970 13 0.0032745591939547 10 0.7692307692307692 0.0025188916876574 0.025278 Cellulitis 4181 12 0.0028701267639321 12 1.0 0.0028701267639321 0.02519 Haematological_Disorders 5787 18 0.0031104199066874 15 0.8333333333333333 0.0025920165889062 0.024925 Pelvic_Pain_and_Disorders 4172 11 0.0026366251198466 11 1.0 0.0026366251198466 0.023141 Pulmonary_Embolism 14596 37 0.0025349410797479 35 0.9459459459459459 0.0023979172375993 0.021621

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000106	0.075079	0.074973
with errors_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_in_all_negative,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 0.000106 + 1.0* 0.074973 / 20 then 0.000106 + 1.0* 0.074973 / 20 
            when composite_index < 0.000106 + 2.0* 0.074973 / 20 then 0.000106 + 2.0* 0.074973 / 20
            when composite_index < 0.000106 + 3.0* 0.074973 / 20 then 0.000106 + 3.0* 0.074973 / 20
            when composite_index < 0.000106 + 4.0* 0.074973/ 20 then 0.000106 + 4.0* 0.074973 / 20
            when composite_index < 0.000106 + 5.0* 0.074973 / 20 then 0.000106 + 5.0* 0.074973 / 20
            when composite_index < 0.000106 + 6.0* 0.074973 / 20 then 0.000106 + 6.0* 0.074973/ 20
            when composite_index < 0.000106 + 7.0* 0.074973 / 20 then 0.000106 + 7.0* 0.074973 / 20
            when composite_index < 0.000106 + 8.0* 0.074973 / 20 then 0.000106 + 8.0* 0.074973 / 20
            when composite_index < 0.000106 + 9.0* 0.074973/ 20 then 0.000106 + 9.0* 0.074973 / 20
            when composite_index < 0.000106 + 10.0* 0.074973 / 20 then 0.000106 + 10.0* 0.074973 / 20
            when composite_index < 0.000106 + 11.0* 0.074973 / 20 then 0.000106 + 11.0* 0.074973 / 20
            when composite_index < 0.000106 + 12.0* 0.074973 / 20 then 0.000106 + 12.0* 0.074973 / 20
            when composite_index < 0.000106 + 13.0* 0.074973 / 20 then 0.000106 + 13.0* 0.074973 / 20
            when composite_index < 0.000106 + 14.0* 0.074973 / 20 then 0.000106 + 14.0* 0.074973 / 20
            when composite_index < 0.000106 + 15.0* 0.074973 / 20 then 0.000106 + 15.0* 0.074973 / 20
            when composite_index < 0.000106 + 16.0* 0.074973 / 20 then 0.000106 + 16.0* 0.074973 / 20
            when composite_index < 0.000106 + 17.0* 0.074973 / 20 then 0.000106 + 17.0* 0.074973 / 20
            when composite_index < 0.000106 + 18.0* 0.074973 / 20 then 0.000106 + 18.0* 0.074973 / 20
            when composite_index < 0.000106 + 19.0* 0.074973 / 20 then 0.000106 + 19.0* 0.074973 / 20
            when composite_index <= 0.000106 + 20.0* 0.074973 / 20 then 0.000106 + 20.0* 0.074973 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select errors_metrics.group,
         num_posts, 
         num_errors, 
         ratio_errors,
         num_negative_errors,
         ratio_negative_in_errors,
         ratio_negative_errors_in_all_negative,
         ratio_negative_errors_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (1.0 * num_posts / (select sum(num_posts) from errors_metrics)) +
         (1.0 * ratio_errors  / (select sum(ratio_errors) from errors_metrics)) + 
         (1.0 * ratio_negative_errors_over_all / (select sum(ratio_negative_errors_over_all) from errors_metrics)) as composite_index
  from errors_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.00385465 44 0.0076033 68 0.01135195 73 0.0151006 39 0.01884925 18 0.0225979 13 0.02634655 9 0.0300952 4 0.03384385 2 0.0375925 2 0.04134115 1 0.04883845 2 0.0600844 1 0.075079 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
with errors_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_in_all_negative,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select errors_metrics.group,
       num_posts, 
       num_errors, 
       ratio_errors,
       num_negative_errors,
       ratio_negative_in_errors,
       ratio_negative_errors_in_all_negative,
       ratio_negative_errors_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (1.0 * num_posts / (select sum(num_posts) from errors_metrics)) +
       (1.0 * ratio_errors  / (select sum(ratio_errors) from errors_metrics)) + 
       (1.0 * ratio_negative_errors_over_all / (select sum(ratio_negative_errors_over_all) from errors_metrics)) as composite_index
from errors_metrics
order by composite_index desc


group num_posts num_errors ratio_errors num_negative_errors ratio_negative_in_errors ratio_negative_errors_in_all_negative ratio_negative_errors_over_all composite_index Anxiety_Disorders 526203 388 7.373580158228E-4 369 0.9510309278350515 7.012502779346E-4 7.012502779346E-4 0.075079 Hip_Replacement 422127 144 3.41129565273E-4 131 0.9097222222222222 3.103331461859E-4 3.103331461859E-4 0.058024 Polymyalgia_Rheumatica_and_GCA 312978 267 8.530951057263E-4 243 0.9101123595505618 7.764123995936E-4 7.764123995936E-4 0.048041 Menopause 342523 119 3.47421924951E-4 112 0.9411764705882353 3.269853411304E-4 3.269853411304E-4 0.047723 Lyme_Disease 11216 53 0.004725392296719 47 0.8867924528301887 0.0041904422253923 0.0041904422253923 0.04049 Knee_Problems 250359 47 1.877304191181E-4 46 0.9787234042553191 1.837361548816E-4 1.837361548816E-4 0.034351 Prostate_Problems 241638 80 3.310737549558E-4 69 0.8625 2.855511136493E-4 2.855511136493E-4 0.034278 Appendicitis 1603 6 0.0037429819089208 6 1.0 0.0037429819089208 0.0037429819089208 0.033062 Depression 230756 73 3.163514708177E-4 70 0.9589041095890412 3.033507254416E-4 3.033507254416E-4 0.032876 Pityriasis_Rosea 10977 35 0.0031884850141204 34 0.9714285714285714 0.0030973854422884 0.0030973854422884 0.029002 Osteomyelitis 5217 16 0.003066896683918 16 1.0 0.003066896683918 0.003066896683918 0.0276 Trazodone 983 3 0.0030518819938962 3 1.0 0.0030518819938962 0.0030518819938962 0.026914 Abdominal_Disorders 136553 147 0.0010765050932605 130 0.8843537414965986 9.520113069651E-4 9.520113069651E-4 0.026725 Citalopram 186113 40 2.149231918243E-4 36 0.9 1.934308726419E-4 1.934308726419E-4 0.026113 Pituitary_Disorders 3970 13 0.0032745591939547 10 0.7692307692307692 0.0025188916876574 0.0025188916876574 0.025797 Cellulitis 4181 12 0.0028701267639321 12 1.0 0.0028701267639321 0.0028701267639321 0.025736 Haematological_Disorders 5787 18 0.0031104199066874 15 0.8333333333333333 0.0025920165889062 0.0025920165889062 0.025681 Lichen_Sclerosus 102644 126 0.0012275437434239 119 0.9444444444444444 0.0011593468687892 0.0011593468687892 0.023876 Pelvic_Pain_and_Disorders 4172 11 0.0026366251198466 11 1.0 0.0026366251198466 0.0026366251198466 0.023686 Pulmonary_Embolism 14596 37 0.0025349410797479 35 0.9459459459459459 0.0023979172375993 0.0023979172375993 0.023529 Gallbladder_Problems 110324 117 0.0010605126717668 111 0.9487179487179487 0.001006127406548 0.001006127406548 0.023478 Vertigo_and_Dizziness 88940 121 0.0013604677310546 111 0.9173553719008264 0.0012480323813807 0.0012480323813807 0.023049 Irritable_Bowel_Syndrome 84172 113 0.0013424891888039 98 0.8672566371681416 0.0011642826593166 0.0011642826593166 0.021968 Coagulation_Disorders 1828 5 0.0027352297592998 4 0.8 0.0021881838074398 0.0021881838074398 0.021739 Coeliac_Disease 9081 22 0.0024226406783394 20 0.9090909090909091 0.0022024006166722 0.0022024006166722 0.021441 Asthma 6926 16 0.0023101357204736 16 1.0 0.0023101357204736 0.0023101357204736 0.021181 Movement_Disorders 4734 11 0.0023236163920575 11 1.0 0.0023236163920575 0.0023236163920575 0.021013 Genital_Herpes_Simplex 100631 87 8.645447227991E-4 83 0.9540229885057471 8.247955401417E-4 8.247955401417E-4 0.020557 Cauda_Equina_Syndrome 6221 15 0.0024111879119113 13 0.8666666666666667 0.0020896961903231 0.0020896961903231 0.020503 Lumbar_Puncture 1736 4 0.0023041474654378 4 1.0 0.0023041474654378 0.0023041474654378 0.02045 Gilberts_Syndrome 4430 10 0.0022573363431151 10 1.0 0.0022573363431151 0.0022573363431151 0.020391 Multiple_Sclerosis 11629 26 0.0022357898357554 24 0.9230769230769231 0.0020638060022358 0.0020638060022358 0.020355 Chronic_Fatigue_Syndrome 104500 81 7.751196172249E-4 75 0.9259259259259259 7.177033492823E-4 7.177033492823E-4 0.020198 Sjogrens_Syndrome 31788 57 0.0017931294828237 54 0.9473684210526316 0.0016987542468856 0.0016987542468856 0.019461 Hypothyroidism 74189 81 0.0010918060628934 77 0.9506172839506173 0.0010378897141086 0.0010378897141086 0.019032 Breast_Cancer_and_Screening

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0	0.039024	0.039024
with errors_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_in_all_negative,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.039024 / 20 then 1.0* 0.039024 / 20 
            when composite_index < 2.0* 0.039024 / 20 then 2.0* 0.039024 / 20
            when composite_index < 3.0* 0.039024 / 20 then 3.0* 0.039024 / 20
            when composite_index < 4.0* 0.039024/ 20 then 4.0* 0.039024 / 20
            when composite_index < 5.0* 0.039024 / 20 then 5.0* 0.039024 / 20
            when composite_index < 6.0* 0.039024 / 20 then 6.0* 0.039024 / 20
            when composite_index < 7.0* 0.039024 / 20 then 7.0* 0.039024 / 20
            when composite_index < 8.0* 0.039024 / 20 then 8.0* 0.039024 / 20
            when composite_index < 9.0* 0.039024 / 20 then 9.0* 0.039024 / 20
            when composite_index < 10.0* 0.039024 / 20 then 10.0* 0.039024 / 20
            when composite_index < 11.0* 0.039024 / 20 then 11.0* 0.039024 / 20
            when composite_index < 12.0* 0.039024 / 20 then 12.0* 0.039024 / 20
            when composite_index < 13.0* 0.039024 / 20 then 13.0* 0.039024 / 20
            when composite_index < 14.0* 0.039024 / 20 then 14.0* 0.039024 / 20
            when composite_index < 15.0* 0.039024 / 20 then 15.0* 0.039024 / 20
            when composite_index < 16.0* 0.039024 / 20 then 16.0* 0.039024 / 20
            when composite_index < 17.0* 0.039024 / 20 then 17.0* 0.039024 / 20
            when composite_index < 18.0* 0.039024 / 20 then 18.0* 0.039024 / 20
            when composite_index < 19.0* 0.039024 / 20 then 19.0* 0.039024 / 20
            when composite_index <= 20.0* 0.039024 / 20 then 20.0* 0.039024 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select errors_metrics.group,
         num_posts, 
         num_errors, 
         ratio_errors,
         num_negative_errors,
         ratio_negative_in_errors,
         ratio_negative_errors_in_all_negative,
         ratio_negative_errors_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from errors_metrics)) +
         (1.0 * ratio_errors  / (select sum(ratio_errors) from errors_metrics)) + 
         (1.0 * ratio_negative_errors_over_all / (select sum(ratio_negative_errors_over_all) from errors_metrics)) as composite_index
  from errors_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.0019512 43 0.0039024 38 0.0058536 51 0.0078048 51 0.009756 29 0.0117072 27 0.0136584 7 0.0156096 7 0.0175608 4 0.019512 3 0.0214632 6 0.0234144 3 0.0253656 3 0.0273168 2 0.029268 1 0.0331704 1 0.039024 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
with errors_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_in_all_negative,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select errors_metrics.group,
       num_posts, 
       num_errors, 
       ratio_errors,
       num_negative_errors,
       ratio_negative_in_errors,
       ratio_negative_errors_in_all_negative,
       ratio_negative_errors_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from errors_metrics)) +
       (1.0 * ratio_errors  / (select sum(ratio_errors) from errors_metrics)) + 
       (1.0 * ratio_negative_errors_over_all / (select sum(ratio_negative_errors_over_all) from errors_metrics)) as composite_index
from errors_metrics
order by composite_index desc


group num_posts num_errors ratio_errors num_negative_errors ratio_negative_in_errors ratio_negative_errors_in_all_negative ratio_negative_errors_over_all composite_index Lyme_Disease 11216 53 0.004725392296719 47 0.8867924528301887 0.0041904422253923 0.0041904422253923 0.039024 Appendicitis 1603 6 0.0037429819089208 6 1.0 0.0037429819089208 0.0037429819089208 0.032852 Pityriasis_Rosea 10977 35 0.0031884850141204 34 0.9714285714285714 0.0030973854422884 0.0030973854422884 0.027567 Osteomyelitis 5217 16 0.003066896683918 16 1.0 0.003066896683918 0.003066896683918 0.026918 Trazodone 983 3 0.0030518819938962 3 1.0 0.0030518819938962 0.0030518819938962 0.026786 Pituitary_Disorders 3970 13 0.0032745591939547 10 0.7692307692307692 0.0025188916876574 0.0025188916876574 0.025278 Cellulitis 4181 12 0.0028701267639321 12 1.0 0.0028701267639321 0.0028701267639321 0.02519 Haematological_Disorders 5787 18 0.0031104199066874 15 0.8333333333333333 0.0025920165889062 0.0025920165889062 0.024925 Pelvic_Pain_and_Disorders 4172 11 0.0026366251198466 11 1.0 0.0026366251198466 0.0026366251198466 0.023141 Pulmonary_Embolism 14596 37 0.0025349410797479 35 0.9459459459459459 0.0023979172375993 0.0023979172375993 0.021621 Coagulation_Disorders 1828 5 0.0027352297592998 4 0.8 0.0021881838074398 0.0021881838074398 0.0215 Movement_Disorders 4734 11 0.0023236163920575 11 1.0 0.0023236163920575 0.0023236163920575 0.020394 Asthma 6926 16 0.0023101357204736 16 1.0 0.0023101357204736 0.0023101357204736 0.020276 Coeliac_Disease 9081 22 0.0024226406783394 20 0.9090909090909091 0.0022024006166722 0.0022024006166722 0.020254 Lumbar_Puncture 1736 4 0.0023041474654378 4 1.0 0.0023041474654378 0.0023041474654378 0.020223 Gilberts_Syndrome 4430 10 0.0022573363431151 10 1.0 0.0022573363431151 0.0022573363431151 0.019812 Cauda_Equina_Syndrome 6221 15 0.0024111879119113 13 0.8666666666666667 0.0020896961903231 0.0020896961903231 0.01969 Multiple_Sclerosis 11629 26 0.0022357898357554 24 0.9230769230769231 0.0020638060022358 0.0020638060022358 0.018835 Breast_Cancer_and_Screening 2890 6 0.002076124567474 6 1.0 0.002076124567474 0.002076124567474 0.018222 Orthopaedic_Disorders 4932 11 0.0022303325223033 9 0.8181818181818182 0.0018248175182482 0.0018248175182482 0.017718 Hip_Dysplasia_and_Disorders 8757 20 0.0022838871759735 15 0.75 0.0017129153819801 0.0017129153819801 0.01743 Idiopathic_Intracranial_Hypertension 3527 8 0.0022682166146867 6 0.75 0.001701162461015 0.001701162461015 0.01731 Adrenal_Disorders 9887 20 0.0020228582987762 19 0.95 0.0019217153838374 0.0019217153838374 0.01729 Methotrexate 5120 10 0.001953125 10 1.0 0.001953125 0.001953125 0.017142 Mastocytosis_and_Mast_Cell_Disorders 2254 4 0.0017746228926353 4 1.0 0.0017746228926353 0.0017746228926353 0.015576 Bowel_Disorders 10766 19 0.0017648151588334 19 1.0 0.0017648151588334 0.0017648151588334 0.01549 Sjogrens_Syndrome 31788 57 0.0017931294828237 54 0.9473684210526316 0.0016987542468856 0.0016987542468856 0.015306 Autonomic_Dysfunction 5219 9 0.0017244682889442 9 1.0 0.0017244682889442 0.0017244682889442 0.015135 Sex_Chromosome_Aneuploidies 6116 12 0.0019620667102681 9 0.75 0.0014715500327011 0.0014715500327011 0.014973 Investigations_and_Procedures 1831 3 0.0016384489350082 3 1.0 0.0016384489350082 0.0016384489350082 0.014381 Muscle_Disorders 5109 8 0.001565864161284 8 1.0 0.001565864161284 0.001565864161284 0.013743 Abscess_Non_dental 5190 8 0.0015414258188825 8 1.0 0.0015414258188825 0.0015414258188825 0.013528 Cholesteatoma 5918 9 0.0015207840486651 9 1.0 0.0015207840486651 0.0015207840486651 0.013348 Dietary_Nutrition_and_Exercise_Advice 12808 19 0.0014834478450968 19 1.0 0.0014834478450968 0.0014834478450968 0.01302 Oesophageal_Achalasia_and_Spasm 26607 42 0.0015785319652723 35 0.8333333333333333 0.0013154433043936 0.0013154433043936 0.012649 Hepatitis 1431 2 0.0013976240391335 2 1.0 0.0013976240391335 0.0013976240391335 0.012267 Thyroid_and_Parathyroid_Disorders 16393 23 0.0014030378820228 22 0.9565217

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000106	0.075079	0.074973
with errors_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_in_all_negative,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.019197 / 20 then 1.0* 0.019197 / 20 
            when composite_index < 2.0* 0.019197 / 20 then 2.0* 0.019197 / 20
            when composite_index < 3.0* 0.019197 / 20 then 3.0* 0.019197 / 20
            when composite_index < 4.0* 0.019197/ 20 then 4.0* 0.019197 / 20
            when composite_index < 5.0* 0.019197 / 20 then 5.0* 0.019197 / 20
            when composite_index < 6.0* 0.019197 / 20 then 6.0* 0.019197 / 20
            when composite_index < 7.0* 0.019197 / 20 then 7.0* 0.019197 / 20
            when composite_index < 8.0* 0.019197 / 20 then 8.0* 0.019197 / 20
            when composite_index < 9.0* 0.019197 / 20 then 9.0* 0.019197 / 20
            when composite_index < 10.0* 0.019197 / 20 then 10.0* 0.019197 / 20
            when composite_index < 11.0* 0.019197 / 20 then 11.0* 0.019197 / 20
            when composite_index < 12.0* 0.019197 / 20 then 12.0* 0.019197 / 20
            when composite_index < 13.0* 0.019197 / 20 then 13.0* 0.019197 / 20
            when composite_index < 14.0* 0.019197 / 20 then 14.0* 0.019197 / 20
            when composite_index < 15.0* 0.019197 / 20 then 15.0* 0.019197 / 20
            when composite_index < 16.0* 0.019197 / 20 then 16.0* 0.019197 / 20
            when composite_index < 17.0* 0.019197 / 20 then 17.0* 0.019197 / 20
            when composite_index < 18.0* 0.019197 / 20 then 18.0* 0.019197 / 20
            when composite_index < 19.0* 0.019197 / 20 then 19.0* 0.019197 / 20
            when composite_index <= 20.0* 0.019197 / 20 then 20.0* 0.019197 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select errors_metrics.group,
         num_posts, 
         num_errors, 
         ratio_errors,
         num_negative_errors,
         ratio_negative_in_errors,
         ratio_negative_errors_in_all_negative,
         ratio_negative_errors_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from errors_metrics)) +
         (0.0 * ratio_errors  / (select sum(ratio_errors) from errors_metrics)) + 
         (1.0 * ratio_negative_errors_over_all / (select sum(ratio_negative_errors_over_all) from errors_metrics)) as composite_index
  from errors_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 9.5985E-4 44 0.0019197 38 0.00287955 48 0.0038394 52 0.00479925 25 0.0057591 28 0.00671895 8 0.0076788 6 0.00863865 7 0.0095985 5 0.01055835 4 0.0115182 3 0.01247805 3 0.0134379 1 0.01439775 3 0.0172773 1 0.019197 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
with errors_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_in_all_negative,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select errors_metrics.group,
       num_posts, 
       num_errors, 
       ratio_errors,
       num_negative_errors,
       ratio_negative_in_errors,
       ratio_negative_errors_in_all_negative,
       ratio_negative_errors_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from errors_metrics)) +
       (0.0 * ratio_errors  / (select sum(ratio_errors) from errors_metrics)) + 
       (1.0 * ratio_negative_errors_over_all / (select sum(ratio_negative_errors_over_all) from errors_metrics)) as composite_index
from errors_metrics
order by composite_index desc


group num_posts num_errors ratio_errors num_negative_errors ratio_negative_in_errors ratio_negative_errors_in_all_negative ratio_negative_errors_over_all composite_index Lyme_Disease 11216 53 0.004725392296719 47 0.8867924528301887 0.0041904422253923 0.0041904422253923 0.019197 Appendicitis 1603 6 0.0037429819089208 6 1.0 0.0037429819089208 0.0037429819089208 0.017147 Pityriasis_Rosea 10977 35 0.0031884850141204 34 0.9714285714285714 0.0030973854422884 0.0030973854422884 0.014189 Osteomyelitis 5217 16 0.003066896683918 16 1.0 0.003066896683918 0.003066896683918 0.01405 Trazodone 983 3 0.0030518819938962 3 1.0 0.0030518819938962 0.0030518819938962 0.013981 Cellulitis 4181 12 0.0028701267639321 12 1.0 0.0028701267639321 0.0028701267639321 0.013148 Pelvic_Pain_and_Disorders 4172 11 0.0026366251198466 11 1.0 0.0026366251198466 0.0026366251198466 0.012078 Haematological_Disorders 5787 18 0.0031104199066874 15 0.8333333333333333 0.0025920165889062 0.0025920165889062 0.011874 Pituitary_Disorders 3970 13 0.0032745591939547 10 0.7692307692307692 0.0025188916876574 0.0025188916876574 0.011539 Pulmonary_Embolism 14596 37 0.0025349410797479 35 0.9459459459459459 0.0023979172375993 0.0023979172375993 0.010985 Movement_Disorders 4734 11 0.0023236163920575 11 1.0 0.0023236163920575 0.0023236163920575 0.010645 Asthma 6926 16 0.0023101357204736 16 1.0 0.0023101357204736 0.0023101357204736 0.010583 Lumbar_Puncture 1736 4 0.0023041474654378 4 1.0 0.0023041474654378 0.0023041474654378 0.010555 Gilberts_Syndrome 4430 10 0.0022573363431151 10 1.0 0.0022573363431151 0.0022573363431151 0.010341 Coeliac_Disease 9081 22 0.0024226406783394 20 0.9090909090909091 0.0022024006166722 0.0022024006166722 0.010089 Coagulation_Disorders 1828 5 0.0027352297592998 4 0.8 0.0021881838074398 0.0021881838074398 0.010024 Cauda_Equina_Syndrome 6221 15 0.0024111879119113 13 0.8666666666666667 0.0020896961903231 0.0020896961903231 0.009573 Breast_Cancer_and_Screening 2890 6 0.002076124567474 6 1.0 0.002076124567474 0.002076124567474 0.009511 Multiple_Sclerosis 11629 26 0.0022357898357554 24 0.9230769230769231 0.0020638060022358 0.0020638060022358 0.009454 Methotrexate 5120 10 0.001953125 10 1.0 0.001953125 0.001953125 0.008947 Adrenal_Disorders 9887 20 0.0020228582987762 19 0.95 0.0019217153838374 0.0019217153838374 0.008803 Orthopaedic_Disorders 4932 11 0.0022303325223033 9 0.8181818181818182 0.0018248175182482 0.0018248175182482 0.00836 Mastocytosis_and_Mast_Cell_Disorders 2254 4 0.0017746228926353 4 1.0 0.0017746228926353 0.0017746228926353 0.00813 Bowel_Disorders 10766 19 0.0017648151588334 19 1.0 0.0017648151588334 0.0017648151588334 0.008085 Autonomic_Dysfunction 5219 9 0.0017244682889442 9 1.0 0.0017244682889442 0.0017244682889442 0.0079 Hip_Dysplasia_and_Disorders 8757 20 0.0022838871759735 15 0.75 0.0017129153819801 0.0017129153819801 0.007847 Idiopathic_Intracranial_Hypertension 3527 8 0.0022682166146867 6 0.75 0.001701162461015 0.001701162461015 0.007793 Sjogrens_Syndrome 31788 57 0.0017931294828237 54 0.9473684210526316 0.0016987542468856 0.0016987542468856 0.007782 Investigations_and_Procedures 1831 3 0.0016384489350082 3 1.0 0.0016384489350082 0.0016384489350082 0.007506 Muscle_Disorders 5109 8 0.001565864161284 8 1.0 0.001565864161284 0.001565864161284 0.007173 Abscess_Non_dental 5190 8 0.0015414258188825 8 1.0 0.0015414258188825 0.0015414258188825 0.007061 Cholesteatoma 5918 9 0.0015207840486651 9 1.0 0.0015207840486651 0.0015207840486651 0.006967 Dietary_Nutrition_and_Exercise_Advice 12808 19 0.0014834478450968 19 1.0 0.0014834478450968 0.0014834478450968 0.006796 Sex_Chromosome_Aneuploidies 6116 12 0.0019620667102681 9 0.75 0.0014715500327011 0.0014715500327011 0.006741 Hepatitis 1431 2 0.0013976240391335 2 1.0 0.0013976240391335 0.0013976240391335 0.006403 Thyroid_and_Parathyroid_Disorders 16393 23 0.0014030378820228 22 0.9565217391304348 0.0013420362349783 0.0013420362349783 0.006148 Oesophageal_Achalasia_and_Spasm 26607 42 0.0015785319652723 35 0.833

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000106	0.075079	0.074973
with errors_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_in_all_negative,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.019197 / 20 then 1.0* 0.019197 / 20 
            when composite_index < 2.0* 0.019197 / 20 then 2.0* 0.019197 / 20
            when composite_index < 3.0* 0.019197 / 20 then 3.0* 0.019197 / 20
            when composite_index < 4.0* 0.019197/ 20 then 4.0* 0.019197 / 20
            when composite_index < 5.0* 0.019197 / 20 then 5.0* 0.019197 / 20
            when composite_index < 6.0* 0.019197 / 20 then 6.0* 0.019197 / 20
            when composite_index < 7.0* 0.019197 / 20 then 7.0* 0.019197 / 20
            when composite_index < 8.0* 0.019197 / 20 then 8.0* 0.019197 / 20
            when composite_index < 9.0* 0.019197 / 20 then 9.0* 0.019197 / 20
            when composite_index < 10.0* 0.019197 / 20 then 10.0* 0.019197 / 20
            when composite_index < 11.0* 0.019197 / 20 then 11.0* 0.019197 / 20
            when composite_index < 12.0* 0.019197 / 20 then 12.0* 0.019197 / 20
            when composite_index < 13.0* 0.019197 / 20 then 13.0* 0.019197 / 20
            when composite_index < 14.0* 0.019197 / 20 then 14.0* 0.019197 / 20
            when composite_index < 15.0* 0.019197 / 20 then 15.0* 0.019197 / 20
            when composite_index < 16.0* 0.019197 / 20 then 16.0* 0.019197 / 20
            when composite_index < 17.0* 0.019197 / 20 then 17.0* 0.019197 / 20
            when composite_index < 18.0* 0.019197 / 20 then 18.0* 0.019197 / 20
            when composite_index < 19.0* 0.019197 / 20 then 19.0* 0.019197 / 20
            when composite_index <= 20.0* 0.019197 / 20 then 20.0* 0.019197 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select errors_metrics.group,
         num_posts, 
         num_errors, 
         ratio_errors,
         num_negative_errors,
         ratio_negative_in_errors,
         ratio_negative_errors_in_all_negative,
         ratio_negative_errors_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from errors_metrics)) +
         (1.0 * ratio_errors  / (select sum(ratio_errors) from errors_metrics)) + 
         (0.0 * ratio_negative_errors_over_all / (select sum(ratio_negative_errors_over_all) from errors_metrics)) as composite_index
  from errors_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency null 1 9.5985E-4 41 0.0019197 38 0.00287955 51 0.0038394 51 0.00479925 31 0.0057591 23 0.00671895 12 0.0076788 5 0.00863865 3 0.0095985 6 0.01055835 5 0.0115182 3 0.01247805 1 0.0134379 4 0.01439775 1 0.01631745 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
with errors_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.errors = 1 then 1 else 0 end) as num_errors,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as ratio_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.errors = 1 then 1 else 0 end) as ratio_negative_in_errors,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_in_all_negative,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_errors_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select errors_metrics.group,
       num_posts, 
       num_errors, 
       ratio_errors,
       num_negative_errors,
       ratio_negative_in_errors,
       ratio_negative_errors_in_all_negative,
       ratio_negative_errors_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from errors_metrics)) +
       (1.0 * ratio_errors  / (select sum(ratio_errors) from errors_metrics)) + 
       (0.0 * ratio_negative_errors_over_all / (select sum(ratio_negative_errors_over_all) from errors_metrics)) as composite_index
from errors_metrics
order by composite_index desc


group num_posts num_errors ratio_errors num_negative_errors ratio_negative_in_errors ratio_negative_errors_in_all_negative ratio_negative_errors_over_all composite_index Lyme_Disease 11216 53 0.004725392296719 47 0.8867924528301887 0.0041904422253923 0.0041904422253923 0.019827 Appendicitis 1603 6 0.0037429819089208 6 1.0 0.0037429819089208 0.0037429819089208 0.015705 Pituitary_Disorders 3970 13 0.0032745591939547 10 0.7692307692307692 0.0025188916876574 0.0025188916876574 0.013739 Pityriasis_Rosea 10977 35 0.0031884850141204 34 0.9714285714285714 0.0030973854422884 0.0030973854422884 0.013378 Haematological_Disorders 5787 18 0.0031104199066874 15 0.8333333333333333 0.0025920165889062 0.0025920165889062 0.013051 Osteomyelitis 5217 16 0.003066896683918 16 1.0 0.003066896683918 0.003066896683918 0.012868 Trazodone 983 3 0.0030518819938962 3 1.0 0.0030518819938962 0.0030518819938962 0.012805 Cellulitis 4181 12 0.0028701267639321 12 1.0 0.0028701267639321 0.0028701267639321 0.012042 Coagulation_Disorders 1828 5 0.0027352297592998 4 0.8 0.0021881838074398 0.0021881838074398 0.011476 Pelvic_Pain_and_Disorders 4172 11 0.0026366251198466 11 1.0 0.0026366251198466 0.0026366251198466 0.011063 Pulmonary_Embolism 14596 37 0.0025349410797479 35 0.9459459459459459 0.0023979172375993 0.0023979172375993 0.010636 Coeliac_Disease 9081 22 0.0024226406783394 20 0.9090909090909091 0.0022024006166722 0.0022024006166722 0.010165 Cauda_Equina_Syndrome 6221 15 0.0024111879119113 13 0.8666666666666667 0.0020896961903231 0.0020896961903231 0.010117 Movement_Disorders 4734 11 0.0023236163920575 11 1.0 0.0023236163920575 0.0023236163920575 0.009749 Asthma 6926 16 0.0023101357204736 16 1.0 0.0023101357204736 0.0023101357204736 0.009693 Lumbar_Puncture 1736 4 0.0023041474654378 4 1.0 0.0023041474654378 0.0023041474654378 0.009668 Hip_Dysplasia_and_Disorders 8757 20 0.0022838871759735 15 0.75 0.0017129153819801 0.0017129153819801 0.009583 Idiopathic_Intracranial_Hypertension 3527 8 0.0022682166146867 6 0.75 0.001701162461015 0.001701162461015 0.009517 Gilberts_Syndrome 4430 10 0.0022573363431151 10 1.0 0.0022573363431151 0.0022573363431151 0.009471 Multiple_Sclerosis 11629 26 0.0022357898357554 24 0.9230769230769231 0.0020638060022358 0.0020638060022358 0.009381 Orthopaedic_Disorders 4932 11 0.0022303325223033 9 0.8181818181818182 0.0018248175182482 0.0018248175182482 0.009358 Breast_Cancer_and_Screening 2890 6 0.002076124567474 6 1.0 0.002076124567474 0.002076124567474 0.008711 Adrenal_Disorders 9887 20 0.0020228582987762 19 0.95 0.0019217153838374 0.0019217153838374 0.008487 Sex_Chromosome_Aneuploidies 6116 12 0.0019620667102681 9 0.75 0.0014715500327011 0.0014715500327011 0.008232 Methotrexate 5120 10 0.001953125 10 1.0 0.001953125 0.001953125 0.008195 Sjogrens_Syndrome 31788 57 0.0017931294828237 54 0.9473684210526316 0.0016987542468856 0.0016987542468856 0.007524 Mastocytosis_and_Mast_Cell_Disorders 2254 4 0.0017746228926353 4 1.0 0.0017746228926353 0.0017746228926353 0.007446 Bowel_Disorders 10766 19 0.0017648151588334 19 1.0 0.0017648151588334 0.0017648151588334 0.007405 Autonomic_Dysfunction 5219 9 0.0017244682889442 9 1.0 0.0017244682889442 0.0017244682889442 0.007235 Investigations_and_Procedures 1831 3 0.0016384489350082 3 1.0 0.0016384489350082 0.0016384489350082 0.006875 Oesophageal_Achalasia_and_Spasm 26607 42 0.0015785319652723 35 0.8333333333333333 0.0013154433043936 0.0013154433043936 0.006623 Muscle_Disorders 5109 8 0.001565864161284 8 1.0 0.001565864161284 0.001565864161284 0.00657 Abscess_Non_dental 5190 8 0.0015414258188825 8 1.0 0.0015414258188825 0.0015414258188825 0.006467 Cholesteatoma 5918 9 0.0015207840486651 9 1.0 0.0015207840486651 0.0015207840486651 0.006381 Chiari_Malformation 17184 26 0.0015130353817505 20 0.7692307692307692 0.0011638733705773 0.0011638733705773 0.006348 Dietary_Nutrition_and_Exercise_Advice 12808 19 0.0014834478450968 19 1.0 0.0014834478450968 0.0014834478450968 0.006224 Neurological_Disorders 27532 39 0.0014

In [0]:
%sql
-- Lyme_Disease, Pityriasis_Rosea
select t.group, t.text
from `simplified_whole_sentences` as t
where t.errors = 1 and t.sentiment = 1 and 
(t.group = 'Lyme_Disease' or 
t.group ="Appendicitis" or 
t.group ="Pityriasis_Rosea" or 
t.group ="Osteomyelitis" or 
t.group ="Trazodone" or 
t.group ="Pituitary_Disorders" or 
t.group ="Haematological_Disorders" or 
t.group ="Cellulitis" or 
t.group ="Pelvic_Pain_and_Disorders" or 
t.group ="Pulmonary_Embolism" or
t.group ="Pelvic_Pain_and_Disorders" or 
t.group ="Movement_Disorders" or 
t.group ="Asthma" or 
t.group ="Lumbar_Puncture" or 
t.group ="Gilberts_Syndrome" or 
t.group ="Coeliac_Disease" or 
t.group ="Coagulation_Disorders") 
order by t.group

group text Appendicitis They re checked my second CT and saw that the radiologists had missed the two stones inside of my appendix . Appendicitis I had bouts of appendicitis for around 1 year prior to my surgery which was misdiagnosed multiple times . Appendicitis Within two weeks of surgery I developed a rash on my trunk ( back , buttocks , shoulders , chest , upper arms ) that was misdiagnosed at least 4 times before I was sent to a dermatologist who performed a skin biopsy . Appendicitis My lower abdomin is sore and feel like at times I am going to have diarea Has anyone experienced pain a week before appendicitis was finally diagnosed ? Has anyone experienced psjns like this and misdiagnosed as a ruptured cyst ? Appendicitis She was misdiagnosed by 5 doctors until we refused to bring her home from a e . Appendicitis I was hospitalised 4 months before it burst and was misdiagnosed that I had such bad morning sickness I had given myself stomach spasms ! That s what hospital told me although my GP was adamant to the paramedic I had a grumbling appendix . Asthma Not sure why they suggested one if you had asthma for 25 years unless they suspect you were misdiagnosed all these years ? Or if it went away ? The first sounds very unlikely the second is possible but also not that likely . Asthma in my humble opinion you have been misdiagnosed . Asthma I dont think it worked and I think maybe the doctor miss diagnosed me . Asthma Due to a mistake from a previous ct scan , the pneumonia worsened . Asthma I think you suspect you have been misdiagnosed , but being on a lot of prednisone is pretty serious . Asthma Her opinion was that if you are suffering daily symptons , then your Asthma is not properly managed and your medication is most likely incorrect . Asthma With me I was never diagonsed with anything regarding my lungs and I still have not been but I always feel like the doctors are missing something . Asthma Can anxiety really cause wheezing or have the doctors misdiagnosed and I may possibly have asthma ? ! . Asthma Yes , I believe I have been misdiagnosed as I do not think the doctor realizes that I have not moved from bed in a week because I get out of breath otherwise . Asthma My background - I was injured at work from a toxic chemical exposure and it took me seeing 6 different doctors ( of all who misdiagnosed me as having asthma ) - until finally I saw a Respiratory Specialist and was diagnosed as having RADS ( Reactive Airways Dysfunction Syndrome ) it mimics asthma but it does NOT respond to traditional asthma med s and in fact they make my breathing worse . Asthma i have just placed a blog under COPD as I was misdiagnosed with COPD and await a different inhaler to help my asthma . Asthma Most doctors are fine with this , sometimes they are so busy they miss things and do not realise that the patient has left the surgery still no wiser about their condition . Asthma my asthma is always flaring up no matter what i do , my doctor missed a chest infection last year which has left closed air pockets in my lungs which means i struggle sometimes . Asthma I do not know why this comes up so much but doctor miss it . Asthma It would not surprise me if many other people have RADS and they have been misdiagnosed or they just think they have become sensitive to things . Asthma I am only ever as low as 300 or so , when my medication is incorrect or I have failed to take it for a few days . Cellulitis I was misdiagnosed because the athletes foot does not usually show up til 3rd 4 th time infection comes back . Cellulitis I am sure your email will help someone just as the other emails helped me when I was in search of answers ( and sympathy ! ) In fact , if my ( US ) doctor reads your email he may learn something as he maintained the drug for over one month while treating me for misdiagnosed Athlete s Foot . Cellulitis After my bug bite it took 2 months of antibiotics for me ( as I was on wrong one being initially misdiagnosed . Cellul

In [0]:
df = sqlContext.sql('''
select t.group, t.text
from `simplified_whole_sentences` as t
where t.errors = 1 and t.sentiment = 1 and t.group = 'Lyme_Disease'
''')
f = df.select("text").collect()
text = ""
for each in f:
  text += each['text'] + " "
  
# r = Rake(ranking_metric=Metric.DEGREE_TO_FREQUENCY_RATIO)
# r = Rake(ranking_metric=Metric.WORD_DEGREE)
# r = Rake(ranking_metric=Metric.WORD_FREQUENCY)
r = Rake(min_length=1, max_length=3, ranking_metric=Metric.WORD_DEGREE)
r.extract_keywords_from_text(text)
r.get_ranked_phrases()

Out[13]: ['many lyme patients',
 'past 6 years',
 'many neuro problems',
 'many gps make',
 'even years later',
 'doctor dismissed lymes',
 'many people',
 'many times',
 'notoriously unreliable test',
 'many others',
 'half years ago',
 'doctor dismissed',
 'many walked',
 'many misdiagnoses',
 'doctors dismissed',
 'doctor really needs',
 'saw doctor today',
 'elisa blood test',
 'doctors office mis',
 '5 years',
 '20 years',
 '2 years',
 'trouble getting treatment',
 'gp also made',
 'doctors dismiss',
 'years',
 'test results',
 'past 6 days',
 'dismissed lymes',
 'wont even acknowledge',
 'hae missed something',
 'diagnosis last week',
 'suffered wrong diagnoses',
 'still feel wrong',
 'someone finally told',
 'lyme disease',
 'know lyme',
 'imperfect test',
 'clear holter monitor',
 'auto immune disease',
 'neuro symptoms',
 'gp missed',
 'gp misdiagnosed',
 'getting quite despirate',
 'doctor',
 'dismissive doctors',
 'wrongly dx bipolar',
 'test',
 'similar rash behind',
 'second episode happened',
 'notoriously unreliable',
 'doxycycline course immediately',
 'treatment early',
 'initial treatment',
 'heart rate went',
 'finally got',
 'even begin',
 'doctors',
 'dismissed',
 'symptoms pop',
 'probably dismiss',
 'prob dismiss',
 'one week',
 'nero symptoms',
 'ineffective testing done',
 'clear mri',
 'clear eeg',
 'awful illness especially',
 'wrongly diagnosed',
 'treatment',
 'suffers also',
 'means patients',
 'maybe something',
 'lyme',
 'diagnosis formed',
 'continual mis',
 'symptoms',
 'sinus pains',
 'recent episode',
 'really helpful',
 'positive results',
 'people end',
 'make sense',
 'immune system',
 'get misdiagnosed',
 'dismiss',
 'blood tests',
 'already know',
 'unreliable',
 'turned away',
 'something',
 'sinus tachycardia',
 'several times',
 'sent away',
 'patients',
 'one shot',
 'mis',
 'medical profession',
 'medical practicioner',
 'got rid',
 'finally',
 'diagnosis',
 'also',
 'treated aggressively',
 'sometimes wonder',
 'results',
 'people',
 'obviously missing',
 'much work',
 'misdiagnosed',
 'long process',
 'ld bacteria',
 'know',
 'idea based',
 'cfs etc',
 '11 months',
 'would presented',
 'whole affair',
 'went',
 'told',
 'today',
 'sure yet',
 'stay informed',
 'stage possibility',
 'somewhat backtrack',
 'similar',
 'severe case',
 'safe route',
 'right place',
 'rash',
 'practice nurse',
 'pounds spent',
 'pituitary etiology',
 'peripheral neuropathy',
 'panic attacks',
 'often happens',
 'norwegian boyfriend',
 'next thursday',
 'nearly year',
 'mental health',
 'made',
 'left untreated',
 'lead us',
 'hyperventilation syndrome',
 'hi guys',
 'hello megan',
 'feel',
 'doxycycline',
 'diagnoses',
 'dental x',
 'ct scan',
 'course',
 'confusing onset',
 'clinical diagnose',
 '2weeks co',
 'wonder',
 'treated',
 'pains',
 'others',
 'much',
 'months',
 'missing',
 'long',
 'ld',
 'idea',
 'diagnosed',
 'cfs',
 'want',
 'unheard',
 'unfortunately',
 'undiagnosed',
 'uk',
 'treat',
 'track',
 'torso',
 'top',
 'time',
 'tick',
 'thrown',
 'three',
 'thousands',
 'though',
 'thinks',
 'thinking',
 'think',
 'thankyou',
 'technician',
 'take',
 'sufferers',
 'suffer',
 'stuff',
 'stress',
 'starting',
 'spoken',
 'sorry',
 'situation',
 'sinusitis',
 'simply',
 'seeing',
 'see',
 'say',
 'result',
 'research',
 'rely',
 'recall',
 'realised',
 'rays',
 'questioning',
 'prescribed',
 'pots',
 'plus',
 'pain',
 'never',
 'neurotic',
 'negative',
 'munchausens',
 'ms',
 'moment',
 'mistaken',
 'misdiagnosis',
 'migraines',
 'mentioned',
 'lots',
 'look',
 'llmd',
 'likely',
 'like',
 'late',
 'knew',
 'knee',
 'keep',
 'job',
 'issue',
 'info',
 'imagine',
 'illnesses',
 'ie',
 'hormones',
 'heard',
 'hear',
 'headaches',
 'great',
 'gotten',
 'going',
 'gerd',
 'figure',
 'fibromyalgia',
 'fell',
 'family',
 'fainting',
 'fact',
 'explanation',
 'everyone',
 'eradication',
 'elimination',
 'driving',
 'doctortors',
 'displayed',
 'depressed',
 'decade',
 'debilitating',
 'dealing',
 'da

In [0]:
%sql
with access as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select access.group,
       num_posts, 
       num_access, 
       ratio_access,
       num_negative_access,
       ratio_negative_in_access,
       ratio_negative_access_over_all,
       (ratio_access * 1.0 / (select sum(ratio_access) from access)) + (ratio_negative_access_over_all * 1.0 / (select sum(ratio_negative_access_over_all) from access)) as composite_index
from access
order by composite_index desc
LIMIT 10

group num_posts num_access ratio_access num_negative_access ratio_negative_in_access ratio_negative_access_over_all composite_index Surgery_and_Anaesthetics 2742 23 0.0083880379285193 10 0.4347826086956522 0.0036469730123997 0.023507 Anticoagulants 4087 38 0.0092977734279423 10 0.2631578947368421 0.0024467824810374 0.020805 Angina 9390 55 0.0058572949946752 36 0.6545454545454545 0.0038338658146965 0.020651 Cervical_Smear_and_Disorders 5336 35 0.0065592203898051 18 0.5142857142857143 0.0033733133433283 0.020098 Hepatitis 1431 10 0.0069881201956674 4 0.4 0.0027952480782669 0.018784 Pilonidal_Sinus 4255 24 0.0056404230317274 14 0.5833333333333333 0.0032902467685076 0.018564 Disc_Prolapse 31536 173 0.0054857940131913 87 0.5028901734104047 0.0027587519025875 0.016603 Lumbar_Puncture 1736 9 0.005184331797235 5 0.5555555555555556 0.0028801843317972 0.01659 Raynauds_Phenomenon 1662 8 0.0048134777376655 5 0.625 0.0030084235860409 0.016503 Deep_Vein_Thrombosis 5015 32 0.0063808574277168 11 0.34375 0.0021934197407777 0.015971

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.001018	0.071867	0.070849
with access_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_in_all_negative,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 0.001018 + 1.0* 0.070849/ 20 then 0.001018 + 1.0* 0.070849/ 20 
            when composite_index < 0.001018 + 2.0* 0.070849/ 20 then 0.001018 + 2.0* 0.070849/ 20
            when composite_index < 0.001018 + 3.0* 0.070849/ 20 then 0.001018 + 3.0* 0.070849/ 20
            when composite_index < 0.001018 + 4.0* 0.070849/ 20 then 0.001018 + 4.0* 0.070849/ 20
            when composite_index < 0.001018 + 5.0* 0.070849/ 20 then 0.001018 + 5.0* 0.070849/ 20
            when composite_index < 0.001018 + 6.0* 0.070849/ 20 then 0.001018 + 6.0* 0.070849/ 20
            when composite_index < 0.001018 + 7.0* 0.070849/ 20 then 0.001018 + 7.0* 0.070849/ 20
            when composite_index < 0.001018 + 8.0* 0.070849/ 20 then 0.001018 + 8.0* 0.070849/ 20
            when composite_index < 0.001018 + 9.0* 0.070849/ 20 then 0.001018 + 9.0* 0.070849/ 20
            when composite_index < 0.001018 + 10.0* 0.070849/ 20 then 0.001018 + 10.0* 0.070849/ 20
            when composite_index < 0.001018 + 11.0* 0.070849/ 20 then 0.001018 + 11.0* 0.070849/ 20
            when composite_index < 0.001018 + 12.0* 0.070849/ 20 then 0.001018 + 12.0* 0.070849/ 20
            when composite_index < 0.001018 + 13.0* 0.070849/ 20 then 0.001018 + 13.0* 0.070849/ 20
            when composite_index < 0.001018 + 14.0* 0.070849/ 20 then 0.001018 + 14.0* 0.070849/ 20
            when composite_index < 0.001018 + 15.0* 0.070849/ 20 then 0.001018 + 15.0* 0.070849/ 20
            when composite_index < 0.001018 + 16.0* 0.070849/ 20 then 0.001018 + 16.0* 0.070849/ 20
            when composite_index < 0.001018 + 17.0* 0.070849/ 20 then 0.001018 + 17.0* 0.070849/ 20
            when composite_index < 0.001018 + 18.0* 0.070849/ 20 then 0.001018 + 18.0* 0.070849/ 20
            when composite_index < 0.001018 + 19.0* 0.070849/ 20 then 0.001018 + 19.0* 0.070849/ 20
            when composite_index <= 0.001018 + 20.0* 0.070849/ 20 then 0.001018 + 20.0* 0.070849/ 20
       end as composite_index_range,
       count(*) as frequency
from(
select access_metrics.group,
         num_posts, 
         num_access, 
         ratio_access,
         num_negative_access,
         ratio_negative_in_access,
         ratio_negative_access_in_all_negative,
         ratio_negative_access_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (1.0 * num_posts / (select sum(num_posts) from access_metrics)) +
         (1.0 * ratio_access  / (select sum(ratio_access) from access_metrics)) + 
         (1.0 * ratio_negative_access_over_all / (select sum(ratio_negative_access_over_all) from access_metrics)) as composite_index
  from access_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.00456045 20 0.0081029 91 0.01164535 77 0.0151878 46 0.01873025 24 0.0222727 8 0.02581515 3 0.0293576 1 0.0364425 1 0.03998495 2 0.04706985 1 0.0506123 1 0.0647821 1 0.071867 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.001018	0.071867	0.070849
with access_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_in_all_negative,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select access_metrics.group,
       num_posts, 
       num_access, 
       ratio_access,
       num_negative_access,
       ratio_negative_in_access,
       ratio_negative_access_in_all_negative,
       ratio_negative_access_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (1.0 * num_posts / (select sum(num_posts) from access_metrics)) +
       (1.0 * ratio_access  / (select sum(ratio_access) from access_metrics)) + 
       (1.0 * ratio_negative_access_over_all / (select sum(ratio_negative_access_over_all) from access_metrics)) as composite_index
from access_metrics
order by composite_index desc


group num_posts num_access ratio_access num_negative_access ratio_negative_in_access ratio_negative_access_in_all_negative ratio_negative_access_over_all composite_index Anxiety_Disorders 526203 544 0.0010338215479577 268 0.4926470588235294 5.093091449498E-4 5.093091449498E-4 0.071867 Hip_Replacement 422127 1143 0.0027077159243545 453 0.3963254593175853 0.0010731367574213 0.0010731367574213 0.062416 Menopause 342523 334 9.751169994424E-4 150 0.4491017964071856 4.379267961568E-4 4.379267961568E-4 0.047546 Polymyalgia_Rheumatica_and_GCA 312978 757 0.0024187003559356 246 0.3249669749009247 7.859977378602E-4 7.859977378602E-4 0.046809 Prostate_Problems 241638 751 0.0031079548746472 212 0.2822902796271638 8.773454506328E-4 8.773454506328E-4 0.038731 Knee_Problems 250359 428 0.0017095450932461 147 0.3434579439252336 5.871568427738E-4 5.871568427738E-4 0.036998 Depression 230756 341 0.0014777513910798 149 0.436950146627566 6.457036870114E-4 6.457036870114E-4 0.034311 Citalopram 186113 145 7.790965703632E-4 53 0.3655172413793103 2.847732291672E-4 2.847732291672E-4 0.026331 Gallbladder_Problems 110324 407 0.0036891338240093 211 0.5184275184275184 0.0019125484935282 0.0019125484935282 0.025773 Surgery_and_Anaesthetics 2742 23 0.0083880379285193 10 0.4347826086956522 0.0036469730123997 0.0036469730123997 0.023865 Abdominal_Disorders 136553 211 0.0015451875828433 106 0.5023696682464455 7.762553733715E-4 7.762553733715E-4 0.022521 Angina 9390 55 0.0058572949946752 36 0.6545454545454545 0.0038338658146965 0.0038338658146965 0.021878 Alcohol_Consumption 116039 329 0.0028352536647162 90 0.2735562310030395 7.756013064573E-4 7.756013064573E-4 0.021607 Anticoagulants 4087 38 0.0092977734279423 10 0.2631578947368421 0.0024467824810374 0.0024467824810374 0.021339 Cervical_Smear_and_Disorders 5336 35 0.0065592203898051 18 0.5142857142857143 0.0033733133433283 0.0033733133433283 0.020795 Disc_Prolapse 31536 173 0.0054857940131913 87 0.5028901734104047 0.0027587519025875 0.0027587519025875 0.020725 Fibromyalgia_Syndrome 104012 202 0.0019420836057378 93 0.4603960396039604 8.941276006615E-4 8.941276006615E-4 0.0192 Pilonidal_Sinus 4255 24 0.0056404230317274 14 0.5833333333333333 0.0032902467685076 0.0032902467685076 0.01912 Hepatitis 1431 10 0.0069881201956674 4 0.4 0.0027952480782669 0.0027952480782669 0.018971 Lichen_Sclerosus 102644 197 0.0019192549004326 70 0.3553299492385787 6.819687463466E-4 6.819687463466E-4 0.018292 Ovarian_Cyst 53101 202 0.0038040714864127 93 0.4603960396039604 0.0017513794467148 0.0017513794467148 0.017921 Uterine_Fibroids 45181 203 0.0044930391093601 79 0.3891625615763547 0.0017485226090613 0.0017485226090613 0.017822 Reflux_Oesophagitis 99149 191 0.0019263936096178 65 0.3403141361256545 6.555789770951E-4 6.555789770951E-4 0.017759 Mirtazapine 94010 187 0.0019891500904159 60 0.320855614973262 6.382299755345E-4 6.382299755345E-4 0.017116 Hypothyroidism 74189 185 0.0024936311312998 90 0.4864864864864865 0.0012131178476594 0.0012131178476594 0.017109 Chronic_Fatigue_Syndrome 104500 126 0.0012057416267943 50 0.3968253968253968 4.784688995215E-4 4.784688995215E-4 0.016886 Cervical_Spondylosis 23036 100 0.0043410314290675 55 0.55 0.0023875672859872 0.0023875672859872 0.016823 Lumbar_Puncture 1736 9 0.005184331797235 5 0.5555555555555556 0.0028801843317972 0.0028801843317972 0.016817 Raynauds_Phenomenon 1662 8 0.0048134777376655 5 0.625 0.0030084235860409 0.0030084235860409 0.01672 Deep_Vein_Thrombosis 5015 32 0.0063808574277168 11 0.34375 0.0021934197407777 0.0021934197407777 0.016626 Sertraline 107756 107 9.929841493745E-4 38 0.3551401869158879 3.526485764134E-4 3.526485764134E-4 0.016605 Cataract 71526 226 0.0031596901825909 58 0.2566371681415929 8.108939406649E-4 8.108939406649E-4 0.01635 Genitourinary_Prolapse 67867 187 0.0027553892171453 76 0.4064171122994652 0.0011198373288933 0.0011198373288933 0.016335 Vitiligo 1400 9 0.0064285714285714 3 0.3333333333333333 0.0021428571428571 0.0021428571428571 0.016053 HRT_Hormone_Replace

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.000792	0.023507	0.022715
with access_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_in_all_negative,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 0.000792 + 1.0* 0.022715/ 20 then 0.000792 + 1.0* 0.022715/ 20 
            when composite_index < 0.000792 + 2.0* 0.022715/ 20 then 0.000792 + 2.0* 0.022715/ 20
            when composite_index < 0.000792 + 3.0* 0.022715/ 20 then 0.000792 + 3.0* 0.022715/ 20
            when composite_index < 0.000792 + 4.0* 0.022715 / 20 then 0.000792 + 4.0* 0.022715/ 20
            when composite_index < 0.000792 + 5.0* 0.022715/ 20 then 0.000792 + 5.0* 0.022715/ 20
            when composite_index < 0.000792 + 6.0* 0.022715/ 20 then 0.000792 + 6.0* 0.022715 / 20
            when composite_index < 0.000792 + 7.0* 0.022715/ 20 then 0.000792 + 7.0* 0.022715/ 20
            when composite_index < 0.000792 + 8.0* 0.022715/ 20 then 0.000792 + 8.0* 0.022715/ 20
            when composite_index < 0.000792 + 9.0* 0.022715/ 20 then 0.000792 + 9.0* 0.022715/ 20
            when composite_index < 0.000792 + 10.0* 0.022715/ 20 then 0.000792 + 10.0* 0.022715/ 20
            when composite_index < 0.000792 + 11.0* 0.022715/ 20 then 0.000792 + 11.0* 0.022715/ 20
            when composite_index < 0.000792 + 12.0* 0.022715/ 20 then 0.000792 + 12.0* 0.022715/ 20
            when composite_index < 0.000792 + 13.0* 0.022715/ 20 then 0.000792 + 13.0* 0.022715/ 20
            when composite_index < 0.000792 + 14.0* 0.022715/ 20 then 0.000792 + 14.0* 0.022715/ 20
            when composite_index < 0.000792 + 15.0* 0.022715/ 20 then 0.000792 + 15.0* 0.022715/ 20
            when composite_index < 0.000792 + 16.0* 0.022715/ 20 then 0.000792 + 16.0* 0.022715/ 20
            when composite_index < 0.000792 + 17.0* 0.022715/ 20 then 0.000792 + 17.0* 0.022715/ 20
            when composite_index < 0.000792 + 18.0* 0.022715/ 20 then 0.000792 + 18.0* 0.022715/ 20
            when composite_index < 0.000792 + 19.0* 0.022715/ 20 then 0.000792 + 19.0* 0.022715/ 20
            when composite_index <= 0.000792 + 20.0* 0.022715/ 20 then 0.000792 + 20.0* 0.022715/ 20
       end as composite_index_range,
       count(*) as frequency
from(
select access_metrics.group,
         num_posts, 
         num_access, 
         ratio_access,
         num_negative_access,
         ratio_negative_in_access,
         ratio_negative_access_in_all_negative,
         ratio_negative_access_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from access_metrics)) +
         (1.0 * ratio_access  / (select sum(ratio_access) from access_metrics)) + 
         (1.0 * ratio_negative_access_over_all / (select sum(ratio_negative_access_over_all) from access_metrics)) as composite_index
  from access_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 0.00192775 10 0.0030635 17 0.00419925 28 0.005335 35 0.00647075 44 0.0076065 43 0.00874225 24 0.009878 20 0.01101375 14 0.0121495 13 0.01328525 9 0.014421 9 0.0166925 5 0.018964 2 0.02009975 1 0.0212355 2 0.023507 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.001018	0.071867	0.070849
with access_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_in_all_negative,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select access_metrics.group,
       num_posts, 
       num_access, 
       ratio_access,
       num_negative_access,
       ratio_negative_in_access,
       ratio_negative_access_in_all_negative,
       ratio_negative_access_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from access_metrics)) +
       (1.0 * ratio_access  / (select sum(ratio_access) from access_metrics)) + 
       (1.0 * ratio_negative_access_over_all / (select sum(ratio_negative_access_over_all) from access_metrics)) as composite_index
from access_metrics
order by composite_index desc


group num_posts num_access ratio_access num_negative_access ratio_negative_in_access ratio_negative_access_in_all_negative ratio_negative_access_over_all composite_index Surgery_and_Anaesthetics 2742 23 0.0083880379285193 10 0.4347826086956522 0.0036469730123997 0.0036469730123997 0.023507 Anticoagulants 4087 38 0.0092977734279423 10 0.2631578947368421 0.0024467824810374 0.0024467824810374 0.020805 Angina 9390 55 0.0058572949946752 36 0.6545454545454545 0.0038338658146965 0.0038338658146965 0.020651 Cervical_Smear_and_Disorders 5336 35 0.0065592203898051 18 0.5142857142857143 0.0033733133433283 0.0033733133433283 0.020098 Hepatitis 1431 10 0.0069881201956674 4 0.4 0.0027952480782669 0.0027952480782669 0.018784 Pilonidal_Sinus 4255 24 0.0056404230317274 14 0.5833333333333333 0.0032902467685076 0.0032902467685076 0.018564 Disc_Prolapse 31536 173 0.0054857940131913 87 0.5028901734104047 0.0027587519025875 0.0027587519025875 0.016603 Lumbar_Puncture 1736 9 0.005184331797235 5 0.5555555555555556 0.0028801843317972 0.0028801843317972 0.01659 Raynauds_Phenomenon 1662 8 0.0048134777376655 5 0.625 0.0030084235860409 0.0030084235860409 0.016503 Deep_Vein_Thrombosis 5015 32 0.0063808574277168 11 0.34375 0.0021934197407777 0.0021934197407777 0.015971 Vitiligo 1400 9 0.0064285714285714 3 0.3333333333333333 0.0021428571428571 0.0021428571428571 0.01587 Psoriasis_and_Psoriatic_Arthritis 10695 56 0.0052360916316036 23 0.4107142857142857 0.0021505376344086 0.0021505376344086 0.01426 Lyme_Disease 11216 47 0.0041904422253923 29 0.6170212765957447 0.0025855920114123 0.0025855920114123 0.014256 Hemifacial_Spasm 8256 50 0.0060562015503876 14 0.28 0.0016957364341085 0.0016957364341085 0.013888 Cervical_Spondylosis 23036 100 0.0043410314290675 55 0.55 0.0023875672859872 0.0023875672859872 0.013812 HRT_Hormone_Replacement_Therapy 17492 101 0.0057740681454379 31 0.3069306930693069 0.0017722387377087 0.0017722387377087 0.013753 Varicose_Vein 2239 15 0.0066994193836534 3 0.2 0.0013398838767307 0.0013398838767307 0.013599 Rhinitis 4431 27 0.006093432633717 7 0.2592592592592593 0.0015797788309637 0.0015797788309637 0.013557 Pulmonary_Fibrosis 7119 36 0.0050568900126422 14 0.3888888888888889 0.0019665683382498 0.0019665683382498 0.013408 Acne 3362 16 0.0047590719809637 7 0.4375 0.0020820939916716 0.0020820939916716 0.013379 Statins_and_Other_Lipid_lowering_Medicines 15127 61 0.004032524624843 35 0.5737704918032787 0.002313743637205 0.002313743637205 0.013146 Weight_Loss_Intentional 9490 57 0.0060063224446786 14 0.2456140350877193 0.0014752370916754 0.0014752370916754 0.013093 Osteoporosis_and_Osteopenia 19528 82 0.0041990987300287 41 0.5 0.0020995493650143 0.0020995493650143 0.012669 Urinary_Incontinence 7059 29 0.0041082306275676 15 0.5172413793103448 0.0021249468763281 0.0021249468763281 0.012628 Wolff_Parkinson_White_Syndrome 956 4 0.00418410041841 2 0.5 0.002092050209205 0.002092050209205 0.012624 Opiates_And_Opioids 12290 48 0.0039056143205858 27 0.5625 0.0021969080553295 0.0021969080553295 0.012587 Urethral_Disorders 8723 41 0.0047002178149719 16 0.3902439024390244 0.0018342313424281 0.0018342313424281 0.012484 Levothyroxine_Sodium 9399 35 0.0037238004042983 21 0.6 0.002234280242579 0.002234280242579 0.01246 Dementia 3444 12 0.0034843205574913 8 0.6666666666666667 0.0023228803716609 0.0023228803716609 0.012424 Hernia 29611 123 0.0041538617405694 58 0.4715447154471545 0.0019587315524636 0.0019587315524636 0.012143 Polycythaemia_Rubra_Vera 17976 94 0.0052291944815309 27 0.2872340425531915 0.001502002670227 0.001502002670227 0.012116 Stroke_and_TIA 7872 35 0.0044461382113821 14 0.4 0.0017784552845528 0.0017784552845528 0.011951 Uterine_Fibroids 45181 203 0.0044930391093601 79 0.3891625615763547 0.0017485226090613 0.0017485226090613 0.011917 Crohns_Disease 16784 73 0.0043493803622498 30 0.410958904109589 0.0017874165872259 0.0017874165872259 0.011848 Sciatica 13788 56 0.0040615027560197 26 0.4642857142857143 0.001885697708152 0.001885697708152 0.011776 Co

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0	0.012616	0.012616
with access_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_in_all_negative,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.012616 / 20 then 1.0* 0.012616 / 20 
            when composite_index < 2.0* 0.012616 / 20 then 2.0* 0.012616 / 20
            when composite_index < 3.0* 0.012616 / 20 then 3.0* 0.012616 / 20
            when composite_index < 4.0* 0.012616/ 20 then 4.0* 0.012616 / 20
            when composite_index < 5.0* 0.012616 / 20 then 5.0* 0.012616 / 20
            when composite_index < 6.0* 0.012616 / 20 then 6.0* 0.012616 / 20
            when composite_index < 7.0* 0.012616 / 20 then 7.0* 0.012616 / 20
            when composite_index < 8.0* 0.012616 / 20 then 8.0* 0.012616 / 20
            when composite_index < 9.0* 0.012616 / 20 then 9.0* 0.012616 / 20
            when composite_index < 10.0* 0.012616 / 20 then 10.0* 0.012616 / 20
            when composite_index < 11.0* 0.012616 / 20 then 11.0* 0.012616 / 20
            when composite_index < 12.0* 0.012616 / 20 then 12.0* 0.012616 / 20
            when composite_index < 13.0* 0.012616 / 20 then 13.0* 0.012616 / 20
            when composite_index < 14.0* 0.012616 / 20 then 14.0* 0.012616 / 20
            when composite_index < 15.0* 0.012616 / 20 then 15.0* 0.012616 / 20
            when composite_index < 16.0* 0.012616 / 20 then 16.0* 0.012616 / 20
            when composite_index < 17.0* 0.012616 / 20 then 17.0* 0.012616 / 20
            when composite_index < 18.0* 0.012616 / 20 then 18.0* 0.012616 / 20
            when composite_index < 19.0* 0.012616 / 20 then 19.0* 0.012616 / 20
            when composite_index <= 20.0* 0.012616 / 20 then 20.0* 0.012616 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select access_metrics.group,
         num_posts, 
         num_access, 
         ratio_access,
         num_negative_access,
         ratio_negative_in_access,
         ratio_negative_access_in_all_negative,
         ratio_negative_access_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from access_metrics)) +
         (0.0 * ratio_access  / (select sum(ratio_access) from access_metrics)) + 
         (1.0 * ratio_negative_access_over_all / (select sum(ratio_negative_access_over_all) from access_metrics)) as composite_index
  from access_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency 6.308E-4 13 0.0012616 14 0.0018924 26 0.0025232 41 0.003154 34 0.0037848 46 0.0044156 25 0.0050464 17 0.0056772 18 0.006308 13 0.0069388 10 0.0075696 7 0.0082004 4 0.0088312 1 0.009462 2 0.0100928 2 0.0113544 2 0.012616 2

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.001018	0.071867	0.070849
with access_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_in_all_negative,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select access_metrics.group,
       num_posts, 
       num_access, 
       ratio_access,
       num_negative_access,
       ratio_negative_in_access,
       ratio_negative_access_in_all_negative,
       ratio_negative_access_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from access_metrics)) +
       (0.0 * ratio_access  / (select sum(ratio_access) from access_metrics)) + 
       (1.0 * ratio_negative_access_over_all / (select sum(ratio_negative_access_over_all) from access_metrics)) as composite_index
from access_metrics
order by composite_index desc


group num_posts num_access ratio_access num_negative_access ratio_negative_in_access ratio_negative_access_in_all_negative ratio_negative_access_over_all composite_index Angina 9390 55 0.0058572949946752 36 0.6545454545454545 0.0038338658146965 0.0038338658146965 0.012616 Surgery_and_Anaesthetics 2742 23 0.0083880379285193 10 0.4347826086956522 0.0036469730123997 0.0036469730123997 0.012001 Cervical_Smear_and_Disorders 5336 35 0.0065592203898051 18 0.5142857142857143 0.0033733133433283 0.0033733133433283 0.0111 Pilonidal_Sinus 4255 24 0.0056404230317274 14 0.5833333333333333 0.0032902467685076 0.0032902467685076 0.010827 Raynauds_Phenomenon 1662 8 0.0048134777376655 5 0.625 0.0030084235860409 0.0030084235860409 0.0099 Lumbar_Puncture 1736 9 0.005184331797235 5 0.5555555555555556 0.0028801843317972 0.0028801843317972 0.009478 Hepatitis 1431 10 0.0069881201956674 4 0.4 0.0027952480782669 0.0027952480782669 0.009198 Disc_Prolapse 31536 173 0.0054857940131913 87 0.5028901734104047 0.0027587519025875 0.0027587519025875 0.009078 Lyme_Disease 11216 47 0.0041904422253923 29 0.6170212765957447 0.0025855920114123 0.0025855920114123 0.008508 Anticoagulants 4087 38 0.0092977734279423 10 0.2631578947368421 0.0024467824810374 0.0024467824810374 0.008051 Cervical_Spondylosis 23036 100 0.0043410314290675 55 0.55 0.0023875672859872 0.0023875672859872 0.007857 Dementia 3444 12 0.0034843205574913 8 0.6666666666666667 0.0023228803716609 0.0023228803716609 0.007644 Statins_and_Other_Lipid_lowering_Medicines 15127 61 0.004032524624843 35 0.5737704918032787 0.002313743637205 0.002313743637205 0.007614 Levothyroxine_Sodium 9399 35 0.0037238004042983 21 0.6 0.002234280242579 0.002234280242579 0.007352 Opiates_And_Opioids 12290 48 0.0039056143205858 27 0.5625 0.0021969080553295 0.0021969080553295 0.007229 Deep_Vein_Thrombosis 5015 32 0.0063808574277168 11 0.34375 0.0021934197407777 0.0021934197407777 0.007218 Alzheimers_Disease 1390 3 0.002158273381295 3 1.0 0.002158273381295 0.002158273381295 0.007102 Psoriasis_and_Psoriatic_Arthritis 10695 56 0.0052360916316036 23 0.4107142857142857 0.0021505376344086 0.0021505376344086 0.007077 Vitiligo 1400 9 0.0064285714285714 3 0.3333333333333333 0.0021428571428571 0.0021428571428571 0.007051 Urinary_Incontinence 7059 29 0.0041082306275676 15 0.5172413793103448 0.0021249468763281 0.0021249468763281 0.006992 Osteoporosis_and_Osteopenia 19528 82 0.0041990987300287 41 0.5 0.0020995493650143 0.0020995493650143 0.006909 Wolff_Parkinson_White_Syndrome 956 4 0.00418410041841 2 0.5 0.002092050209205 0.002092050209205 0.006884 Acne 3362 16 0.0047590719809637 7 0.4375 0.0020820939916716 0.0020820939916716 0.006851 Idiopathic_Intracranial_Hypertension 3527 12 0.0034023249220301 7 0.5833333333333333 0.0019846895378509 0.0019846895378509 0.006531 Testicular_Pain_and_Disorders 5063 15 0.0029626703535453 10 0.6666666666666667 0.0019751135690302 0.0019751135690302 0.006499 Pulmonary_Fibrosis 7119 36 0.0050568900126422 14 0.3888888888888889 0.0019665683382498 0.0019665683382498 0.006471 Hernia 29611 123 0.0041538617405694 58 0.4715447154471545 0.0019587315524636 0.0019587315524636 0.006445 Bowel_Disorders 10766 39 0.0036225153260264 21 0.5384615384615385 0.0019505851755527 0.0019505851755527 0.006419 Antibiotics 3111 8 0.0025715204114433 6 0.75 0.0019286403085824 0.0019286403085824 0.006346 Angiotensin_II_Receptor_Blockers 3648 11 0.003015350877193 7 0.6363636363636364 0.0019188596491228 0.0019188596491228 0.006314 Gallbladder_Problems 110324 407 0.0036891338240093 211 0.5184275184275184 0.0019125484935282 0.0019125484935282 0.006293 Sciatica 13788 56 0.0040615027560197 26 0.4642857142857143 0.001885697708152 0.001885697708152 0.006205 Urethral_Disorders 8723 41 0.0047002178149719 16 0.3902439024390244 0.0018342313424281 0.0018342313424281 0.006036 Codeine_and_Paracetamol_Co_codamol 15968 49 0.0030686372745491 29 0.5918367346938777 0.0018161322645291 0.0018161322645291 0.005976 Pernicious_Anaemia 19906 82 0.0041193609966844 36 0.

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0	0.012616	0.012616
with access_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_in_all_negative,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select case when composite_index < 1.0* 0.012616 / 20 then 1.0* 0.012616 / 20 
            when composite_index < 2.0* 0.012616 / 20 then 2.0* 0.012616 / 20
            when composite_index < 3.0* 0.012616 / 20 then 3.0* 0.012616 / 20
            when composite_index < 4.0* 0.012616/ 20 then 4.0* 0.012616 / 20
            when composite_index < 5.0* 0.012616 / 20 then 5.0* 0.012616 / 20
            when composite_index < 6.0* 0.012616 / 20 then 6.0* 0.012616 / 20
            when composite_index < 7.0* 0.012616 / 20 then 7.0* 0.012616 / 20
            when composite_index < 8.0* 0.012616 / 20 then 8.0* 0.012616 / 20
            when composite_index < 9.0* 0.012616 / 20 then 9.0* 0.012616 / 20
            when composite_index < 10.0* 0.012616 / 20 then 10.0* 0.012616 / 20
            when composite_index < 11.0* 0.012616 / 20 then 11.0* 0.012616 / 20
            when composite_index < 12.0* 0.012616 / 20 then 12.0* 0.012616 / 20
            when composite_index < 13.0* 0.012616 / 20 then 13.0* 0.012616 / 20
            when composite_index < 14.0* 0.012616 / 20 then 14.0* 0.012616 / 20
            when composite_index < 15.0* 0.012616 / 20 then 15.0* 0.012616 / 20
            when composite_index < 16.0* 0.012616 / 20 then 16.0* 0.012616 / 20
            when composite_index < 17.0* 0.012616 / 20 then 17.0* 0.012616 / 20
            when composite_index < 18.0* 0.012616 / 20 then 18.0* 0.012616 / 20
            when composite_index < 19.0* 0.012616 / 20 then 19.0* 0.012616 / 20
            when composite_index <= 20.0* 0.012616 / 20 then 20.0* 0.012616 / 20
       end as composite_index_range,
       count(*) as frequency
from(
select access_metrics.group,
         num_posts, 
         num_access, 
         ratio_access,
         num_negative_access,
         ratio_negative_in_access,
         ratio_negative_access_in_all_negative,
         ratio_negative_access_over_all,
         -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
         (0.0 * num_posts / (select sum(num_posts) from access_metrics)) +
         (1.0 * ratio_access  / (select sum(ratio_access) from access_metrics)) + 
         (0.0 * ratio_negative_access_over_all / (select sum(ratio_negative_access_over_all) from access_metrics)) as composite_index
  from access_metrics
  order by composite_index
)
group by composite_index_range
order by composite_index_range

composite_index_range frequency null 1 6.308E-4 2 0.0012616 12 0.0018924 30 0.0025232 43 0.003154 40 0.0037848 49 0.0044156 30 0.0050464 21 0.0056772 12 0.006308 14 0.0069388 6 0.0075696 5 0.0082004 3 0.0088312 5 0.009462 2 0.0100928 1 0.0119852 1

In [0]:
%sql
/* Query the created temp table in a SQL cell */
-- 0.001018	0.071867	0.070849
with access_metrics as
(
select t.group, count(*) as num_posts, 
sum(case when t.access = 1 then 1 else 0 end) as num_access,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as ratio_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end) as num_negative_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / sum(case when t.access = 1 then 1 else 0 end) as ratio_negative_in_access,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_in_all_negative,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as ratio_negative_access_over_all
from `simplified_whole_sentences` as t
group by t.group
)
select access_metrics.group,
       num_posts, 
       num_access, 
       ratio_access,
       num_negative_access,
       ratio_negative_in_access,
       ratio_negative_access_in_all_negative,
       ratio_negative_access_over_all,
       -- takes the size of disease, size of the topic issue, and sevrity of the topic into account as an additional index
       (0.0 * num_posts / (select sum(num_posts) from access_metrics)) +
       (1.0 * ratio_access  / (select sum(ratio_access) from access_metrics)) + 
       (0.0 * ratio_negative_access_over_all / (select sum(ratio_negative_access_over_all) from access_metrics)) as composite_index
from access_metrics
order by composite_index desc


group num_posts num_access ratio_access num_negative_access ratio_negative_in_access ratio_negative_access_in_all_negative ratio_negative_access_over_all composite_index Anticoagulants 4087 38 0.0092977734279423 10 0.2631578947368421 0.0024467824810374 0.0024467824810374 0.012754 Surgery_and_Anaesthetics 2742 23 0.0083880379285193 10 0.4347826086956522 0.0036469730123997 0.0036469730123997 0.011506 Hepatitis 1431 10 0.0069881201956674 4 0.4 0.0027952480782669 0.0027952480782669 0.009586 Varicose_Vein 2239 15 0.0066994193836534 3 0.2 0.0013398838767307 0.0013398838767307 0.00919 Cervical_Smear_and_Disorders 5336 35 0.0065592203898051 18 0.5142857142857143 0.0033733133433283 0.0033733133433283 0.008998 Vitiligo 1400 9 0.0064285714285714 3 0.3333333333333333 0.0021428571428571 0.0021428571428571 0.008819 Deep_Vein_Thrombosis 5015 32 0.0063808574277168 11 0.34375 0.0021934197407777 0.0021934197407777 0.008753 Rhinitis 4431 27 0.006093432633717 7 0.2592592592592593 0.0015797788309637 0.0015797788309637 0.008359 Hemifacial_Spasm 8256 50 0.0060562015503876 14 0.28 0.0016957364341085 0.0016957364341085 0.008308 Weight_Loss_Intentional 9490 57 0.0060063224446786 14 0.2456140350877193 0.0014752370916754 0.0014752370916754 0.008239 Angina 9390 55 0.0058572949946752 36 0.6545454545454545 0.0038338658146965 0.0038338658146965 0.008035 HRT_Hormone_Replacement_Therapy 17492 101 0.0057740681454379 31 0.3069306930693069 0.0017722387377087 0.0017722387377087 0.007921 Pilonidal_Sinus 4255 24 0.0056404230317274 14 0.5833333333333333 0.0032902467685076 0.0032902467685076 0.007737 Disc_Prolapse 31536 173 0.0054857940131913 87 0.5028901734104047 0.0027587519025875 0.0027587519025875 0.007525 Prostate_Cancer 31848 171 0.0053692539562924 36 0.2105263157894737 0.0011303692539563 0.0011303692539563 0.007365 Psoriasis_and_Psoriatic_Arthritis 10695 56 0.0052360916316036 23 0.4107142857142857 0.0021505376344086 0.0021505376344086 0.007183 Polycythaemia_Rubra_Vera 17976 94 0.0052291944815309 27 0.2872340425531915 0.001502002670227 0.001502002670227 0.007173 Lumbar_Puncture 1736 9 0.005184331797235 5 0.5555555555555556 0.0028801843317972 0.0028801843317972 0.007112 Pulmonary_Fibrosis 7119 36 0.0050568900126422 14 0.3888888888888889 0.0019665683382498 0.0019665683382498 0.006937 Spleen_Disorders_and_Splenectomy 1012 5 0.0049407114624506 1 0.2 9.881422924901E-4 9.881422924901E-4 0.006778 Warts_And_Verrucas 814 4 0.0049140049140049 0 0.0 0.0 0.0 0.006741 Raynauds_Phenomenon 1662 8 0.0048134777376655 5 0.625 0.0030084235860409 0.0030084235860409 0.006603 Acne 3362 16 0.0047590719809637 7 0.4375 0.0020820939916716 0.0020820939916716 0.006528 Urethral_Disorders 8723 41 0.0047002178149719 16 0.3902439024390244 0.0018342313424281 0.0018342313424281 0.006448 Uterine_Fibroids 45181 203 0.0044930391093601 79 0.3891625615763547 0.0017485226090613 0.0017485226090613 0.006163 Stroke_and_TIA 7872 35 0.0044461382113821 14 0.4 0.0017784552845528 0.0017784552845528 0.006099 Atrial_Fibrillation_And_Flutter 29842 132 0.0044232960257355 42 0.3181818181818182 0.0014074123718249 0.0014074123718249 0.006068 Colonoscopy 16731 73 0.0043631582093121 29 0.3972602739726027 0.0017333094256171 0.0017333094256171 0.005985 Scoliosis_and_Kyphosis 4827 21 0.0043505282784338 8 0.380952380952381 0.00165734410607 0.00165734410607 0.005968 Crohns_Disease 16784 73 0.0043493803622498 30 0.410958904109589 0.0017874165872259 0.0017874165872259 0.005966 Cervical_Spondylosis 23036 100 0.0043410314290675 55 0.55 0.0023875672859872 0.0023875672859872 0.005955 Cardiovascular_Disorders 26166 112 0.0042803638309256 37 0.3303571428571429 0.0014140487655736 0.0014140487655736 0.005872 Osteoporosis_and_Osteopenia 19528 82 0.0041990987300287 41 0.5 0.0020995493650143 0.0020995493650143 0.00576 Lyme_Disease 11216 47 0.0041904422253923 29 0.6170212765957447 0.0025855920114123 0.0025855920114123 0.005748 Wolff_Parkinson_White_Syndrome 956 4 0.00418410041841 2 0.5 0.002092050209205 0.002092050209205 0.00574 Glaucom

In [0]:
%sql
-- Cervical_Spondylosis, Surgery_and_Anaesthetics
select t.group, t.text
from `simplified_whole_sentences` as t
where t.access = 1 and t.sentiment = 1 and 
(t.group = 'Surgery_and_Anaesthetics' or 
t.group = "Anticoagulants" or 
t.group = "Angina" or 
t.group = "Cervical_Smear_and_Disorders" or 
t.group = "Hepatitis" or 
t.group = "Pilonidal_Sinus" or 
t.group = "Raynauds_Phenomenon" or 
t.group = "Lumbar_Puncture" or 
t.group = "Disc_Prolapse" or 
t.group = "Deep_Vein_Thrombosis" or 
t.group = "Hepatitis" or 
t.group = "Lyme_Disease" or 
t.group = "Cervical_Spondylosis" or 
t.group = "Dementia" or 
t.group = "Statins_and_Other_Lipid_lowering_Medicines" or 
t.group = "Levothyroxine_Sodium" or 
t.group = "Opiates_And_Opioids" or 
t.group = "Varicose_Vein" or 
t.group = "Vitiligo" or 
t.group = "Rhinitis" or 
t.group = "Hemifacial_Spasm" or 
t.group = "Weight_Loss_Intentional" or 
t.group = "HRT_Hormone_Replacement_Therapy" or 
t.group = "Prostate_Cancer")
order by t.group

group text Angina I was diagnosed with MVD about 10-12 years ago , MVD is the small blood vessels in your heart that can not be seen by the naked eye even via catheterization ( Angiogram ) and it does not show up on an ECG ( EKG ) , it is a very painful thing and gives off angina like symptoms there are medications available but will not fix the problem , unfortunately there is no cure for MVD or Prinzmetal Angina , my coronary arteries have started to spasm now hence the new diagnosis , I have had 2 NSTEMI s due to Angina Now strangely enough I heard the exact same explanation by another doctor to another patient 6 days ago , we must be the unlucky numbers or they have stuffed their research up Now I am almost positive it was Cathy McPhee that put me onto this , I have to look the name of the procedure up , it is mentioned in this discussion , I asked my cardiologist about this procedure and I was told it is not available here I would have to travel to the USA or the UK to seek out a surgeon that performs this procedure Angina March 2017 my heart imploded , I refused treatment in the ambulance because they could never catch it in action , I let it go to far . Angina I looked up the medicine of course it is not available here . Angina they say to me we do not perform those procedures they are either outdated and do not work or we do not have the surgeons available to do those procedures . Angina Quick update ! I went into hospital for my bypass on the 31st May but after taking the pre-med the op was cancelled as the person before me took longer than expected . Angina Hi , ? There are tests available for cardiologists to make informed decisions or diagnosis to angina , however , in saying that there a 3-4 different types of angina that is very hard to diagnose . Angina I was suppose to have another stress test but I refused because I only had one mid last year and as the cardio s say . Angina hence my refusal to have another stress test . Angina Hi Fella s , Long time no hear , hope all is going as well as expected for you all ? I have had nothing but trouble with my PM angina as well for the last 18 months , triggers are high emotional stress and now our winter , this week alone I have 3 visits to ED ( ER ) via ambulance , twice in one day because one ED doctor refused pain relief and refused to release 2-3 tablets to see me through to the next day when I had an appointment with my GP to get a new script . Angina I had to have words with my cardiologist about pain relief as these new doctors were refusing the endone usually given , I think they were thinking along the lines of a drug seeker Pfft when I have endone at home it keeps me out of the ED , it is just that I have been instructed to call for an ambulance if pain returns after taking 2 endone tablets 3-4 hours after taking the first one or my chest pain increases even with pain relief , you know , the usual heart attack symptoms , I have had to do this Angina give adequate pain relief now I am sure you can guess what some doctors consider adequate pain relief ? so now I have to have another word in my cardiologists ear because of this doctor this week refusing me opioid pain relief because Panadol does not work , ibuprofen nurofen . Angina I have not been able to access many procedures becase the anaethetists insurance companies bwo nt take the risk , having to have investigations treatments not cardiac abroad . Angina Hi frank , Sounds awfully simiilar to my cardiologists here , I was the same , I was getting chest pain for no apparent reason , had a cholsterol test done , was off the charts , dangerously off the charts , was put onto a statin it helped with the total cholesterol but triglycerides were still high and I had all the severe side effects of any statins available even the old fashioned questron powder so statins are a no - no for me , because my cholestrol was high the cardiologist wanted to see what Angina Two weeks ago he went for the stress test , but th

In [0]:
df = sqlContext.sql('''
select t.group, t.text
from `simplified_whole_sentences` as t
where t.delays = 1 and t.sentiment = 1 and 
(t.group = 'Kidney_Failure_and_CKD' or 
 t.group = 'Kidney_Stones' or 
 t.group = 'Kidney_Problems')
order by t.group
''')
f = df.select("text").collect()
text = ""
for each in f:
  text += each['text'] + " "
  
# r = Rake(ranking_metric=Metric.DEGREE_TO_FREQUENCY_RATIO)
# r = Rake(ranking_metric=Metric.WORD_DEGREE)
# r = Rake(ranking_metric=Metric.WORD_FREQUENCY)
r = Rake(min_length=1, max_length=5, ranking_metric=Metric.WORD_DEGREE)
r.extract_keywords_from_text(text)
r.get_ranked_phrases()

Out[11]: ['three weeks still waiting',
 'wait another three weeks',
 '6 8 week waiting list',
 'kidney stone waiting',
 'first time 2 weeks ago',
 'waiting 4 weeks',
 'wait another week',
 'wait 3 weeks',
 '6 8 week wait',
 '2 weeks time',
 'got heart scan next week',
 'long waiting list',
 'initially told 3 weeks',
 'waiting months',
 'wait 2 months',
 'still waiting',
 'done another urine test',
 'waiting time',
 'kidney stone',
 'another stone 6mm',
 '2 weeks',
 'waiting list',
 'bone marrow biopsy yesterday hope',
 'worry waiting though',
 'another stone',
 'another blood test',
 '6 weeks',
 '3 weeks',
 'kidney doctor',
 'decreased kidney function due',
 'stone oct 2014 urologist',
 'ultrasound june 2014 ultrasound revealed',
 'moment waiting',
 'waiting game',
 'easy waiting',
 'currently waiting',
 '5 weeks',
 'still havnt got even',
 'doctors last week',
 'waiting',
 'feeling unwell pain',
 '12 weeks',
 'extremely large stone called',
 'repeated next week',
 'left kidney',
 'worst three months',
 'one kidney',
 'kidney specialist',
 'chest xray im worried',
 'long wait',
 'kidney stones',
 'feeling really tired',
 'bone marrow biopsy',
 'worried doctor',
 'kidney problems',
 'guess another reason',
 'awaiting another operation',
 'would often get similar',
 'kidney removed',
 'kidney disease',
 'allow kidney',
 'large stone',
 '9mm stone impacted',
 'still feel fine',
 'kidney',
 '3 months',
 '150mg ranitidine plus peptic liquid',
 'doctor felt concerned',
 'doctor delays removal',
 'biopsy full report',
 'water retention even though',
 'wait till',
 'really got',
 'calling doctor tomorrow',
 'worst pain',
 'mouth terrible pains yesterday',
 'long time',
 'come back bad',
 'blood test',
 'wait',
 'take months',
 'severe pain',
 'next appointment',
 'intense tingling feeling',
 'first appointment',
 'doctor phoned',
 'took biopsy',
 'would get',
 'urine test',
 'really hope',
 'pain relief',
 'pain killers',
 'pain became',
 'doctors seem pretty clueless',
 'doctor decided',
 'constant pain',
 'back plus stinging',
 'awful pain',
 '5mg bit worried',
 'sufficiently worried enough',
 'months sad',
 'feeling well',
 'extra tablet works ive',
 'eight months',
 'could cause complications',
 '2 stones',
 'pain',
 'feeling sick',
 'feeling shocked',
 'doctor',
 'bloody biopsy',
 '10 minutes appointment',
 'months',
 'come back',
 'test results',
 'shock completely changed diet',
 'full skeletal xray',
 'feeling',
 'biopsy',
 'renal function deteriorate',
 'last posted update',
 'could see',
 'baby last year',
 'appreciated please please',
 'would go',
 'urgent appointment',
 'still',
 'see urologist',
 'really slacking',
 'really scared',
 'often come',
 'consultants appointment',
 'worried',
 'time',
 'quite awhile since',
 'professional would',
 'nhs scan',
 'get worse',
 'feel like',
 'bad dream honestly',
 'tests done',
 'say something helpful',
 'ridiculously long',
 'really',
 'passing blood',
 'got',
 'first hospitalised',
 'feel sleepy',
 'feel alone',
 'ct scan',
 'blood thinner',
 'appointment',
 'anyone else experience',
 'would',
 'ultrasound',
 'list',
 'heart failure',
 'scan',
 'national amyloidosis centre',
 'month ago',
 'long',
 'hospital rang today',
 'first',
 'feel',
 'could spread',
 'blood',
 'yes pre op',
 'told us',
 'struggling quite',
 'spleen ive',
 'see heamatologist',
 'quite painful',
 'much worse',
 'metally emotionally draining',
 'lung pleural complication',
 'left side',
 'left flank',
 'keep getting fobbed',
 'im sure',
 'gon na pass',
 'get',
 'even',
 'bank holiday weekend',
 'back',
 'appointments hoping',
 'advanced ovarian cancer',
 '2013 gave birth',
 'varying pains',
 'take ibuprofen',
 'much thought',
 'hope',
 'heart',
 'different cause',
 'could',
 'come',
 'around chest',
 'appointments thank',
 'urologist',
 'urine',
 'untreatable type',
 'took 19',
 'told',
 'specialist says',
 'something wrong',
 'severe hydronephrosis',
 'see',
 'renal department',
 'previous experience',
 'pot

In [0]:
df = sqlContext.sql('''
select t.group, t.text
from `simplified_whole_sentences` as t
where t.access = 1 and t.sentiment = 1 and t.group = 'Anticoagulants'
''')
f = df.select("text").collect()
text = ""
for each in f:
  text += each['text'] + " "
  
# r = Rake(ranking_metric=Metric.DEGREE_TO_FREQUENCY_RATIO)
# r = Rake(ranking_metric=Metric.WORD_DEGREE)
# r = Rake(ranking_metric=Metric.WORD_FREQUENCY)
r = Rake(min_length=1, max_length=4)
r.extract_keywords_from_text(text)
r.get_ranked_phrases()

Out[15]: ['10mg tablets last week',
 'thr next month',
 'requiring ongoing monitoring',
 'originally sent due',
 'long repetitive consultations',
 'like pulling teeth',
 '19 july 2013',
 'gps may feel',
 'cancelled due dvt',
 'trying another one',
 'become available together',
 'rare 10mg',
 'gps pharmacists',
 'dvt clinic',
 'last straw',
 'would suggest',
 'would appreciate',
 'warfarin treatment',
 'tolerating warfarin',
 'terrified something',
 'specialist nature',
 'regular supply',
 'pharmacy refused',
 'lousy itching',
 'insufficient expertise',
 'guys hospital',
 'gp amended',
 'dull pain',
 'began taking',
 'apparent inability',
 'anticoagulants available',
 'accept responsibility',
 '50mg dosage',
 'supplies received',
 'prescribed plavix',
 'last',
 'trying',
 'available',
 'supplies',
 'prescribed',
 'year',
 'wholesalers',
 'wellbeing',
 'ward',
 'use',
 'thousands',
 'take',
 'speak',
 'sit',
 'shortage',
 'seem',
 'requires',
 'requests',
 'reliant',
 'reliable',
 'refuse',
 'professor',
 'product',
 'produce',
 'prescription',
 'phenindione',
 'patients',
 'mydoctorthey',
 'medication',
 'many',
 'least',
 'jeopardising',
 'information',
 'including',
 'health',
 'happen',
 'goldshield',
 'getting',
 'get',
 'generic',
 'fatuigue',
 'doctor',
 'dispense',
 'date',
 'comments',
 'coagulant',
 'chest',
 'change',
 'breath',
 'booked',
 'apparently',
 'anywhere',
 'anti',
 'advice',
 'accordingly']

In [0]:
%sql
select t.group, 
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(*) as trusts_ratio,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(*) as costs_ratio,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(*) as delays_ratio,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(*) as errors_ratio,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(*) as access_ratio,
sum(case when t.trusts = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as negative_trusts_ratio_over_all,
sum(case when t.costs = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as negative_costs_ratio_over_all,
sum(case when t.delays = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as negative_delays_ratio_over_all,
sum(case when t.errors = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as negative_errors_ratio_over_all,
sum(case when t.access = 1 and t.sentiment = 1 then 1 else 0 end)*1.0 / count(*) as negative_access_ratio_over_all
from `whole_posts` as t
group by t.group
order by count(*) DESC

group trusts_ratio costs_ratio delays_ratio errors_ratio access_ratio negative_trusts_ratio_over_all negative_costs_ratio_over_all negative_delays_ratio_over_all negative_errors_ratio_over_all negative_access_ratio_over_all Anxiety_Disorders 0.0483685761331138 0.009240402114568 0.0155234422393622 0.03235765664269 0.0089370829361296 0.0356833347777104 0.0072038304879106 0.0109844873905884 0.0263562700407314 0.0067488517202531 Hip_Replacement 0.0469747677132414 0.0105024439649478 0.0581597604473997 0.0131555770839755 0.0206746223964067 0.0272799330661852 0.0063851336474526 0.02723589766172 0.0096987978334581 0.0111960015852746 Menopause 0.0360331067100207 0.0109813774756134 0.0123115577889447 0.0213715637008572 0.0080697605675436 0.0276529707360331 0.0077150458173219 0.0077150458173219 0.0159769435412356 0.0056310966597694 Polymyalgia_Rheumatica_and_GCA 0.0596331865617307 0.0180633082550359 0.0241133030544673 0.0409631453038866 0.0199355129494158 0.0385882189786083 0.0110425406511112 0.0136428249488611 0.0275283430988455 0.0118226259404362 Knee_Problems 0.0481092981092981 0.0133169299835967 0.0634766468099801 0.0122809289475956 0.0144824311490978 0.0304109470776137 0.008309591642925 0.0340153673487007 0.0091945091945092 0.0081153414486748 Prostate_Problems 0.0739301613442783 0.0486348781554772 0.0349193278608373 0.0400658758137979 0.0273539023699853 0.0469107845912354 0.0270193767530429 0.0185790381101876 0.026478989217982 0.0159028331746481 Citalopram 0.0417792331832446 0.0051575931232092 0.0229226361031519 0.0105880747714559 0.0066311911584118 0.0289807613589849 0.0034929731204803 0.0137262928093874 0.0080229226361032 0.0044207941056079 Depression 0.0557332385690595 0.0102760009476427 0.0142442549158967 0.013651978204217 0.0154288083392561 0.0419924188580905 0.0084695569770197 0.0100390902629709 0.0115197820421701 0.011697465055674 Sertraline 0.0386608036919326 0.0061822456354217 0.0157168357351213 0.0102311811572119 0.0067046889285559 0.0276894945361139 0.0042230832861683 0.0087073882189037 0.0078801863381079 0.0043972310505464 Abdominal_Disorders 0.057976137870084 0.0168360583296509 0.0461776403004861 0.0996464869642068 0.0144498453380468 0.0482545293857711 0.0132125497127707 0.0303579319487406 0.073088820150243 0.010958904109589 Chronic_Fatigue_Syndrome 0.0449634018821889 0.0127470995369218 0.0212119703231589 0.0315689886969078 0.0111537120948066 0.0334611362844197 0.0096599113678235 0.0136433799731116 0.0260419260070707 0.0076183837076134 Genital_Herpes_Simplex 0.0199578778457527 0.0113328653093973 0.0279811453214322 0.061177414502056 0.0074716678367265 0.015143917360345 0.0077725403670645 0.0165981345903119 0.0414201183431953 0.0047638150636847 Gallbladder_Problems 0.0671846918278888 0.015910772808965 0.1096838989322339 0.0583042604926525 0.0358917433132466 0.0534411671424041 0.0125277513479226 0.0693519399513691 0.0438735595728935 0.0270641716883391 Alcohol_Consumption 0.0414659801804794 0.0186015612024581 0.0085810773404196 0.0100204838620384 0.0236394840281238 0.0270165531749986 0.0125671261695178 0.005536178929303 0.0071416708188009 0.0145047887947738 Lichen_Sclerosus 0.0644226482389657 0.0202296032099866 0.0280316540347749 0.0443045028979046 0.0163843067320553 0.0436357556843513 0.0133749442710655 0.0168858671422202 0.0323785109228712 0.0089723584485065 Mirtazapine 0.0658577845184623 0.0109082424313131 0.0144665461121157 0.0156332030566412 0.0137665519454005 0.0482412646561279 0.0074082715977367 0.0091582570145249 0.0124832293064224 0.0092749227089774 Fibromyalgia_Syndrome 0.069500835920707 0.0168975400047767 0.0311679006448531 0.0371984714592787 0.0184499641748268 0.0553498925244805 0.0128970623358013 0.0216742297587772 0.0286601385240029 0.0146286123716265 Sexual_Health 0.0161036673586211 0.0089325029879852 0.0168585267660565 0.0385607347298232 0.0057872554570045 0.0097502673460401 0.0050323960495691 0.0092470277410832 0.0266716990627162 0.0031452475309807 Reflux_Oesophagitis 0.0567937191338483 0.0210839559326326 0

In [0]:
%sql
select t.group, 
count(t.text) as num_posts,
sum(case when t.trusts = 1 then 1 else 0 end)*1.0 / count(t.trusts) as trusts_ratio,
sum(case when t.trusts = 1 and sentiment = 1 then 1 else 0 end)*1.0 / count(t.trusts) as trusts_sentiment_ratio,
sum(case when t.costs = 1 then 1 else 0 end)*1.0 / count(t.costs) as costs_ratio,
sum(case when t.costs = 1 and sentiment = 1 then 1 else 0 end)*1.0 / count(t.costs) as costs_sentiment_ratio,
sum(case when t.delays = 1 then 1 else 0 end)*1.0 / count(t.delays) as delays_ratio,
sum(case when t.delays = 1 and sentiment = 1 then 1 else 0 end)*1.0 / count(t.delays) as delays_sentiment_ratio,
sum(case when t.errors = 1 then 1 else 0 end)*1.0 / count(t.errors) as errors_ratio,
sum(case when t.errors = 1 and sentiment = 1 then 1 else 0 end)*1.0 / count(t.errors) as errors_sentiment_ratio,
sum(case when t.access = 1 then 1 else 0 end)*1.0 / count(t.access) as access_ratio,
sum(case when t.access = 1 and sentiment = 1 then 1 else 0 end)*1.0 / count(t.access) as access_sentiment_ratio
from `whole_posts` as t

WHERE t.group in ('Mastocytosis_and_Mast_Cell_Disorders', 'Cholesteatoma', 'Cataract', 'Lyme_Disease', 'Surgery_and_Anaesthetics')
group by t.group

group num_posts trusts_ratio trusts_sentiment_ratio costs_ratio costs_sentiment_ratio delays_ratio delays_sentiment_ratio errors_ratio errors_sentiment_ratio access_ratio access_sentiment_ratio Cataract 10636 0.0822677698382851 0.0481383978939451 0.0823617901466717 0.0432493418578413 0.081797668296352 0.03412937194434 0.0377021436630312 0.0259496051147048 0.0333772094772471 0.0174877773599097 Surgery_and_Anaesthetics 501 0.1377245508982036 0.1057884231536926 0.0399201596806387 0.0279441117764471 0.063872255489022 0.0439121756487026 0.0279441117764471 0.0239520958083832 0.0738522954091816 0.0479041916167665 Mastocytosis_and_Mast_Cell_Disorders 179 0.1787709497206704 0.1508379888268156 0.0223463687150838 0.0167597765363128 0.1005586592178771 0.0893854748603352 0.1955307262569832 0.1564245810055866 0.0335195530726257 0.0279329608938547 Cholesteatoma 759 0.1001317523056653 0.077733860342556 0.0237154150197628 0.0158102766798419 0.1673254281949934 0.1212121212121212 0.0500658761528327 0.0395256916996047 0.0382081686429513 0.0316205533596838 Lyme_Disease 1348 0.1298219584569733 0.1083086053412463 0.0578635014836795 0.0489614243323442 0.0497032640949555 0.0393175074183976 0.1520771513353116 0.1305637982195846 0.0445103857566766 0.0370919881305638

In [0]:
%sql
select COUNT(*) 
from `whole_posts` as t
WHERE t.group in ('Abdominal_Disorders', 'Cataract', 'Gallbladder_Problems', 'Irritable_Bowel_Syndrome', 'Prostate_Problems')
-- group by t.group

count(1) 105901

In [0]:
%sql

/* Query the created temp table in a SQL cell */

select t.group, count(*) as num_post, sum(case when t.sentiment = 1 then 1 else 0 end)*1.0 / count(t.sentiment) as Negative_Sentiment_Ratio
from `whole_posts` as t
group by t.group
order by Negative_Sentiment_Ratio desc
LIMIT 5

group num_post Negative_Sentiment_Ratio Lumbar_Puncture 283 0.6113074204946995 Complex_Regional_Pain_Syndrome 1312 0.5640243902439024 Topiramate 211 0.5639810426540284 Antibiotics 528 0.5606060606060606 Cervical_Smear_and_Disorders 790 0.5594936708860759

In [0]:
%sql

/* Query the created temp table in a SQL cell */

select t.group, count(*) as num_post, sum(case when t.sentiment = 1  then 1 else 0 end)*1.0 / count(t.sentiment) as Negative_Sentiment_Ratio
from `whole_posts` as t
where t.trusts = 1
group by t.group
order by Negative_Sentiment_Ratio desc

group num_post Negative_Sentiment_Ratio Finger_and_Hand_Problems 7 1.0 Topiramate 19 1.0 Scabies 20 0.95 Pneumothorax 31 0.9354838709677419 Threadworm 57 0.9298245614035088 Weight_Loss_and_Gain_Unintentional 12 0.9166666666666667 Vasectomy 46 0.9130434782608696 Hepatitis 11 0.9090909090909091 Alzheimers_Disease 10 0.9 Pityriasis_Rosea 56 0.8928571428571429 Antibiotics 32 0.875 Infectious_Disease 132 0.8712121212121212 Henoch_Schonlein_Purpura 132 0.8712121212121212 Reactive_Arthritis 54 0.8703703703703703 Cushings_Syndrome 115 0.8695652173913043 Globus_Sensation 76 0.8684210526315789 Chest_Pain 128 0.859375 Bowel_Disorders 133 0.8571428571428571 Pregnancy_and_Genetic_Disorders 41 0.853658536585366 Fungal_and_Yeast_Infections 41 0.853658536585366 Paroxetine_Hydrochloride 34 0.8529411764705882 Complex_Regional_Pain_Syndrome 210 0.8523809523809524 Multiple_Sclerosis 142 0.852112676056338 Olanzapine 100 0.85 Constipation 40 0.85 Cauda_Equina_Syndrome 104 0.8461538461538461 Endometriosis 213 0.8450704225352113 Cervical_Smear_and_Disorders 116 0.8448275862068966 Dental_Abscess 45 0.8444444444444444 Mastocytosis_and_Mast_Cell_Disorders 32 0.84375 Fentanyl 127 0.8425196850393701 Bartholins_Cyst 165 0.8424242424242424 Lumbar_Puncture 19 0.8421052631578947 Sore_Throat 80 0.8375 Orthopaedic_Disorders 67 0.8358208955223881 Lyme_Disease 175 0.8342857142857143 Idiopathic_Intracranial_Hypertension 54 0.8333333333333333 Abdominal_Disorders 1312 0.8323170731707317 Urethral_Disorders 101 0.8316831683168316 Pelvic_Pain_and_Disorders 65 0.8307692307692308 Cystitis 76 0.8289473684210527 Cramps 23 0.8260869565217391 Abscess_Non_dental 63 0.8253968253968254 Bacterial_Vaginosis 166 0.825301204819277 Haemorrhoids 326 0.8251533742331288 Gilberts_Syndrome 51 0.823529411764706 Gabapentin 401 0.8229426433915212 Testicular_Pain_and_Disorders 67 0.8208955223880597 Neurological_Disorders 295 0.8203389830508475 Hidradenitis_Suppurativa 272 0.8198529411764706 Codeine_and_Paracetamol_Co_codamol 165 0.8181818181818182 Nail_Disorders 11 0.8181818181818182 Adrenal_Disorders 142 0.8169014084507042 Sex_Chromosome_Aneuploidies 54 0.8148148148148148 Frozen_Shoulder 448 0.8147321428571429 Menstrual_Cycle_and_Disorders 64 0.8125 Spinal_Problems 720 0.8125 Levothyroxine_Sodium 149 0.8120805369127517 Statins_and_Other_Lipid_lowering_Medicines 249 0.8112449799196787 Substance_Misuse 90 0.8111111111111111 Osteomyelitis 95 0.8105263157894737 Proton_Pump_Inhibitors 147 0.8095238095238095 Disc_Prolapse 508 0.8090551181102362 Urinary_Tract_Infection 292 0.8082191780821918 Coeliac_Disease 104 0.8076923076923077 Dietary_Nutrition_and_Exercise_Advice 114 0.8070175438596491 Backache 305 0.8065573770491803 Duodenal_Ulcer 62 0.8064516129032258 Deep_Vein_Thrombosis 72 0.8055555555555556 Anal_Fissure_and_Proctalgia 267 0.8052434456928839 Shingles 589 0.8047538200339559 Infectious_Mononucleosis 301 0.8039867109634551 Sweating 51 0.803921568627451 Kidney_Stones 151 0.8013245033112583 Warts_And_Verrucas 5 0.8 Rhinitis 40 0.8 Dementia 45 0.8 Autoimmune_Disorders 145 0.8 ACE_Inhibitors 15 0.8 Venlafaxine 607 0.7990115321252059 Pain_and_Pain_Relief 184 0.7989130434782609 Hypothyroidism 903 0.7984496124031008 Nasal_Problems 79 0.7974683544303797 Headache 261 0.7969348659003831 Neck_Pain 59 0.7966101694915254 Fibromyalgia_Syndrome 1164 0.7963917525773196 Pancreatitis_and_Pancreatic_Disorders 377 0.7957559681697614 Cardiac_Arrhythmias 186 0.7956989247311828 Gallbladder_Problems 1271 0.7954366640440598 Sarcoidosis 393 0.7938931297709924 Beta_blockers_others 97 0.7938144329896907 Vulval_Problems 92 0.7934782608695652 Investigations_and_Procedures 29 0.7931034482758621 Eustachian_Tube_Dysfunction 255 0.792156862745098 Arthroscopy 48 0.7916666666666667 Chiari_Malformation 325 0.7907692307692308 Sleep_Problems 328 0.7896341463414634 Raynauds_Phenomenon 19 0.7894736842105263 Palsy_Non_Cerebral 19 0.7894736842105263 Fluoroquinolone_Antibiotics 104 0.7884615384615385 Opiates_And_Opioids 178 0.786516853

In [0]:
%sql

/* Query the created temp table in a SQL cell */

select t.group, count(*) as num_post, sum(case when t.sentiment = 1  then 1 else 0 end)*1.0 / count(t.sentiment) as Negative_Sentiment_Ratio
from `whole_posts` as t
where t.costs = 1
group by t.group
order by Negative_Sentiment_Ratio desc

group num_post Negative_Sentiment_Ratio Wegeners_Granulomatosis 8 1.0 Reactive_Arthritis 16 1.0 Oesophageal_Cancer 1 1.0 Abscess_Non_dental 8 1.0 ACE_Inhibitors 1 1.0 Finger_and_Hand_Problems 1 1.0 PTSD_Post_Traumatic_Stress_Disorder 8 1.0 Lumbar_Puncture 4 1.0 Complex_Regional_Pain_Syndrome 58 0.9482758620689655 Bowel_Disorders 31 0.9354838709677419 Vasculitis 15 0.9333333333333333 Fentanyl 29 0.9310344827586207 Osteomyelitis 14 0.9285714285714286 Coeliac_Disease 38 0.9210526315789473 Pilonidal_Sinus 12 0.9166666666666667 Escitalopram 11 0.9090909090909091 Sore_Throat 22 0.9090909090909091 Neck_Pain 20 0.9 Kidney_Problems 20 0.9 Henoch_Schonlein_Purpura 10 0.9 Tramadol 38 0.8947368421052632 Vasectomy 27 0.888888888888889 Urinary_Incontinence 33 0.8787878787878788 Cellulitis 16 0.875 Scabies 29 0.8620689655172414 Elbow_Problems 7 0.8571428571428571 Opiates_And_Opioids 70 0.8571428571428571 Cervical_Smear_and_Disorders 61 0.8524590163934426 Sarcoidosis 54 0.8518518518518519 Muscle_Disorders 20 0.85 Lyme_Disease 78 0.8461538461538461 Cushings_Syndrome 13 0.8461538461538461 Sciatica 83 0.8433734939759036 Autonomic_Dysfunction 19 0.8421052631578947 Dental_Abscess 25 0.84 Orthopaedic_Disorders 18 0.8333333333333333 Nasal_Problems 48 0.8333333333333333 Multiple_Sclerosis 42 0.8333333333333333 Pityriasis_Rosea 36 0.8333333333333333 Gabapentin 71 0.8309859154929577 Neurological_Disorders 65 0.8307692307692308 Dermatitis_And_Eczema 46 0.8260869565217391 Chatroom 115 0.8260869565217391 Depression 347 0.824207492795389 Infectious_Mononucleosis 51 0.823529411764706 Disc_Prolapse 221 0.823529411764706 Backache 116 0.8189655172413793 Chest_Pain 22 0.8181818181818182 Beta_blockers_others 11 0.8181818181818182 Arthroscopy 11 0.8181818181818182 Cauda_Equina_Syndrome 22 0.8181818181818182 Benzodiazepines_and_Z_Drugs 136 0.8161764705882353 Fluoxetine 76 0.8157894736842105 Vertigo_and_Dizziness 222 0.8153153153153153 Spinal_Problems 261 0.8084291187739464 Proton_Pump_Inhibitors 62 0.8064516129032258 Kidney_Stones 41 0.8048780487804879 Gilberts_Syndrome 5 0.8 Threadworm 35 0.8 Pneumothorax 5 0.8 Haemorrhoids 89 0.797752808988764 Venlafaxine 132 0.7954545454545455 Bisoprolol 34 0.7941176470588235 Pregnancy_and_Genetic_Disorders 19 0.7894736842105263 Movement_Disorders 19 0.7894736842105263 Thyroid_and_Parathyroid_Disorders 85 0.7882352941176471 Substance_Misuse 33 0.7878787878787878 Neuropathic_Pain 80 0.7875 Gallbladder_Problems 301 0.787375415282392 Other_Conditions_and_General_Health 61 0.7868852459016393 Anaemia 28 0.7857142857142857 Abdominal_Disorders 381 0.7847769028871391 Ear_Problems 65 0.7846153846153846 Pain_and_Pain_Relief 74 0.7837837837837838 Hip_Dysplasia_and_Disorders 23 0.782608695652174 Urinary_Tract_Infection 78 0.782051282051282 Mental_Health 78 0.782051282051282 Pregabalin 41 0.7804878048780488 Anxiety_Disorders 853 0.779601406799531 Sleep_Problems 77 0.7792207792207791 Fluoroquinolone_Antibiotics 18 0.7777777777777778 Cystitis 36 0.7777777777777778 Dementia 9 0.7777777777777778 Topiramate 9 0.7777777777777778 Epilepsy_and_Non_epileptic_seizures 36 0.7777777777777778 Angiotensin_II_Receptor_Blockers 18 0.7777777777777778 Folliculitis 9 0.7777777777777778 Contraception 9 0.7777777777777778 Sjogrens_Syndrome 103 0.7766990291262136 Oesophageal_Achalasia_and_Spasm 58 0.7758620689655172 Autoimmune_Disorders 31 0.7741935483870968 Urethral_Disorders 31 0.7741935483870968 Cancer 53 0.7735849056603774 Cardiac_Arrhythmias 35 0.7714285714285714 Eustachian_Tube_Dysfunction 144 0.7708333333333333 Pancreatitis_and_Pancreatic_Disorders 113 0.7699115044247788 Plantar_Fasciitis 73 0.767123287671233 Sweating 30 0.7666666666666667 Bartholins_Cyst 47 0.7659574468085106 Testicular_Pain_and_Disorders 17 0.7647058823529412 Ankylosing_Spondylitis 51 0.7647058823529412 Globus_Sensation 17 0.7647058823529412 Fibromyalgia_Syndrome 283 0.7632508833922261 Shoulder_Problems 100 0.76 Endometriosis 54 0.7592592592592593 Infectious_Disease 58 0.758620689655172

In [0]:
%sql

/* Query the created temp table in a SQL cell */

select t.group, count(*) as num_post, sum(case when t.sentiment = 1  then 1 else 0 end)*1.0 / count(t.sentiment) as Negative_Sentiment_Ratio
from `whole_posts` as t
where t.delays = 1
group by t.group
order by Negative_Sentiment_Ratio desc

group num_post Negative_Sentiment_Ratio Pruritus_Ani 1 1.0 Topiramate 3 1.0 Alopecia_and_Hair_Disorders 4 1.0 Mastocytosis_and_Mast_Cell_Disorders 18 0.888888888888889 Dihydrocodeine 9 0.888888888888889 Acne 8 0.875 Beta_blockers_others 8 0.875 Salivary_Gland_Disorders 37 0.8648648648648649 Sweating 7 0.8571428571428571 Rhinitis 14 0.8571428571428571 Postherpetic_Neuralgia 43 0.8372093023255814 Wolff_Parkinson_White_Syndrome 6 0.8333333333333333 Lumbar_Puncture 12 0.8333333333333333 Eating_Disorders 18 0.8333333333333333 Complex_Regional_Pain_Syndrome 63 0.8253968253968254 Scabies 11 0.8181818181818182 Opiates_And_Opioids 48 0.8125 Allergic_Disorders 26 0.8076923076923077 Reactive_Arthritis 20 0.8 Henoch_Schonlein_Purpura 44 0.7954545454545455 Idiopathic_Intracranial_Hypertension 29 0.7931034482758621 Lyme_Disease 67 0.791044776119403 Benzodiazepines_and_Z_Drugs 61 0.7868852459016393 Levothyroxine_Sodium 45 0.7777777777777778 Steroids 18 0.7777777777777778 Antibiotics 27 0.7777777777777778 Pneumothorax 49 0.7755102040816327 Infectious_Disease 43 0.7674418604651163 Pelvic_Pain_and_Disorders 34 0.7647058823529412 Osteomyelitis 42 0.7619047619047619 Mental_Health 117 0.7606837606837606 Pregnancy_and_Genetic_Disorders 16 0.75 Weight_Loss_and_Gain_Unintentional 4 0.75 Duloxetine 4 0.75 Pregabalin 16 0.75 Anal_Fissure_and_Proctalgia 232 0.7456896551724138 Chest_Pain 51 0.7450980392156863 Statins_and_Other_Lipid_lowering_Medicines 43 0.7441860465116279 Fentanyl 31 0.7419354838709677 Sinusitis 112 0.7410714285714286 Frozen_Shoulder 412 0.7402912621359223 PTSD_Post_Traumatic_Stress_Disorder 23 0.7391304347826086 Haemorrhoids 449 0.7371937639198218 Endometriosis 162 0.7345679012345679 Lymphadenopathy 45 0.7333333333333333 Contraception 15 0.7333333333333333 Pernicious_Anaemia 138 0.7318840579710145 Codeine_and_Paracetamol_Co_codamol 41 0.7317073170731707 Neck_Pain 26 0.7307692307692308 Constipation 26 0.7307692307692308 Cauda_Equina_Syndrome 89 0.7303370786516854 Blepharitis 37 0.7297297297297297 Sleep_Problems 74 0.7297297297297297 Oral_and_Dental_Problems 118 0.728813559322034 Bartholins_Cyst 136 0.7279411764705882 Threadworm 11 0.7272727272727273 Methotrexate 22 0.7272727272727273 Bacterial_Vaginosis 44 0.7272727272727273 Psoriasis_and_Psoriatic_Arthritis 95 0.7263157894736842 Pain_and_Pain_Relief 80 0.725 Cervical_Smear_and_Disorders 40 0.725 Cholesteatoma 127 0.7244094488188976 Dental_Abscess 32 0.71875 Nail_Disorders 7 0.7142857142857143 Cellulitis 21 0.7142857142857143 Eustachian_Tube_Dysfunction 100 0.71 Sarcoidosis 175 0.7085714285714286 Shingles 199 0.7085427135678392 Cystitis 48 0.7083333333333333 Respiratory_Symptoms_and_Disorders 65 0.7076923076923077 Anxiety_Disorders 1433 0.7076064200976971 Sjogrens_Syndrome 129 0.7054263565891473 Depression 481 0.7047817047817048 Multiple_Sclerosis 132 0.7045454545454545 Urethral_Disorders 81 0.7037037037037037 Lupus 74 0.7027027027027027 Proton_Pump_Inhibitors 40 0.7 Migraine 140 0.7 Spinal_Problems 478 0.698744769874477 Chatroom 53 0.6981132075471698 Urinary_Tract_Infection 96 0.6979166666666667 Amitriptyline 33 0.696969696969697 Fibromyalgia_Syndrome 522 0.6954022988505747 Cushings_Syndrome 105 0.6952380952380952 Ulcerative_Colitis 169 0.6923076923076923 Vasculitis 29 0.6896551724137931 Bowel_Disorders 106 0.6886792452830189 Urticarial_Rash 61 0.6885245901639344 Surgery_and_Anaesthetics 32 0.6875 Fungal_and_Yeast_Infections 16 0.6875 Adrenal_Disorders 83 0.6867469879518072 Duodenal_Ulcer 83 0.6867469879518072 Globus_Sensation 51 0.6862745098039216 Disc_Prolapse 649 0.6856702619414484 Hidradenitis_Suppurativa 108 0.6851851851851852 Irritable_Bowel_Syndrome 381 0.6850393700787402 Vertigo_and_Dizziness 621 0.6811594202898551 Sore_Throat 77 0.6753246753246753 Abscess_Non_dental 83 0.674698795180723 Atrophic_Vaginitis 100 0.67 Venlafaxine 136 0.6691176470588235 Paroxetine_Hydrochloride 9 0.6666666666666667 Folliculitis 3 0.6666666666666667 Spleen_Disorders_and_Splenectomy 9 0.6666666666666

In [0]:
%sql

/* Query the created temp table in a SQL cell */

select t.group, count(*) as num_post, sum(case when t.sentiment = 1  then 1 else 0 end)*1.0 / count(t.sentiment) as Negative_Sentiment_Ratio
from `whole_posts` as t
where t.errors = 1
group by t.group
order by Negative_Sentiment_Ratio desc

group num_post Negative_Sentiment_Ratio Quetiapine 11 1.0 Smoking 4 1.0 Paroxetine_Hydrochloride 8 1.0 PTSD_Post_Traumatic_Stress_Disorder 18 1.0 Scabies 26 0.9615384615384615 Opiates_And_Opioids 35 0.942857142857143 Fentanyl 23 0.9130434782608696 Anal_Fissure_and_Proctalgia 103 0.912621359223301 Henoch_Schonlein_Purpura 100 0.91 Abscess_Non_dental 32 0.90625 Appendicitis 21 0.9047619047619048 Scoliosis_and_Kyphosis 21 0.9047619047619048 Tramadol 81 0.9012345679012346 Dihydrocodeine 10 0.9 Osteomyelitis 60 0.9 Varicose_Vein 10 0.9 Gabapentin 184 0.891304347826087 Spleen_Disorders_and_Splenectomy 9 0.888888888888889 Threadworm 34 0.8823529411764706 Idiopathic_Intracranial_Hypertension 49 0.8775510204081634 Pilonidal_Sinus 8 0.875 Dental_Abscess 8 0.875 Urinary_Incontinence 55 0.8727272727272727 Lyme_Disease 205 0.8585365853658538 Pregnancy_and_Genetic_Disorders 49 0.8571428571428571 Surgery_and_Anaesthetics 14 0.8571428571428571 Mental_Health 167 0.8562874251497006 Pityriasis_Rosea 97 0.8556701030927835 Benzodiazepines_and_Z_Drugs 123 0.853658536585366 Frozen_Shoulder 149 0.8523489932885906 Bipolar_Affective_Disorder 88 0.8522727272727273 Gilberts_Syndrome 53 0.8490566037735849 Pelvic_Pain_and_Disorders 66 0.8484848484848485 Bartholins_Cyst 33 0.8484848484848485 Pruritus_Ani 13 0.8461538461538461 Vasectomy 39 0.8461538461538461 Depression 461 0.8438177874186551 Haemorrhoids 102 0.8431372549019608 Tinnitus 44 0.8409090909090909 Infectious_Mononucleosis 293 0.8395904436860068 Shingles 329 0.8389057750759878 Chiari_Malformation 167 0.8383233532934132 Hemifacial_Spasm 43 0.8372093023255814 Disc_Prolapse 165 0.8363636363636364 Endometriosis 169 0.8343195266272189 ACE_Inhibitors 12 0.8333333333333333 Arthroscopy 12 0.8333333333333333 Topiramate 12 0.8333333333333333 Venlafaxine 176 0.8295454545454545 Menstrual_Cycle_and_Disorders 82 0.8292682926829268 Psoriasis_and_Psoriatic_Arthritis 93 0.8279569892473118 Dementia 29 0.8275862068965517 Orlistat 23 0.8260869565217391 Beta_blockers_others 40 0.825 Chronic_Fatigue_Syndrome 634 0.8249211356466877 Cauda_Equina_Syndrome 73 0.8219178082191781 Postherpetic_Neuralgia 56 0.8214285714285714 Salivary_Gland_Disorders 33 0.8181818181818182 Chest_Pain 197 0.817258883248731 Anxiety_Disorders 2987 0.8145296283896887 Escitalopram 43 0.813953488372093 Backache 150 0.8133333333333334 Rhinitis 32 0.8125 Fluoroquinolone_Antibiotics 79 0.810126582278481 Cervical_Smear_and_Disorders 100 0.81 Pregabalin 42 0.8095238095238095 Cervical_Spondylosis 152 0.8092105263157895 Spinal_Problems 309 0.8090614886731392 Pernicious_Anaemia 219 0.8082191780821918 Cellulitis 36 0.8055555555555556 Fluoxetine 108 0.8055555555555556 Reactive_Arthritis 82 0.8048780487804879 Costochondritis_and_Tietzes_Syndrome 189 0.8042328042328042 Foot_and_Toe_Problems 117 0.8034188034188035 Bacterial_Vaginosis 161 0.8012422360248447 Rosacea 15 0.8 Vulval_Problems 135 0.8 Pneumothorax 30 0.8 Eating_Disorders 10 0.8 Contraception 15 0.8 Mastocytosis_and_Mast_Cell_Disorders 35 0.8 Statins_and_Other_Lipid_lowering_Medicines 115 0.8 Oesophageal_Cancer 20 0.8 Methotrexate 50 0.8 Proton_Pump_Inhibitors 130 0.8 Weight_Loss_Intentional 10 0.8 Plantar_Fasciitis 35 0.8 Mirtazapine 268 0.7985074626865672 Genitourinary_Prolapse 191 0.7958115183246073 Hidradenitis_Suppurativa 137 0.7956204379562044 Levothyroxine_Sodium 73 0.7945205479452055 Hip_Dysplasia_and_Disorders 96 0.7916666666666667 Tendon_Problems 81 0.7901234567901235 Hydrocele 19 0.7894736842105263 Cholesteatoma 38 0.7894736842105263 Cushings_Syndrome 90 0.7888888888888889 Benefits_and_Allowances 99 0.7878787878787878 Coagulation_Disorders 33 0.7878787878787878 Complex_Regional_Pain_Syndrome 108 0.787037037037037 Hernia 266 0.7857142857142857 Lumbar_Puncture 14 0.7857142857142857 Infectious_Disease 102 0.7843137254901961 Amlodipine 175 0.7828571428571429 Acne 9 0.7777777777777778 Nail_Disorders 18 0.7777777777777778 Cystitis 81 0.7777777777777778 Movement_Disorders 58 0.7758620689655172 Olanzapi

In [0]:
%sql

/* Query the created temp table in a SQL cell */

select t.group, count(*) as num_post, sum(case when t.sentiment = 1  then 1 else 0 end)*1.0 / count(t.sentiment) as Negative_Sentiment_Ratio
from `whole_posts` as t
where t.access = 1
group by t.group
order by Negative_Sentiment_Ratio desc

group num_post Negative_Sentiment_Ratio Dihydrocodeine 7 1.0 Quetiapine 5 1.0 Pelvic_Pain_and_Disorders 10 1.0 Smoking 2 1.0 Trazodone 2 1.0 Cramps 5 1.0 Lymphadenopathy 3 1.0 Pneumothorax 10 1.0 Herpes_Non_Genital 3 1.0 Globus_Sensation 11 1.0 Paroxetine_Hydrochloride 6 1.0 Dementia 16 1.0 Folliculitis 3 1.0 Finger_and_Hand_Problems 2 1.0 Osteomyelitis 19 0.9473684210526316 Olanzapine 27 0.9259259259259259 Lumbar_Puncture 12 0.9166666666666667 Cystitis 24 0.9166666666666667 Antibiotics 11 0.9090909090909091 Elbow_Problems 10 0.9 Scabies 10 0.9 Codeine_and_Paracetamol_Co_codamol 72 0.888888888888889 Idiopathic_Intracranial_Hypertension 17 0.8823529411764706 Fentanyl 25 0.88 Duloxetine 8 0.875 Opiates_And_Opioids 76 0.8684210526315789 Hydrocele 15 0.8666666666666667 Complex_Regional_Pain_Syndrome 41 0.853658536585366 Beta_blockers_others 13 0.8461538461538461 Gabapentin 58 0.8448275862068966 Pregnancy_and_Genetic_Disorders 25 0.84 Mastocytosis_and_Mast_Cell_Disorders 6 0.8333333333333333 Topiramate 6 0.8333333333333333 Lyme_Disease 60 0.8333333333333333 Henoch_Schonlein_Purpura 35 0.8285714285714286 Cholesteatoma 29 0.8275862068965517 Chest_Pain 23 0.8260869565217391 Cystoscopy 28 0.8214285714285714 Venlafaxine 106 0.8207547169811321 Dental_Abscess 11 0.8181818181818182 Spinal_Problems 209 0.8181818181818182 Reactive_Arthritis 11 0.8181818181818182 Alopecia_and_Hair_Disorders 11 0.8181818181818182 Urethral_Disorders 44 0.8181818181818182 Pregabalin 22 0.8181818181818182 Multiple_Sclerosis 38 0.8157894736842105 Hidradenitis_Suppurativa 74 0.8108108108108107 Shoulder_Problems 58 0.8103448275862069 Duodenal_Ulcer 21 0.8095238095238095 Hip_Dysplasia_and_Disorders 42 0.8095238095238095 Sore_Throat 21 0.8095238095238095 Upper_Gastrointestinal_Endoscopy 62 0.8064516129032258 Neuropathic_Pain 67 0.8059701492537313 Bartholins_Cyst 56 0.8035714285714286 Vasectomy 15 0.8 Alzheimers_Disease 5 0.8 Breast_Cancer_and_Screening 10 0.8 Carbimazole 15 0.8 Cushings_Syndrome 25 0.8 PTSD_Post_Traumatic_Stress_Disorder 25 0.8 Stroke_and_TIA 49 0.7959183673469388 Disc_Prolapse 258 0.7945736434108527 Amitriptyline 34 0.7941176470588235 Fibromyalgia_Syndrome 309 0.7928802588996764 Sarcoidosis 96 0.7916666666666667 Benzodiazepines_and_Z_Drugs 144 0.7916666666666667 Cardiac_Arrhythmias 48 0.7916666666666667 Polycystic_Ovary_Syndrome 19 0.7894736842105263 Cervical_Spondylosis 126 0.7857142857142857 Barretts_Oesophagus 23 0.782608695652174 Kidney_Problems 46 0.782608695652174 Endometriosis 55 0.7818181818181817 Threadworm 18 0.7777777777777778 Cervical_Smear_and_Disorders 62 0.7741935483870968 Pancreatitis_and_Pancreatic_Disorders 93 0.7741935483870968 Infectious_Mononucleosis 44 0.7727272727272727 Abscess_Non_dental 22 0.7727272727272727 Coeliac_Disease 35 0.7714285714285714 Neck_Pain 13 0.7692307692307692 Urinary_Symptoms_and_Problems 52 0.7692307692307692 Steroids 13 0.7692307692307692 Anal_Fissure_and_Proctalgia 99 0.7676767676767677 Tramadol 43 0.7674418604651163 Bipolar_Affective_Disorder 47 0.7659574468085106 Propranolol 17 0.7647058823529412 Cellulitis 21 0.7619047619047619 Rhinitis 25 0.76 Sciatica 75 0.76 Abdominal_Disorders 327 0.7584097859327217 Depression 521 0.7581573896353166 Chiari_Malformation 82 0.7560975609756098 Anxiety_Disorders 825 0.7551515151515152 Pain_and_Pain_Relief 57 0.7543859649122807 Gallbladder_Problems 679 0.7540500736377025 Backache 93 0.7526881720430108 Mental_Health 133 0.7518796992481203 Fluoroquinolone_Antibiotics 16 0.75 Wolff_Parkinson_White_Syndrome 4 0.75 Levothyroxine_Sodium 44 0.75 Autoimmune_Disorders 24 0.75 Ramipril 12 0.75 Investigations_and_Procedures 12 0.75 Coagulation_Disorders 8 0.75 Statins_and_Other_Lipid_lowering_Medicines 94 0.7446808510638298 Urinary_Incontinence 47 0.7446808510638298 Hernia 156 0.7435897435897436 Psoriasis_and_Psoriatic_Arthritis 70 0.7428571428571429 Cauda_Equina_Syndrome 35 0.7428571428571429 Substance_Misuse 31 0.7419354838709677 Plantar_Fasciitis 27 0.7407407407407407 Bacterial

In [0]:
# With this registered as a temp view, it will only be available to this particular notebook. If you'd like other users to be able to query this table, you can also create a table from the DataFrame.
# Once saved, this table will persist across cluster restarts as well as allow various users across different notebooks to query this data.
# To do so, choose your table name and uncomment the bottom line.

permanent_table_name = "whole_corpus_sentence_merged_top_10_tiny_tsne_csv"

# df.write.format("parquet").saveAsTable(permanent_table_name)